In [1]:
{
 "cells": [
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "## acquire\n",
    "\n",
    "Goal: Predict the logerror\n",
    "\n",
    "Zillow data:\n",
    "- 2017 data\n",
    "- Latest transaction per property id only.\n",
    "- The logerror from that latest transaction.\n",
    "- All fields related to the properties.\n",
    "- Gather descriptions from the lookup tables.\n",
    "- Only properties with latitude and longitude.\n",
    "- Only single family homes."
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 4,
   "metadata": {},
   "outputs": [],
   "source": [
    "import pandas as pd\n",
    "import numpy as np\n",
    "from sklearn.model_selection import train_test_split\n",
    "from sklearn.preprocessing import PowerTransformer, LabelEncoder, OneHotEncoder, QuantileTransformer, MinMaxScaler\n",
    "from sklearn.cluster import KMeans\n",
    "import matplotlib.pyplot as plt\n",
    "import seaborn as sns\n",
    "%matplotlib inline\n",
    "from mpl_toolkits.mplot3d import Axes3D\n",
    "import warnings\n",
    "warnings.filterwarnings(\"ignore\")\n",
    "\n",
    "import acquire\n",
    "import summarize\n",
    "import prepare"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 7,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "<class 'pandas.core.frame.DataFrame'>\n",
      "RangeIndex: 85224 entries, 0 to 85223\n",
      "Data columns (total 60 columns):\n",
      "id                              85224 non-null int64\n",
      "parcelid                        85224 non-null int64\n",
      "airconditioningtypeid           28311 non-null float64\n",
      "architecturalstyletypeid        261 non-null float64\n",
      "basementsqft                    42 non-null float64\n",
      "bathroomcnt                     85224 non-null float64\n",
      "bedroomcnt                      85224 non-null float64\n",
      "buildingclasstypeid             0 non-null object\n",
      "buildingqualitytypeid           53810 non-null float64\n",
      "calculatedbathnbr               85207 non-null float64\n",
      "decktypeid                      654 non-null float64\n",
      "finishedfloor1squarefeet        6821 non-null float64\n",
      "calculatedfinishedsquarefeet    85224 non-null float64\n",
      "finishedsquarefeet12            85035 non-null float64\n",
      "finishedsquarefeet13            2 non-null float64\n",
      "finishedsquarefeet15            29 non-null float64\n",
      "finishedsquarefeet50            6821 non-null float64\n",
      "finishedsquarefeet6             158 non-null float64\n",
      "fips                            85224 non-null float64\n",
      "fireplacecnt                    9551 non-null float64\n",
      "fullbathcnt                     85207 non-null float64\n",
      "garagecarcnt                    29680 non-null float64\n",
      "garagetotalsqft                 29680 non-null float64\n",
      "hashottuborspa                  2358 non-null float64\n",
      "heatingorsystemtypeid           55685 non-null float64\n",
      "latitude                        85224 non-null float64\n",
      "longitude                       85224 non-null float64\n",
      "lotsizesquarefeet               75486 non-null float64\n",
      "poolcnt                         17726 non-null float64\n",
      "poolsizesum                     964 non-null float64\n",
      "pooltypeid10                    1154 non-null float64\n",
      "pooltypeid2                     1204 non-null float64\n",
      "pooltypeid7                     16522 non-null float64\n",
      "propertycountylandusecode       85224 non-null object\n",
      "propertylandusetypeid           85224 non-null float64\n",
      "propertyzoningdesc              54068 non-null object\n",
      "rawcensustractandblock          85224 non-null float64\n",
      "regionidcity                    83552 non-null float64\n",
      "regionidcounty                  85224 non-null float64\n",
      "regionidneighborhood            33262 non-null float64\n",
      "regionidzip                     85209 non-null float64\n",
      "roomcnt                         85224 non-null float64\n",
      "storytypeid                     42 non-null float64\n",
      "threequarterbathnbr             12007 non-null float64\n",
      "typeconstructiontypeid          299 non-null float64\n",
      "unitcnt                         54142 non-null float64\n",
      "yardbuildingsqft17              2635 non-null float64\n",
      "yardbuildingsqft26              93 non-null float64\n",
      "yearbuilt                       85186 non-null float64\n",
      "numberofstories                 20264 non-null float64\n",
      "fireplaceflag                   222 non-null float64\n",
      "structuretaxvaluedollarcnt      85162 non-null float64\n",
      "taxvaluedollarcnt               85223 non-null float64\n",
      "assessmentyear                  85224 non-null float64\n",
      "landtaxvaluedollarcnt           85223 non-null float64\n",
      "taxamount                       85219 non-null float64\n",
      "taxdelinquencyflag              1614 non-null object\n",
      "taxdelinquencyyear              1614 non-null float64\n",
      "censustractandblock             84996 non-null float64\n",
      "logerror                        85224 non-null float64\n",
      "dtypes: float64(54), int64(2), object(4)\n",
      "memory usage: 39.0+ MB\n"
     ]
    }
   ],
   "source": [
    "df = acquire.get_zillow_data()\n",
    "df.info()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Only single family"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 8,
   "metadata": {},
   "outputs": [],
   "source": [
    "df = df[df.propertylandusetypeid == 261]"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "## prepare \n",
    "\n",
    "### Missing Values"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "- remove columns with > 99% missing and rows  > 40% missing\n",
    "- aggregate pool information: use all pool and spa columns to compute a single boolean attribute of `has_pool`\n",
    "- fill with 0: taxdelinquencyflag, fireplacecnt, garagecarcnt and convert them to boolean\n",
    "- After doing all that, then remove all columns with > 5% missing, and following that, rows with > 99% missing"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 13,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "<class 'pandas.core.frame.DataFrame'>\n",
      "Int64Index: 58419 entries, 0 to 85221\n",
      "Data columns (total 31 columns):\n",
      "id                              58419 non-null int64\n",
      "parcelid                        58419 non-null int64\n",
      "bathroomcnt                     58419 non-null float64\n",
      "bedroomcnt                      58419 non-null float64\n",
      "calculatedbathnbr               58419 non-null float64\n",
      "calculatedfinishedsquarefeet    58419 non-null float64\n",
      "finishedsquarefeet12            58419 non-null float64\n",
      "fips                            58419 non-null float64\n",
      "fullbathcnt                     58419 non-null float64\n",
      "latitude                        58419 non-null float64\n",
      "longitude                       58419 non-null float64\n",
      "lotsizesquarefeet               58419 non-null float64\n",
      "propertycountylandusecode       58419 non-null object\n",
      "propertylandusetypeid           58419 non-null float64\n",
      "rawcensustractandblock          58419 non-null float64\n",
      "regionidcity                    58419 non-null float64\n",
      "regionidcounty                  58419 non-null float64\n",
      "regionidzip                     58419 non-null float64\n",
      "roomcnt                         58419 non-null float64\n",
      "yearbuilt                       58419 non-null float64\n",
      "structuretaxvaluedollarcnt      58419 non-null float64\n",
      "taxvaluedollarcnt               58419 non-null float64\n",
      "assessmentyear                  58419 non-null float64\n",
      "landtaxvaluedollarcnt           58419 non-null float64\n",
      "taxamount                       58419 non-null float64\n",
      "censustractandblock             58419 non-null float64\n",
      "logerror                        58419 non-null float64\n",
      "has_pool                        58419 non-null float64\n",
      "is_taxdelinquent                58419 non-null float64\n",
      "has_fireplace                   58419 non-null float64\n",
      "has_garage                      58419 non-null float64\n",
      "dtypes: float64(28), int64(2), object(1)\n",
      "memory usage: 14.3+ MB\n"
     ]
    }
   ],
   "source": [
    "# remove columns with > 99% missing and rows  > 40% missing\n",
    "df = prepare.handle_missing_values(df, prop_required_column = .01, prop_required_row = .40)\n",
    "df.info()"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 17,
   "metadata": {},
   "outputs": [],
   "source": [
    "# aggregate pool information: use all pool and spa columns to compute a single attribute of pool_spa\n",
    "# # gather pool columns\n",
    "# pool_cols = ['hashottuborspa', 'poolcnt', 'poolsizesum', 'pooltypeid2', 'pooltypeid7']\n",
    "# # fill all missing values with 0\n",
    "# pool = df[pool_cols].fillna(0)\n",
    "# # where there is a value in one or more of the pool attributes, assign a 1 to a new col named 'pool'\n",
    "# pool.loc[pool.sum(axis=1)>0, 'has_pool'] = 1\n",
    "# # append the new column to our original dataframe and remove the original pool columns \n",
    "# df = df.join(pool[['has_pool']])\n",
    "\n",
    "# fill with 0\n",
    "#df.loc[df.taxdelinquencyflag == 'Y', 'is_taxdelinquent'] = 1\n",
    "#df.loc[df.fireplacecnt > 0, 'has_fireplace'] = 1\n",
    "#df.loc[df.garagecarcnt > 0, 'has_garage'] = 1\n",
    "fill_with_0 = ['has_garage', 'has_fireplace', 'has_pool', 'is_taxdelinquent']\n",
    "df[fill_with_0] = df[fill_with_0].fillna(0)\n",
    "\n",
    "# remove columns where > 5% missing and rows where > 99% missing\n",
    "df = prepare.handle_missing_values(df, prop_required_column = .95, prop_required_row = .99)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### Variable Changes\n",
    "\n",
    "Are there any instances where taxvaluedollarcnt is not equal to the sum of the land tax value and the structure tax value? (landtaxvaluedollarcnt + structuretaxvaluedollarcnt). "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 18,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "(array([], dtype=int64),)"
      ]
     },
     "execution_count": 18,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "np.where((df.taxvaluedollarcnt - (df.landtaxvaluedollarcnt + df.structuretaxvaluedollarcnt)) != 0)\n",
    "# add taxvaluedollarcnt to list to drop"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "No. I will attempt to reduce the dependency between variables and extracting the most unique information from each. \n",
    "\n",
    "- `land_dollar_per_sqft`: a land dollar per sqft (landtaxvaluedollarcnt/lotsizesquarefeet)\n",
    "- `structure_dollar_per_sqft`: structuretaxvaluedollarcnt/calculatedfinishedsquarefeet\n",
    "- `tax_rate`: taxvaluedollarcnt/taxamount\n",
    "- compute `living_area_sqft` by subtracting estimated square feet from bedrooms (121: 11x11) and bathrooms (36: 6x6)\n",
    "- compute `bedbath_index` where multiple bedrooms by a weight of 2, full baths by weight of 1, half/three-quarter baths by weight of .5, then sum them all together.  \n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 19,
   "metadata": {},
   "outputs": [],
   "source": [
    "df['structure_dollar_per_sqft'] = df.structuretaxvaluedollarcnt/df.calculatedfinishedsquarefeet\n",
    "df['land_dollar_per_sqft'] = df.landtaxvaluedollarcnt/df.lotsizesquarefeet\n",
    "df['living_area_sqft'] = df.calculatedfinishedsquarefeet - (df.bedroomcnt*121 + df.bathroomcnt*36)\n",
    "df['tax_rate'] = df.taxvaluedollarcnt/df.taxamount\n",
    "df['bedbath_index'] = df.bedroomcnt*2 + df.fullbathcnt + .5*(df.bathroomcnt-df.fullbathcnt)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "- turn yearbuilt into age (from present)\n",
    "- reduce regionidcity into the top 5 cities and the others assign to a catch-all id.\n",
    "- take the first 3 digits of zip to reduce the variance in zipcode \n",
    "- Look at variables that don't actually represent numeric values to think about encoding. (fips, regionidcity, regionidzip, regionidcounty)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 20,
   "metadata": {},
   "outputs": [],
   "source": [
    "df['age'] = 2017 - df.yearbuilt"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 21,
   "metadata": {},
   "outputs": [],
   "source": [
    "df.loc[:,'latitude'] = df.loc[:,'latitude']/1e6\n",
    "df.loc[:,'longitude'] = df.loc[:,'longitude']/1e6"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "City ID and County: Is there any cross-over or is city purely a subset of county? \n",
    "\n",
    "Count the number of counties each city is located in:"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 22,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th>regionidcounty</th>\n",
       "      <th>1286.0</th>\n",
       "      <th>2061.0</th>\n",
       "      <th>3101.0</th>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>regionidcity</th>\n",
       "      <th></th>\n",
       "      <th></th>\n",
       "      <th></th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>5465.0</th>\n",
       "      <td>1</td>\n",
       "      <td>0</td>\n",
       "      <td>275</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>9840.0</th>\n",
       "      <td>0</td>\n",
       "      <td>1</td>\n",
       "      <td>94</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>10608.0</th>\n",
       "      <td>414</td>\n",
       "      <td>0</td>\n",
       "      <td>1</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>12520.0</th>\n",
       "      <td>0</td>\n",
       "      <td>2</td>\n",
       "      <td>173</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>15237.0</th>\n",
       "      <td>80</td>\n",
       "      <td>0</td>\n",
       "      <td>2</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>18875.0</th>\n",
       "      <td>1</td>\n",
       "      <td>0</td>\n",
       "      <td>53</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>41673.0</th>\n",
       "      <td>0</td>\n",
       "      <td>104</td>\n",
       "      <td>3</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>44833.0</th>\n",
       "      <td>320</td>\n",
       "      <td>0</td>\n",
       "      <td>1</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "regionidcounty  1286.0  2061.0  3101.0\n",
       "regionidcity                          \n",
       "5465.0               1       0     275\n",
       "9840.0               0       1      94\n",
       "10608.0            414       0       1\n",
       "12520.0              0       2     173\n",
       "15237.0             80       0       2\n",
       "18875.0              1       0      53\n",
       "41673.0              0     104       3\n",
       "44833.0            320       0       1"
      ]
     },
     "execution_count": 22,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "ct = pd.DataFrame(pd.crosstab(df.regionidcity, df.regionidcounty))\n",
    "s = ct.astype(bool).sum(axis=1)\n",
    "s = s.where(s>1).dropna()\n",
    "pd.crosstab(df[df.regionidcity.isin(list(s.index))].regionidcity, df[df.regionidcity.isin(list(s.index))].regionidcounty)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Taking a look at these, I can see that when there are multiple counties, there is clearly a dominant county and only a handful of properties in the other. I will 'fix' the anomalies to be in what is likely the correct county. I'll test it here, but will need to implement above before we do all the prepping. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 23,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "3101.0    37640\n",
       "1286.0    15898\n",
       "2061.0     4881\n",
       "Name: regionidcounty, dtype: int64"
      ]
     },
     "execution_count": 23,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "df.loc[df.regionidcity.isin([5465.0,12447.0,12520.0]), 'regionidcounty'] = 3101.0\n",
    "df.loc[df.regionidcity.isin([10608.0,15237.0,18874.0,44833.0]), 'regionidcounty'] = 1286.0\n",
    "df.loc[df.regionidcity==41673.0, 'regionidcounty'] = 2061.0\n",
    "df.regionidcounty.value_counts()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "- Looking at the counts for each county, it seems reasonable to not split county 2061 geographically much more than that.  \n",
    "- County 1286 can probably be split more effectively: city 16764 and all others \n",
    "- County 3101 can definitedly be split more effectively: city 12447, 5534, 46298, 40227, and all others\n",
    "\n",
    "However, I'm going to wait to do this. I will first run some statistical tests to see if there are cities and zips that have significantly different logerror from the rest of the properties. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "# df.loc[(df['regionidcity']==12447) | (df['regionidcity']==5534) | (df['regionidcity']==40227) | (df['regionidcity']==46298) | (df['regionidcity']==16764), 'cityid'] = df['regionidcity']\n",
    "# df.cityid.fillna(0, inplace=True)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 24,
   "metadata": {},
   "outputs": [],
   "source": [
    "# have to do float first because of an issue with 0.0, then int, then string to ensure no decimals in the string.  \n",
    "# df['cityid'] = df.cityid.astype(float).astype(int).astype(str)\n",
    "df['regionidcity'] = df.regionidcity.astype(float).astype(int).astype(str)\n",
    "df['regionidzip'] = df.regionidzip.astype(float).astype(int).astype(str)\n",
    "df['regionidcounty'] = df.regionidcounty.astype(float).astype(int).astype(str)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": [
    "# df['loc_id'] = df.regionidcounty + '_' + df.cityid"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 27,
   "metadata": {},
   "outputs": [],
   "source": [
    "# clean up remaining columns\n",
    "df_prepped = df.drop(columns=(['id','parcelid','assessmentyear','propertycountylandusecode',\n",
    "                               #'propertylandusedesc',#'transactiondate', #'propertylandusetypeid',\n",
    "                               'finishedsquarefeet12', 'taxvaluedollarcnt', 'fips',\n",
    "                               'yearbuilt', 'rawcensustractandblock', 'censustractandblock', 'roomcnt', \n",
    "                               'calculatedbathnbr','taxamount','calculatedfinishedsquarefeet',\n",
    "                               'landtaxvaluedollarcnt','structuretaxvaluedollarcnt',\n",
    "                               'bedroomcnt','bathroomcnt','fullbathcnt'\n",
    "                              ]))"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 29,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "(58419, 18)"
      ]
     },
     "execution_count": 29,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "df_prepped.shape"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 30,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>0</th>\n",
       "      <th>2</th>\n",
       "      <th>4</th>\n",
       "      <th>5</th>\n",
       "      <th>6</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>latitude</th>\n",
       "      <td>34.281</td>\n",
       "      <td>34.1363</td>\n",
       "      <td>33.4856</td>\n",
       "      <td>33.8701</td>\n",
       "      <td>33.8995</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>longitude</th>\n",
       "      <td>-118.489</td>\n",
       "      <td>-118.175</td>\n",
       "      <td>-117.7</td>\n",
       "      <td>-118.403</td>\n",
       "      <td>-118.213</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>lotsizesquarefeet</th>\n",
       "      <td>7528</td>\n",
       "      <td>11423</td>\n",
       "      <td>6000</td>\n",
       "      <td>2708</td>\n",
       "      <td>6677</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>propertylandusetypeid</th>\n",
       "      <td>261</td>\n",
       "      <td>261</td>\n",
       "      <td>261</td>\n",
       "      <td>261</td>\n",
       "      <td>261</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>regionidcity</th>\n",
       "      <td>12447</td>\n",
       "      <td>47019</td>\n",
       "      <td>17686</td>\n",
       "      <td>29712</td>\n",
       "      <td>24174</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>regionidcounty</th>\n",
       "      <td>3101</td>\n",
       "      <td>3101</td>\n",
       "      <td>1286</td>\n",
       "      <td>3101</td>\n",
       "      <td>3101</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>regionidzip</th>\n",
       "      <td>96370</td>\n",
       "      <td>96293</td>\n",
       "      <td>96961</td>\n",
       "      <td>96109</td>\n",
       "      <td>96091</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>logerror</th>\n",
       "      <td>0.0276</td>\n",
       "      <td>-0.004</td>\n",
       "      <td>-0.005</td>\n",
       "      <td>-0.2705</td>\n",
       "      <td>0.044</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>has_pool</th>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>1</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>is_taxdelinquent</th>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>has_fireplace</th>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>has_garage</th>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "      <td>1</td>\n",
       "      <td>0</td>\n",
       "      <td>0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>structure_dollar_per_sqft</th>\n",
       "      <td>72.8943</td>\n",
       "      <td>27.963</td>\n",
       "      <td>74.2768</td>\n",
       "      <td>287.137</td>\n",
       "      <td>49.7679</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>land_dollar_per_sqft</th>\n",
       "      <td>31.5377</td>\n",
       "      <td>5.06977</td>\n",
       "      <td>44.1628</td>\n",
       "      <td>578.767</td>\n",
       "      <td>7.0349</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>living_area_sqft</th>\n",
       "      <td>1249</td>\n",
       "      <td>1867</td>\n",
       "      <td>1709</td>\n",
       "      <td>2439</td>\n",
       "      <td>1019</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>tax_rate</th>\n",
       "      <td>53.4704</td>\n",
       "      <td>10.4407</td>\n",
       "      <td>79.1682</td>\n",
       "      <td>90.2418</td>\n",
       "      <td>48.3828</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>bedbath_index</th>\n",
       "      <td>8</td>\n",
       "      <td>7</td>\n",
       "      <td>10.25</td>\n",
       "      <td>12</td>\n",
       "      <td>5</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>age</th>\n",
       "      <td>58</td>\n",
       "      <td>77</td>\n",
       "      <td>36</td>\n",
       "      <td>35</td>\n",
       "      <td>78</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "                                 0        2        4        5        6\n",
       "latitude                    34.281  34.1363  33.4856  33.8701  33.8995\n",
       "longitude                 -118.489 -118.175   -117.7 -118.403 -118.213\n",
       "lotsizesquarefeet             7528    11423     6000     2708     6677\n",
       "propertylandusetypeid          261      261      261      261      261\n",
       "regionidcity                 12447    47019    17686    29712    24174\n",
       "regionidcounty                3101     3101     1286     3101     3101\n",
       "regionidzip                  96370    96293    96961    96109    96091\n",
       "logerror                    0.0276   -0.004   -0.005  -0.2705    0.044\n",
       "has_pool                         0        0        1        0        0\n",
       "is_taxdelinquent                 0        0        0        0        0\n",
       "has_fireplace                    0        0        0        0        0\n",
       "has_garage                       0        0        1        0        0\n",
       "structure_dollar_per_sqft  72.8943   27.963  74.2768  287.137  49.7679\n",
       "land_dollar_per_sqft       31.5377  5.06977  44.1628  578.767   7.0349\n",
       "living_area_sqft              1249     1867     1709     2439     1019\n",
       "tax_rate                   53.4704  10.4407  79.1682  90.2418  48.3828\n",
       "bedbath_index                    8        7    10.25       12        5\n",
       "age                             58       77       36       35       78"
      ]
     },
     "execution_count": 30,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "df_prepped.head().T"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### Split Data"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 31,
   "metadata": {},
   "outputs": [],
   "source": [
    "train, test = train_test_split(df_prepped, test_size=.30)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### Scaling"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### Create Uniform Scaler\n",
    "when we the space between doesn't matter as much as order does, a uniform scaler is a good choice. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 32,
   "metadata": {},
   "outputs": [],
   "source": [
    "def scale_uniform(train, test, column_list):\n",
    "    scaler = QuantileTransformer(output_distribution='uniform', random_state=123)\n",
    "    train_scaled = pd.DataFrame(scaler.fit_transform(train[column_list]), \n",
    "                                columns = column_list, \n",
    "                                index = train.index)\n",
    "    train.drop(columns=column_list, inplace=True)\n",
    "    train = train.join(train_scaled)\n",
    "    \n",
    "    test_scaled = pd.DataFrame(scaler.transform(test[column_list]), \n",
    "                                columns = column_list, \n",
    "                                index = test.index)\n",
    "    test.drop(columns=column_list, inplace=True)\n",
    "    test = test.join(test_scaled)\n",
    "    \n",
    "    return train, test, scaler"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### Create MinMax Scaler\n",
    "When we want to preserve distance but want to be within bounds, a min-max scaler is a good choice. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 33,
   "metadata": {},
   "outputs": [],
   "source": [
    "def scale_minmax(train, test, column_list):\n",
    "    scaler = MinMaxScaler(feature_range=(0,1))\n",
    "    train_scaled = pd.DataFrame(scaler.fit_transform(train[column_list]), \n",
    "                                columns = column_list, \n",
    "                                index = train.index)\n",
    "    train.drop(columns=column_list, inplace=True)\n",
    "    train = train.join(train_scaled)\n",
    "    \n",
    "    test_scaled = pd.DataFrame(scaler.transform(test[column_list]), \n",
    "                                columns = column_list, \n",
    "                                index = test.index)\n",
    "    test.drop(columns=column_list, inplace=True)\n",
    "    test = test.join(test_scaled)\n",
    "    \n",
    "    return train, test, scaler"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "We will scale square feet, dollar per square foot, tax rate, beds & baths using a uniform scaler as that will help minimize the impact extreme outliers will have. \n",
    "\n",
    "For latitude, longitude and age, we want to preserve the distance between. We want 1876 to be futher away from the next oldest house of 1900 than 1900 is from the next oldest house of 1901. For this reason, we will use a min-max scaler. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 34,
   "metadata": {},
   "outputs": [],
   "source": [
    "column_list1 = ['lotsizesquarefeet','structure_dollar_per_sqft','land_dollar_per_sqft','living_area_sqft','tax_rate','bedbath_index']\n",
    "train, test, scaler_uniform = scale_uniform(train, test, column_list1)\n",
    "\n",
    "column_list2 = ['latitude','longitude','age']\n",
    "train, test, scaler_minmax = scale_minmax(train, test, column_list2)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 38,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>count</th>\n",
       "      <th>mean</th>\n",
       "      <th>std</th>\n",
       "      <th>min</th>\n",
       "      <th>25%</th>\n",
       "      <th>50%</th>\n",
       "      <th>75%</th>\n",
       "      <th>max</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>propertylandusetypeid</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>261.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>261.000</td>\n",
       "      <td>261.000000</td>\n",
       "      <td>261.000000</td>\n",
       "      <td>261.000000</td>\n",
       "      <td>261.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>logerror</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.012140</td>\n",
       "      <td>0.166284</td>\n",
       "      <td>-4.605</td>\n",
       "      <td>-0.026300</td>\n",
       "      <td>0.005000</td>\n",
       "      <td>0.039200</td>\n",
       "      <td>4.52</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>has_pool</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.217861</td>\n",
       "      <td>0.412798</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>is_taxdelinquent</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.022278</td>\n",
       "      <td>0.147587</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>has_fireplace</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.142323</td>\n",
       "      <td>0.349385</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>has_garage</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.351576</td>\n",
       "      <td>0.477468</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>0.000000</td>\n",
       "      <td>1.000000</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>lotsizesquarefeet</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.499993</td>\n",
       "      <td>0.288689</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.250050</td>\n",
       "      <td>0.499866</td>\n",
       "      <td>0.749985</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>structure_dollar_per_sqft</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.500000</td>\n",
       "      <td>0.288684</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.249893</td>\n",
       "      <td>0.500026</td>\n",
       "      <td>0.749969</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>land_dollar_per_sqft</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.499998</td>\n",
       "      <td>0.288681</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.249968</td>\n",
       "      <td>0.500030</td>\n",
       "      <td>0.749878</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>living_area_sqft</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.500002</td>\n",
       "      <td>0.288682</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.249750</td>\n",
       "      <td>0.500501</td>\n",
       "      <td>0.750000</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>tax_rate</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.499997</td>\n",
       "      <td>0.288685</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.249898</td>\n",
       "      <td>0.500128</td>\n",
       "      <td>0.749906</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>bedbath_index</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.500087</td>\n",
       "      <td>0.285462</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.246246</td>\n",
       "      <td>0.381882</td>\n",
       "      <td>0.753253</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>latitude</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.459301</td>\n",
       "      <td>0.183913</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.328515</td>\n",
       "      <td>0.460357</td>\n",
       "      <td>0.572324</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>longitude</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.670213</td>\n",
       "      <td>0.190339</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.560595</td>\n",
       "      <td>0.693213</td>\n",
       "      <td>0.810974</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>age</th>\n",
       "      <td>40893.0</td>\n",
       "      <td>0.401351</td>\n",
       "      <td>0.174712</td>\n",
       "      <td>0.000</td>\n",
       "      <td>0.284615</td>\n",
       "      <td>0.423077</td>\n",
       "      <td>0.500000</td>\n",
       "      <td>1.00</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "                             count        mean       std      min         25%  \\\n",
       "propertylandusetypeid      40893.0  261.000000  0.000000  261.000  261.000000   \n",
       "logerror                   40893.0    0.012140  0.166284   -4.605   -0.026300   \n",
       "has_pool                   40893.0    0.217861  0.412798    0.000    0.000000   \n",
       "is_taxdelinquent           40893.0    0.022278  0.147587    0.000    0.000000   \n",
       "has_fireplace              40893.0    0.142323  0.349385    0.000    0.000000   \n",
       "has_garage                 40893.0    0.351576  0.477468    0.000    0.000000   \n",
       "lotsizesquarefeet          40893.0    0.499993  0.288689    0.000    0.250050   \n",
       "structure_dollar_per_sqft  40893.0    0.500000  0.288684    0.000    0.249893   \n",
       "land_dollar_per_sqft       40893.0    0.499998  0.288681    0.000    0.249968   \n",
       "living_area_sqft           40893.0    0.500002  0.288682    0.000    0.249750   \n",
       "tax_rate                   40893.0    0.499997  0.288685    0.000    0.249898   \n",
       "bedbath_index              40893.0    0.500087  0.285462    0.000    0.246246   \n",
       "latitude                   40893.0    0.459301  0.183913    0.000    0.328515   \n",
       "longitude                  40893.0    0.670213  0.190339    0.000    0.560595   \n",
       "age                        40893.0    0.401351  0.174712    0.000    0.284615   \n",
       "\n",
       "                                  50%         75%     max  \n",
       "propertylandusetypeid      261.000000  261.000000  261.00  \n",
       "logerror                     0.005000    0.039200    4.52  \n",
       "has_pool                     0.000000    0.000000    1.00  \n",
       "is_taxdelinquent             0.000000    0.000000    1.00  \n",
       "has_fireplace                0.000000    0.000000    1.00  \n",
       "has_garage                   0.000000    1.000000    1.00  \n",
       "lotsizesquarefeet            0.499866    0.749985    1.00  \n",
       "structure_dollar_per_sqft    0.500026    0.749969    1.00  \n",
       "land_dollar_per_sqft         0.500030    0.749878    1.00  \n",
       "living_area_sqft             0.500501    0.750000    1.00  \n",
       "tax_rate                     0.500128    0.749906    1.00  \n",
       "bedbath_index                0.381882    0.753253    1.00  \n",
       "latitude                     0.460357    0.572324    1.00  \n",
       "longitude                    0.693213    0.810974    1.00  \n",
       "age                          0.423077    0.500000    1.00  "
      ]
     },
     "execution_count": 38,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train.describe().T"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 35,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "<class 'pandas.core.frame.DataFrame'>\n",
      "Int64Index: 40893 entries, 60138 to 73435\n",
      "Data columns (total 18 columns):\n",
      "propertylandusetypeid        40893 non-null float64\n",
      "regionidcity                 40893 non-null object\n",
      "regionidcounty               40893 non-null object\n",
      "regionidzip                  40893 non-null object\n",
      "logerror                     40893 non-null float64\n",
      "has_pool                     40893 non-null float64\n",
      "is_taxdelinquent             40893 non-null float64\n",
      "has_fireplace                40893 non-null float64\n",
      "has_garage                   40893 non-null float64\n",
      "lotsizesquarefeet            40893 non-null float64\n",
      "structure_dollar_per_sqft    40893 non-null float64\n",
      "land_dollar_per_sqft         40893 non-null float64\n",
      "living_area_sqft             40893 non-null float64\n",
      "tax_rate                     40893 non-null float64\n",
      "bedbath_index                40893 non-null float64\n",
      "latitude                     40893 non-null float64\n",
      "longitude                    40893 non-null float64\n",
      "age                          40893 non-null float64\n",
      "dtypes: float64(15), object(3)\n",
      "memory usage: 7.2+ MB\n"
     ]
    }
   ],
   "source": [
    "# train_prepped.describe().T\n",
    "train.info()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "## Cluster\n",
    "\n",
    "### K-Means\n",
    "\n",
    "#### Elbow Method to determine best 'K'"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "1. Let's first cluster by geolocation of latitude and longitude along with dollar per square foot (land and structure) and tax rate.\n",
    "\n",
    "2. Then we will cluster by lot size, living area, beds and baths, and age. \n",
    "\n",
    "##### Clustering 1: location, dollar/sqft, tax rate"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 39,
   "metadata": {},
   "outputs": [],
   "source": [
    "cluster1_cols = ['latitude','longitude','land_dollar_per_sqft','structure_dollar_per_sqft']"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Compute and plot the sum squared distances of each sample to closest cluster center at each k-value.  "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 40,
   "metadata": {},
   "outputs": [],
   "source": [
    "def select_k(cluster_df, ks):\n",
    "    sse = []\n",
    "    for k in ks:\n",
    "        kmeans = KMeans(n_clusters=k, n_init=1, max_iter=100, random_state=123)\n",
    "        kmeans.fit(cluster_df)\n",
    "\n",
    "        # inertia: Sum of squared distances of samples to their closest cluster center.\n",
    "        sse.append(kmeans.inertia_)\n",
    "\n",
    "    # print(pd.DataFrame(dict(k=ks, sse=sse)))\n",
    "\n",
    "    p = plt.plot(ks, sse, 'bx-')\n",
    "    p = plt.xlabel('k')\n",
    "    p = plt.ylabel('SSE')\n",
    "    p = plt.title('The Elbow Method to find the optimal k')\n",
    "\n",
    "    compare_df = pd.DataFrame(dict(k=ks, sse=sse)).assign(change_in_sse=lambda df: df.sse.diff())\n",
    "    return compare_df, p"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 42,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "(     k          sse  change_in_sse\n",
       " 0    1  9680.291192            NaN\n",
       " 1    2  6098.993781   -3581.297411\n",
       " 2    3  4693.368518   -1405.625263\n",
       " 3    4  3797.480436    -895.888081\n",
       " 4    5  3341.991963    -455.488473\n",
       " 5    6  3087.384086    -254.607878\n",
       " 6    7  2596.623391    -490.760695\n",
       " 7    8  2313.558005    -283.065386\n",
       " 8    9  2137.111583    -176.446422\n",
       " 9   10  1979.957576    -157.154008\n",
       " 10  11  1884.981565     -94.976010\n",
       " 11  12  1782.131407    -102.850158,\n",
       " Text(0.5, 1.0, 'The Elbow Method to find the optimal k'))"
      ]
     },
     "execution_count": 42,
     "metadata": {},
     "output_type": "execute_result"
    },
    {
     "data": {
      "image/png": "iVBORw0KGgoAAAANSUhEUgAAAZEAAAEWCAYAAACnlKo3AAAABHNCSVQICAgIfAhkiAAAAAlwSFlzAAALEgAACxIB0t1+/AAAADh0RVh0U29mdHdhcmUAbWF0cGxvdGxpYiB2ZXJzaW9uMy4xLjAsIGh0dHA6Ly9tYXRwbG90bGliLm9yZy+17YcXAAAgAElEQVR4nO3deZgU1dn38e8NKCqogAyEfVwwGncyIGiiIoqIaBN3YyIxGtSYqDF5UPNETTTmUWMSNebVEDeIRsUdFUUUcA3KoEZcYkBBGEAYZVFx1/v945wOPcNMz0zT09XT8/tcV19ddaq66q5mmHvOUqfM3REREclFm6QDEBGRlktJREREcqYkIiIiOVMSERGRnCmJiIhIzpREREQkZ0oiJcbMfm1mtxTgPOVm5mbWLq7PNLOTm/u8hZDPazGzm83st/k4Vh3HNjO7ycxWmdnzZvZtM3tjA47nZrZdc+1fKGb2SzO7vpmOvdDMDqhnW7P9WxczJZEWxsw+zHh9ZWYfZ6wfn+dz3Wxmn9U657/yeY5cZSSxF2qVd40xL2zkcQqSdOs59w/M7OkNOMS3gAOB3u4+yN2fcvev5ym8Gor1jwQz28/MqjLL3P137l50sZYqJZEWxt07pl/AIuDQjLJbm+GUl2ee0913a4ZzbIgOZrZzxvp3gQVJBVNg/YCF7r426UCk9VISKU0bm9lEM/vAzF41s4r0BjPraWZ3m1m1mS0wszPyeN5tY7PKGjO738y6ZJz3sBjL6vhX7Y6x/EQzeyBjv/lmNiljfbGZ7Z7lnH8HxmSsnwBMzNyhvms2sxHAL4Fj6qhl9TOzZ+J3+KiZdW3oWuK2Pczshfi5O4BN6go6fuY6YEg89+pYvmX8t6s2s7fN7Fdmtt7/UzM7Cbg+4/O/qf1XeWx6+YWZvRz/Te4ws00ytv+PmS0zs6Vm9sP6vmAzuwT4NnBNPNc1GZsPMLN5sUntL2ZmGZ/7oZm9HrdNNbN+Wc6R7TtdaGbnmdlr8Vg3mdkmZtYBeBjomVFT7plZu8yosZ4Yf5ZWmdmpZjYwfi+rM6/HzLY1s+lm9p6ZvWtmt5pZp/riznI9m5vZDDO7OvM7KUnurlcLfQELgQNqlf0a+AQYCbQF/g+YFbe1AeYAFwAbA9sAbwEH1XP8m4Hf1rOtHHCgXVyfCSwBdgY6AHcDt8Rt2wNrCU0vGwHjgPkZMayOsfUA3gaWxM9tA6wC2mQ5fzmwOF7rjsAbwAGEv9AbvOb4fd1S69gzgTdj3JvG9UsbcS0bx/h/FrcdCXye5Tv8AfB0rbKJwP3A5vHa/gOc1JjPA/sBVbV+Pp4HegJdgNeBU+O2EcDyjH+vf8Tvc7t6zjUTOLlWmQMPAp2AvkA1MCJuGx2/lx2BdsCvgGfrOXa932nGdbwC9InX8Uz6O619zbX/TTN+Tq4jJPThhP8f9wHdgF7ACmDfuP92MY72QBnwJHBltv9ztf+/AFvF773Of/dSe6kmUpqedvcp7v4l4S/1dBPUQKDM3S9y98/c/S3gb8CxWY71i/jXWvo1Icu+f3f3Vzw0r5wPHG1mbYFjgIfcfZq7fw5cQfjlvFeM4QNgd2BfYCqwxMx2iOtPuftXWc5ZxbrEMYZatZAcrxngJnf/j7t/DEyK8ZHtWoDBhF+CV7r75+5+FzC7gfP8V8Z3dZ67f+DuC4E/AN9v7DHqcLW7L3X3lcADGddxdLzG9L/Xr3M8/qXuvtrdFwEzMo5/CvB/7v66u38B/A7YvZ7aSLbvNO0ad18cr+MS4Lgmxnmxu3/i7o8SEtZt7r7C3ZcATwF7ALj7/BjHp+5eDfyR8HPYWD2BJ4A73f1XTYyxRWqXdADSLN7JWP4I2MTCKKp+hKr/6oztbQn/iepzRRP+MyzOWH6b8Au1K+E/1tvpDe7+lZktJvwVCOE/3X6EvwKfINRM9gWGxPWGTCT8Vb4XsA/QP2NbLtcM63+HHeNytmv5klCLypzV9G0aryvrajOZn+9V9+6NUvs6esblnoQaWuZ58nH89PfUD7jKzP6Qsd0I11L7XA39fMD6P1s9aZrlGcsf17HeEcDMugFXE5rvNifUZFc14TyHAB8Saj6tgmoirctiYIG7d8p4be7uI/N0/D4Zy30JTTnvAksJv1SAMDQ17rskFqWTyLfj8hOEJLIvjUsidxP+877l7rV/QTV0zU2dxjrbtSwDetVqA++b5Vi1z/0u4TvL/Gu9L+u+p3xaxvr/Xtk09XtaDJxS63vf1N2frWPfhn4+qCPWpTnG1ZD/i8fc1d23AL5HSH6N9TfgEWBK7LMpeUoircvzwPtmdo6ZbWpmbc1sZzMbmKfjf8/MvmFmmwEXAXfFJrVJwCFmNszMNgJ+DnwKpH+hPAEMBTZ19ypCLWEEoW35xYZOGptj9gfqGtbZ0DUvB8rr6ryuR7Zr+SfwBXCGmbUzs8OBQVmOtRzobWYbx+tIf1eXxI7ZfsDZQHMMQZ4E/CDj3+vCBvZfTuhPaqzrgPPMbCf474CBo7LEku3nA+B0M+ttYbDGL4E7MuLaysy2bEJs2WxOqEmsNrNewP/kcIyfEJpYHzSzTfMUV9FSEmlF4i+pQwnt1gsIf/leD2T7DzjOat4n8m6Wff9O6Fx8h9CJeUY87xuEv+j+HM95KGFo8mdx+38I/3GfiuvvEzq/n4kxN+baKt39zRyu+c74/p7VuueknvPUey3xeg4nNK2tIrT135PlcNOBV4F3Mr7XnxLa7N8CniZ0eN/YUFxN5e4PA1fGGObH92yuAo6Mo5uubsTx7wUuA243s/cJHeMH17Nv1p+P6B/Ao4Tv5S1CBzbu/m/gNuCt2GfX1Gau2n4DDADWAA+R/d+vTrE5cyyhNnZ/5oi4UmQ1m29FRIqLhRtHT3b3x5KORdanmoiIiORMSURERHKm5iwREclZs9VEzOxGM1thZq9klHUxs2lxmoRpZtY5llucHmB+nIpgQMZnxsT955nZmIzyb5rZ3PiZ0p9aQESkCDVbTcTM9iGMuJno7jvHssuBle5+qZmdC3R293PMbCRhVMpIYE/gKnffMw7nqwQqCGO35wDfdPdVZvY8cCYwC5hCuDP34Ybi6tq1q5eXl+f7ckVEStacOXPedfeyurY12x3r7v6kmZXXKk4RbioDmECYj+ecWD4xDo2bZWadzKxH3HdanOoAM5sGjDCzmcAW7v7PWD6RMFdPg0mkvLycysrKDbk0EZFWxczqndGg0B3r3d19GUB87xbLe1FzWoOqWJatvKqO8jqZ2VgzqzSzyurq6g2+CBERCYpldFZd/RmeQ3md3H28u1e4e0VZWZ01MhERyUGhk8jy2ExFfF8Ry6uoOTdOb8LcONnKe9dRLiIiBVToJDKZdQ8QGkN4bkK6/IQ4SmswsCY2d00FhptZ5ziSazgwNW77wMwGx1FZJ2QcS0RECqTZOtbN7DZCx3hXC09buxC4FJhk4alsi4D0hGxTCCOz5hOmkz4RwN1XmtnFrHsmw0XpTnbgNMI8TZsSOtQb7FQXEZH8anU3G1ZUVHhTRmddfjkMHAhDh64rmzEDZs+GceOaIUARkSJjZnPcvaKubcXSsV60Bg6Eo48OiQPC+9FHh3IRkdZOTzZswNChcMstcOihMHo0TJ0KkybVrJmIiLRWqok0wgEHgDvceiucdpoSiIhImpJIIzz5JHz1FWy8MVx77bqmLRGR1k5JpAHpPpBf/Qo++wz+539q9pGIiLRmSiINmD079IGcfTZsthksXBjWZ89u8KMiIiVPQ3yb4DvfCclj8WLQxPMi0lpoiG+epFKwZAnMmZN0JCIixUFJpAlGjYI2beB+TbAiIgIoiTRJ166w995KIiIiaUoiTTR6NMydCwsWJB2JiEjylESaKJUK76qNiIgoiTTZttvCTjspiYiIgJJITlIpeOopWLmy4X1FREqZkkgOUin48kt46KGkIxERSZaSSA4qKqBHDzVpiYgkkkTM7Ewze8XMXjWzs2JZFzObZmbz4nvnWG5mdrWZzTezl81sQMZxxsT955nZmPrOl29t2sBhh8Ejj8AnnxTqrCIixafgScTMdgZ+BAwCdgNGmVl/4FzgcXfvDzwe1wEOBvrH11jg2nicLoRH7u4Zj3VhOvEUQioFa9fC9OmFOqOISPFJoiayIzDL3T9y9y+AJ4DvAClgQtxnAjA6LqeAiR7MAjqZWQ/gIGCau69091XANGBEoS5i//2hY0c1aYlI65ZEEnkF2MfMtjKzzYCRQB+gu7svA4jv3eL+vYDFGZ+vimX1la/HzMaaWaWZVVZXV+flItq3hxEjYPLk8KwREZHWqOBJxN1fBy4j1BweAf4FfJHlI3XNl+tZyus653h3r3D3irKysiZGXL9UCt55R9PCi0jrlUjHurvf4O4D3H0fYCUwD1gem6mI7yvi7lWEmkpab2BplvKCGTkS2rZVk5aItF5Jjc7qFt/7AocDtwGTgfQIqzFA+lfzZOCEOEprMLAmNndNBYabWefYoT48lhVMly6wzz5KIiLSeiV1n8jdZvYa8ABweuwYvxQ40MzmAQfGdYApwFvAfOBvwI8B3H0lcDEwO74uimUFlUrBa6/B/PmFPrOISPL0ZMMNtHAhbL01XHEF/PzneTusiEjR0JMNm1F5Oey6q5q0RKR1UhLJg1QKnnkG3n036UhERApLSSQPUqlwr8iDDyYdiYhIYSmJ5MGAAdC7t5q0RKT1URLJA7MwIeOjj8LHHycdjYhI4SiJ5EkqBR99BI89lnQkIiKFoySSJ/vtB1tsoSYtEWldlETyZOON4eCD4YEHwlMPRURaAyWRPEqlYMUKeO65pCMRESkMJZE8OvhgaNdOTVoi0nooieRRp06hb0RJRERaCyWRPEul4I03wktEpNQpieTZYYeFd9VGRKQ1UBLJs759YY89lEREpHVQEmkGqRT885+wfHnSkYiINC8lkWaQSoG7JmQUkdKX1ONxf2Zmr5rZK2Z2m5ltYmZbm9lzZjbPzO4ws43jvu3j+vy4vTzjOOfF8jfM7KAkrqUuu+0G/fqpSUtESl/Bk4iZ9QLOACrcfWegLXAscBnwJ3fvD6wCToofOQlY5e7bAX+K+2Fm34if2wkYAfw/M2tbyGupT3pCxmnTYO3apKMREWk+STVntQM2NbN2wGbAMmB/4K64fQIwOi6n4jpx+zAzs1h+u7t/6u4LCM9gH1Sg+BuUSsEnn4REIiJSqgqeRNx9CXAFsIiQPNYAc4DV7v5F3K0K6BWXewGL42e/iPtvlVlex2dqMLOxZlZpZpXV1dX5vaB67LNPuPlQTVoiUsqSaM7qTKhFbA30BDoAB9exq6c/Us+2+srXL3Qf7+4V7l5RVlbW9KBzsNFGMHJk6FzXhIwiUqqSaM46AFjg7tXu/jlwD7AX0Ck2bwH0BpbG5SqgD0DcviWwMrO8js8UhdGjw3PXn3026UhERJpHEklkETDYzDaLfRvDgNeAGcCRcZ8xQLohaHJcJ26f7u4ey4+No7e2BvoDzxfoGhplxIgwRbyatESkVCXRJ/IcoYP8BWBujGE8cA5wtpnNJ/R53BA/cgOwVSw/Gzg3HudVYBIhAT0CnO7uRdVwtPnmsP/+cN994b4REZFSY97KfrtVVFR4ZWVlwc533XVw2mnwyiuw004FO62ISN6Y2Rx3r6hrm+5Yb2aakFFESpmSSDPr2RMGDlQSEZHSpCRSAKkUPP88LC2qsWMiIhtOSaQAUqnw/sADycYhIpJvSiIFsNNOsM02atISkdKjJFIAZqE28vjj8MEHSUcjIpI/SiIFkkrBZ5/B1KlJRyIikj9KIgWy997QpYuatESktCiJFEi7djBqFDz0EHz+edLRiIjkh5JIAaVSsGoVPP100pGIiOSHkkgBDR8O7durSUtESoeSSAF17AgHHBCSSCubskxESpSSSIGlUrBwIcydm3QkIiIbTkmkwA49NNw3oiYtESkFSiIF9rWvwZ57KomISGlQEklAKgVz5kBVVdKRiIhsmIInETP7upm9lPF638zOMrMuZjbNzObF985xfzOzq81svpm9bGYDMo41Ju4/z8zG1H/W4pKekHHy5GTjEBHZUEk8HvcNd9/d3XcHvgl8BNxLeOzt4+7eH3g8rgMcTHh+en9gLHAtgJl1AS4E9gQGARemE0+x22EH6N9fTVoi0vIl3Zw1DHjT3d8GUsCEWD4BGB2XU8BED2YBncysB3AQMM3dV7r7KmAaMKKw4ecmPSHjjBmwZk3S0YiI5C7pJHIscFtc7u7uywDie7dY3gtYnPGZqlhWX/l6zGysmVWaWWV1dXUew89dKhWmP3nkkaQjERHJXWJJxMw2Bg4D7mxo1zrKPEv5+oXu4929wt0rysrKmhZoMxkyBMrK1KQlIi1bkjWRg4EX3H15XF8em6mI7ytieRXQJ+NzvYGlWcpbhLZtw4SMU6ZoQkYRabmSTCLHsa4pC2AykB5hNQa4P6P8hDhKazCwJjZ3TQWGm1nn2KE+PJa1GKlU6BN54omkIxERyU0iScTMNgMOBO7JKL4UONDM5sVtl8byKcBbwHzgb8CPAdx9JXAxMDu+LoplLcaBB8Kmm6pJS0RaLvNWNhNgRUWFV1ZWJh3Gf6VS8OKL8PbbYdSWiEixMbM57l5R17akR2e1eqkULF4ML72UdCQiIk2nJJKwUaM0IaOItFxKIgnr1g322ktJRERaJiWRIpBKheast99OOhIRkaZREikCmpBRRFoqJZEisP32YVJGNWmJSEujJFIkRo8ONx2uXp10JCIijackUiRSKfjiizANiohIS6EkUiQGDQqPzlWTloi0JEoiRaJNGzj0UHj4Yfj006SjERFpHCWRIpJKwQcfwMyZSUciItI4SiJFZNgw6NBBTVoi0nIoiRSRTTaBgw4K94u0snkxRaSFUhIpMqkULFkCc+YkHYmISMOURIrI5ZfDFluEpx6mm7RmzAjlIiLFSEmkiAwcCD/6Eey0U0giM2bA0UeHchGRYpTUkw07mdldZvZvM3vdzIaYWRczm2Zm8+J757ivmdnVZjbfzF42swEZxxkT959nZmPqP2PLMHQoTJoEb74Jc+fC4YeH9aFDk45MRKRuSdVErgIecfcdgN2A14FzgcfdvT/weFwHOBjoH19jgWsBzKwLcCGwJzAIuDCdeFqyoUPhlFPCcps2MGBA9v1FRJJU8CRiZlsA+wA3ALj7Z+6+GkgBE+JuE4DRcTkFTPRgFtDJzHoABwHT3H2lu68CpgEjCngpzWLGDJg4EcaMgZUrYeRI+OqrpKMSEalb1iQSf+HXt61vjufcBqgGbjKzF83sejPrAHR392UA8b1b3L8XsDjj81WxrL7yumIda2aVZlZZXV2dY9jNL90HMmkS3Hwz/OQn8OyzoZ9ERKQYNVQTmZleMLPHa227L8dztgMGANe6+x7AWtY1XdXF6ijzLOXrF7qPd/cKd68oKytrarwFM3t2zT6Qq68ONyDeeCNMnZpsbCIidWkoiWT+ou6SZVtTVAFV7v5cXL+LkFSWx2Yq4vuKjP37ZHy+N7A0S3mLNW5czU709LPXd90VjjsOFixILjYRkbo0lES8nuW61hvF3d8BFpvZ12PRMOA1YDKQHmE1BkhP/jEZOCGO0hoMrInNXVOB4WbWOXaoD49lJaVDB7jnnnAH++GHw8cfJx2RiMg67RrY3s3MzibUOtLLxPUNaRf6KXCrmW0MvAWcSEhok8zsJGARcFTcdwowEpgPfBT3xd1XmtnFwOy430XuvnIDYipa224Lt9wCo0bBqaeG/hLLtR4oIpJH5lkmaTKzC7N92N1/k/eImllFRYVXVlYmHUZOfvMb+PWv4S9/gR//OOloRKS1MLM57l5R17asNZGWmCRK2fnnh873s86CPfaAIUOSjkhEWruGhvj+yMz6x2UzsxvNbE28c3yPwoQoaW3awN//Dn36wJFHwjvvJB2RiLR2DXWsnwksjMvHEe4u3wY4G7i6+cKS+nTuDPfeC6tWhXtKPv886YhEpDVrKIl84e7pX1OjCHeOv+fujwEdmjc0qc+uu8L118NTT4VhwSIiSWkoiXxlZj3MbBPCUNzHMrZt2nxhSUO++1044wy48kq47bakoxGR1qqhJHIBUElo0prs7q8CmNm+hKG5kqArroBvfxtOPjnM+isiUmgN3SeyHBgCfODuq8zsBOCIWD62uYOT7DbaKEyTMmAAfOc7UFkJnTolHZWItCYN1UT+CnwYE8g+wKXAREISuaq5g5OGfe1rcNdd8Pbb8P3va8ZfESmshpJI24y7wI8Bxrv73e5+PrBd84YmjbXXXqFv5MEH4be/TToaEWlNGkwiZpZu8hoGTM/Y1lBTmBTQj38caiK//jVMmZJ0NCLSWjSURG4DnjCz+4GPgacAzGw7YE0zxyZNYAbXXReG/x5/fHjErohIc8uaRNz9EuDnwM3At3zdRFttCJMoShHZbLMw468ZHHEEfPRR0hGJSKlr8PG47j7L3e9197UZZf9x9xeaNzTJxTbbwD/+AS+/DGPHhinkRUSaS8GfsS7Nb8QIuOgiuPVWuOaapKMRkVKmJFKifvlLOPRQOPtsePrppKMRkVKlJFKi2rSBiROhvByOOgqWLUs6IhEpRYkkETNbaGZzzewlM6uMZV3MbJqZzYvvnWO5mdnVZjY/TkE/IOM4Y+L+88xsTH3na606dQoz/r7/fkgkn32WdEQiUmqSrIkMdffdM56WdS7wuLv3Bx6P6wAHA/3jayxwLYSkA1wI7AkMAi5MJx5ZZ+ed4cYb4Zln4Be/SDoaESk1xdSclQImxOUJwOiM8okezAI6mVkP4CBgmruvdPdVwDRgRKGDbgmOOQZ+9jP485/Ds9pFRPIlqSTiwKNmNsfM0hM5dnf3ZQDxvVss7wUszvhsVSyrr3w9ZjbWzCrNrLK6ujqPl9FyXHYZ7LtvGPb7r38lHY2IlIqkksje7j6A0FR1epzcsT5WR5lnKV+/0H28u1e4e0VZWVnToy0BG20Ed9wBXbrA4YeHJyOKiGyoRJKIuy+N7yuAewl9GstjMxXxfUXcvQrok/Hx3sDSLOVSj+7dw4y/ixeHqVE046+IbKiCJxEz62Bmm6eXgeHAK8BkID3Cagxwf1yeDJwQR2kNBtbE5q6pwHAz6xw71IfHMsli8GC4+mp4+GH4zW+SjkZEWrokZuLtDtxrZunz/8PdHzGz2cAkMzsJWAQcFfefAowE5gMfAScCuPtKM7sYmB33uyhj2nrJ4pRT4Lnnwl3tAwfCqFFJRyQiLZV5K5tcqaKiwisrK5MOI3EffwzbbQdr1sBLL4VlgBkzYPZsGDcu2fhEpHiY2ZyM2zFqKKYhvlJAm24antH+0Udw4IGwdm1IIEcfHWonIiKNoQdLtWLHHRc62c85Byoq4N13wzPbhw5NOjIRaSlUE2nlxo2D4cPh3/+G9u1hhx2SjkhEWhIlkVZuxgx44QU48khYsgR22SV0uouINIaSSCuW7gOZNAnuvBOuvz7chPitb8HNNycdnYi0BEoirdjs2TX7QE46Ce6+G/r1gxNPhLPOgi++SDZGESluSiKt2Lhx63eijx4d+kfOOguuugoOOgjeey+Z+ESk+CmJyHratYM//Sk0aT3zTBjyO3du0lGJSDFSEpF6jRkDTz4Jn34KQ4aEpi4RkUxKIpLVoEFQWRlGbR15JFxwgSZuFJF1lESkQT16wMyZ8MMfwsUXw3e+Ex65KyKiJCKN0r59GAL85z/DQw+F2YDnzUs6KhFJmpKINJoZ/OQnMG0arFgRmroeeSTpqEQkSUoi0mRDh4Z+kr594ZBD4Pe/h1Y2GbSIREoikpPycnj2WTjiiHC/yfHHhxmBRaR1URKRnHXoEJ7b/rvfwe23h+lSFi1KOioRKaTEkoiZtTWzF83swbi+tZk9Z2bzzOwOM9s4lreP6/Pj9vKMY5wXy98ws4OSuZLWzQzOOw8eeADefDNMKf/UU0lHJSKFkmRN5Ezg9Yz1y4A/uXt/YBVwUiw/CVjl7tsBf4r7YWbfAI4FdgJGAP/PzNoWKHap5ZBDwuy/nTvD/vvDddclHZGIFEIiScTMegOHANfHdQP2B+6Ku0wARsflVFwnbh8W908Bt7v7p+6+gPAM9kGFuQKpyw47hEQyfDicdhqceip89lnSUYlIc0qqJnIlMA5I3/u8FbDa3dNzxlYBveJyL2AxQNy+Ju7/3/I6PlODmY01s0ozq6yurs7ndUgtnTrB5Mmhieuvf4Vhw2D58qSjEpHmUvAkYmajgBXuPiezuI5dvYFt2T5Ts9B9vLtXuHtFWVlZk+KVpmvbdl1n+5w5oZ+ksjLpqESkOSRRE9kbOMzMFgK3E5qxrgQ6mVn6me+9gaVxuQroAxC3bwmszCyv4zNSBI45JswC3KYNfPvb4ZnuM2bU3GfGDLj88mTiE5ENV/Ak4u7nuXtvdy8ndIxPd/fjgRnAkXG3McD9cXlyXCdun+7uHsuPjaO3tgb6A88X6DKkkfbYI9RCBg0KNZNDDoHHHgvb0k9WHDgw2RhFJHfFdJ/IOcDZZjaf0OdxQyy/Adgqlp8NnAvg7q8Ck4DXgEeA0939y4JHLQ0qKwuJ4/TT4eOPYeRI+PnP1z2at/aDsUSk5TBvZfNVVFRUeKUa6BNz/fVwyilhOvlddglDgYcMCfebiEhxMrM57l5R17ZiqolIK7DttrDllqGz/ZVXYO+9Q5PXX/8KH36YdHQi0lRKIlIw6T6Qu++G2bPhwQehY0f44INwT0nPnmGW4FdfTTpSEWksJREpmNmza/aBjBwZ7ikZOzaM4kql4G9/g513hn33DfNy6WZFkeKmPhEpKtXVcNNNoa9kwQLo3h1OPjkkmr59k45OpHVSn4i0GGVlYWr5+fNhypQwNPh3v4Ottw41lUce0TPeRYqJkogUpTZt4OCDQ3PXggVw7rkwa1Yo698/PAjr3XeTjlJElESk6PXrB5dcAosXw223Qa9eobbSuzeccEJILq2sVVakaCiJSIux8cZw7LHw5JMwdy6cdBLcd1+4z2TAgNApv3Zt0lGKtC5KItIi7bwz/OUvsGQJXHtt6CcZOzYME/7pT8Md8ZqnS6T5KWkZWPUAAA6CSURBVIlIi7b55uEek5degqefhkMPhfHj4Y9/hIMOggsuCMOENU+XSPNQEpGSYBbufr/lFqiqgksvhS5d4OKLw9MWDz44NIVtsQV88UXDxxORxtF9IlKyvvwSvve9MHvw5puHO+MBOnSAPfcMSWfvvWHw4DAVi4jULdt9Iu3qKhQpBU8+GWYPPv/80G8yfnwYxfXMM/Dss2HE11dfhVrMLrusSyp77x1GhGlSSJGGKYlISUr3gaSnWRk6dN36NdeEfT74IDwT/plnwuvvfw/JBkIHfWZS2W032Gij5K5HpFgpiUhJqj1P19ChYX327HVlm28OBxwQXhCav+bOXZdUnnkG7rwzbNtss5pNYEOG1GwCu/zy0Gmf+WyUGTPC+caNa/7rFUmK+kREsqiqqplU/vWvkGzMwjDjdFJp0wbOPHNd4qpdExJpybL1iRQ8iZjZJsCTQHtCTegud78wPuL2dqAL8ALwfXf/zMzaAxOBbwLvAce4+8J4rPOAk4AvgTPcfWpD51cSkQ3x4Yc1m8D++c91HfZduoTtBx4Y7qK/804lECkNxdax/imwv7t/aGYbAU+b2cOER9/+yd1vN7PrCMnh2vi+yt23M7NjgcuAY8zsG4RntO8E9AQeM7Pt9YhcaU4dO8KwYeEFoVby6qvrksqDD8JDD8Emm8Cjj8L224dpWkRKVcHvE/Eg/Qy7jeLLgf2Bu2L5BGB0XE7FdeL2YWZmsfx2d//U3RcA84FBBbgEkf9q2xZ23RVOOy1Mw7LRRvCDH4RRX5ddBuXlYZjxCy8kHalI80jkZkMza2tmLwErgGnAm8Bqd0/fBlYFpP9+6wUsBojb1wBbZZbX8Zna5xtrZpVmVlldXZ3vyxGp0Qdy001hyvrOneGww+D+++Gb34T99gvLX6quLCUkkSTi7l+6++5Ab0LtYce6dovvdY3W9yzldZ1vvLtXuHtFWVlZLiGLZFXXaLC77gojuqqq4IorwpT2o0fDDjuEeb80WaSUgkSnPXH31cBMYDDQyczSfTS9gaVxuQroAxC3bwmszCyv4zMiBTVu3Pqd6EOHhvIttwwTQr75Znjkb5cu4VnyvXuH56RUVSUTs0g+FDyJmFmZmXWKy5sCBwCvAzOAI+NuY4D74/LkuE7cPt3DkLLJwLFm1j6O7OoPPF+YqxBpunbtQpPXrFmhE/6AA8LDtbbeGo4/HubMSTpCkaZLoibSA5hhZi8Ds4Fp7v4gcA5wtpnNJ/R53BD3vwHYKpafDZwL4O6vApOA14BHgNM1MktaAjPYa68wBHj+/FAreeABqKiAffcNz0hRv4m0FLrZUKQIrFkDN9wAV10FixbBttuGmxdPPDEMKxZJUrb7RDQVvEgR2HJLOPvs0G8yaRKUlcEZZ0CfPnDOOeo3keKlJCJSRNq1g6OOCnfCP/tsuPv9iitCv8l3vwuqREuxURIRKVJDhoRayZtvhkf+PvhgmORxn33ghBPCNPeZ9PhfSYKSiEiRKy8Pj/utqgrvixaFaesPOigkl/fe0+N/JTlKIiItxBZbwM9+FkZ03XlnuGnxmmuga9fQ7LXffmECyDVrko5UWhMlEZEWpl07OPLIMPHjySeHsj59QnPXYYeFmxkHDQo3Mk6dqjvjpXkpiYi0UDNmhHtKzj8/1EDuuy+U/e//Qvv28Ic/wIgRYQ6vb30LLrggbP/kk6Qjl1Ki+0REWqDaD72q6yFYa9eGO+OnTw/bKyvD7MLt24ebHfffP+w7aJAe/SvZFdVDqZKmJCKlIJfH8a5ZA089FZLK9OnhKY0AHTqEmsr++4fXHnuEKe5F0pREMiiJiATvvgtPPBGSz/Tp8PrroXzLLcP0K0OHhqTy8MOhtqLnx7dexfZkQxEpAl27whFHhBfAsmUwc+a6pDJ5cijfYovQj3LaaTB2LCxdCscdF5rORFQTEZE6LVq0LqFMmRJqLmnl5WHCyB13XPf6+tdh000TC1eakZqzMiiJiDSde7ix8S9/CXfSd+0amr/eeit01kOYnbi8PNy/kplcdtwxDDuWlkvNWSKyQWbODA/UOv98uPZauOSS0EfyyScwb15IKJmv6dPh00/Xfb5bt3UJJTPJ9O4dkk+mXAYNSHKUREQkq9rDh4cOrbm+yy7hlenLL+Htt9dPLrffDqtXr9uvY8eaSWWHHaB79/qHL0vxUXOWiGSVz5qBOyxfDv/+9/oJZsmSdfulhxhvt13omzntNBg1Cvr3h549oY1uky6oouoTMbM+wETga8BXwHh3v8rMugB3AOXAQuBod19lZgZcBYwEPgJ+4O4vxGONAX4VD/1bd5/Q0PmVRESK0/vvh+SSTjD33AP/+U9IGOl+F4BNNgkP7erfPySZ9Pt224XmMSWY/Cu2JNID6OHuL5jZ5sAcYDTwA2Clu19qZucCnd39HDMbCfyUkET2BK5y9z1j0qkEKgCPx/mmu6/Kdn4lEZHil27COu200Adz9dXhQV3z54c+mPnzw+vNN2v2vbRvXzPBZCaZPn3qTjDqg2lYUXWsu/syYFlc/sDMXgd6ASlgv7jbBGAm4bnrKWCih2w3y8w6xUS0H+H57CsBzGwaMAK4rWAXIyJ5l60P5tRTa+775ZehGSwzsaSXp06tOU9Y+/awzTY1E0v//iG5qA8md4l2rJtZObAH8BzQPSYY3H2ZmXWLu/UCFmd8rCqW1Vde13nGAmMB+vbtm78LEJG8mz275hxgQ4eG9dmza9YWIPSd9O0bXsOG1dz21VchwWQmlvT7tGk1E0y7dmE6/b59w82Uo0bBrFlhCHO3bjVfHTrkfm2lWOtJLImYWUfgbuAsd3/fao/zy9i1jjLPUr5+oft4YDyE5qymRysihVLXL9N0jaQp2rQJtYw+fdb/7FdfhWSRWXuZPDn0x3TuDI8+CnffXfdxN9ts/cRSVrZ+Wbo8c3LLgQNLr9aTSBIxs40ICeRWd78nFi83sx6xFtIDWBHLq4A+GR/vDSyN5fvVKp/ZnHGLSGlo0yZ0wvfuHR7mNWMG3Hjjuvtg7r4bBg+G6mpYsaL+15Il8OKLYfnzz+s+V+fONRPLXnuFms6++4ZZln/7W+jXL8y6vCG1nKQk0bFuhD6Ple5+Vkb574H3MjrWu7j7ODM7BPgJ6zrWr3b3QbFjfQ4wIB7iBULH+sps51fHuohkasy0+g1xD7MkZ0s4ma/33qv7OB07wte+VvPVvfv6Zd26wcYbNxxXvprPiqpjHdgb+D4w18xeimW/BC4FJpnZScAi4Ki4bQohgcwnDPE9EcDdV5rZxcDsuN9FDSUQEZHamtIHUx8z6NQpvLbfPvu+6ST1ve/BzTeHJ1B27w7vvBNey5eH91degcceq3lzZqYuXRpOONtt1/zNZ7rZUESkQHKp9XzySUgs6eRS+5UuX7YMPv54/c+3aRNqSr17h+1NqWGlFVtNRESkVcql1rPJJqHPpF+/7Md2D49Jzkws6ddDD8FLL4U+n6YmkIaoJiIiUsJq37iZ75qIJggQESlRmc1lF10U3o8+OpTni5KIiEiJytZ8li9qzhIRkazUnCUiIs1CSURERHKmJCIiIjlTEhERkZwpiYiISM5a3egsM6sG3k46jkboCrybdBDNqJSvT9fWcpXy9W3ItfVz97K6NrS6JNJSmFllfUPqSkEpX5+ureUq5etrrmtTc5aIiORMSURERHKmJFK8xicdQDMr5evTtbVcpXx9zXJt6hMREZGcqSYiIiI5UxIREZGcKYkUGTPrY2YzzOx1M3vVzM5MOqZ8M7O2ZvaimT2YdCz5ZmadzOwuM/t3/DccknRM+WJmP4s/k6+Y2W1mtknSMW0IM7vRzFaY2SsZZV3MbJqZzYvvnZOMMVf1XNvv48/ly2Z2r5l1yse5lESKzxfAz919R2AwcLqZfSPhmPLtTOD1pINoJlcBj7j7DsBulMh1mlkv4Aygwt13BtoCxyYb1Qa7GRhRq+xc4HF37w88HtdboptZ/9qmATu7+67Af4Dz8nEiJZEi4+7L3P2FuPwB4ZdQr2Sjyh8z6w0cAlyfdCz5ZmZbAPsANwC4+2fuvjrZqPKqHbCpmbUDNgOWJhzPBnH3J4GVtYpTwIS4PAEYXdCg8qSua3P3R939i7g6C+idj3MpiRQxMysH9gCeSzaSvLoSGAd8lXQgzWAboBq4KTbXXW9mHZIOKh/cfQlwBbAIWAascfdHk42qWXR392UQ/qADuiUcT3P5IfBwPg6kJFKkzKwjcDdwlru/n3Q8+WBmo4AV7j4n6ViaSTtgAHCtu+8BrKXlNofUEPsGUsDWQE+gg5l9L9moJBdm9r+EZvNb83E8JZEiZGYbERLIre5+T9Lx5NHewGFmthC4HdjfzG5JNqS8qgKq3D1dc7yLkFRKwQHAAnevdvfPgXuAvRKOqTksN7MeAPF9RcLx5JWZjQFGAcd7nm4SVBIpMmZmhDb11939j0nHk0/ufp6793b3ckKn7HR3L5m/Zt39HWCxmX09Fg0DXkswpHxaBAw2s83iz+gwSmTQQC2TgTFxeQxwf4Kx5JWZjQDOAQ5z94/ydVwlkeKzN/B9wl/pL8XXyKSDkkb7KXCrmb0M7A78LuF48iLWru4CXgDmEn53tOgpQszsNuCfwNfNrMrMTgIuBQ40s3nAgXG9xann2q4BNgemxd8r1+XlXJr2REREcqWaiIiI5ExJREREcqYkIiIiOVMSERGRnCmJiIhIzpRERBJmZuWZs62KtCRKIiIikjMlEZEiYmbbxMkbByYdi0hjKImIFIk4XcrdwInuPjvpeEQao13SAYgIAGWEeZqOcPdXkw5GpLFUExEpDmuAxYS500RaDNVERIrDZ4Sn6E01sw/d/R9JByTSGEoiIkXC3dfGB3dNM7O17l4y05BL6dIsviIikjP1iYiISM6UREREJGdKIiIikjMlERERyZmSiIiI5ExJREREcqYkIiIiOfv/0xCXjbr7gL4AAAAASUVORK5CYII=\n",
      "text/plain": [
       "<Figure size 432x288 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "select_k(cluster_df = train[cluster1_cols], ks = range(1,13))"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "I would say 6 or 8 is hwere the bottom of the elbow sits.  \n",
    "Let's compare k=6 vs. k=8. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 43,
   "metadata": {},
   "outputs": [],
   "source": [
    "def compare_clusters(cluster_df, x_column, y_column, z_column, k1, k2):\n",
    "    estimators = [(str(k1)+' Clusters', KMeans(n_clusters=k1, n_init=1, max_iter=100, random_state=123)),\n",
    "                  (str(k2)+' Clusters', KMeans(n_clusters=k2, n_init=1, max_iter=100, random_state=123))]\n",
    "    \n",
    "    fig, axs = plt.subplots(1, 2, figsize=(14, 6), subplot_kw={'projection': '3d'})\n",
    "    \n",
    "    for ax, (title, kmeans) in zip(axs, estimators):\n",
    "        # fit the kmeans object\n",
    "        kmeans.fit(cluster_df)\n",
    "        \n",
    "        labels = kmeans.labels_\n",
    "        \n",
    "        ax.scatter(cluster_df[x_column], \n",
    "                   cluster_df[y_column],\n",
    "                   cluster_df[z_column],\n",
    "                   c=labels.astype(np.float), edgecolor='k')\n",
    "        ax.set(xticklabels=[], yticklabels=[], zticklabels=[])\n",
    "        ax.set(xlabel=x_column, ylabel=y_column, zlabel=z_column)\n",
    "        ax.set(title=title)\n",
    "    \n",
    "    plt.show()"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 46,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 1008x432 with 2 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "compare_clusters(cluster_df=train[cluster1_cols],\n",
    "                x_column='latitude', y_column='land_dollar_per_sqft', z_column='longitude',\n",
    "                k1=6, k2=8)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 52,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 1008x432 with 2 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "compare_clusters(cluster_df=train[cluster1_cols],\n",
    "                x_column='longitude', y_column='structure_dollar_per_sqft', z_column='latitude',\n",
    "                k1=6, k2=8)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 49,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 1008x432 with 2 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "compare_clusters(cluster_df=train[cluster1_cols],\n",
    "                x_column='longitude', y_column='structure_dollar_per_sqft', z_column='land_dollar_per_sqft',\n",
    "                k1=6, k2=8)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "As latitude moves east (left on the chart), we can see the land dollar per sqft and structure dollar per sqft increases, indicated by the slope upward as you move back and to the left. (low latitude, high structure dollar per sqft, high land dollar per sqft. "
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "I'm going to go with 8."
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 53,
   "metadata": {},
   "outputs": [],
   "source": [
    "def create_k_clusters(train, test, cluster_feature_id, cluster_cols, k):\n",
    "    kmeans = KMeans(n_clusters=k, n_init=1, max_iter=100, random_state=123)\n",
    "    kmeans.fit(train[cluster_cols])\n",
    "    cluster_feature = 'cluster'+str(cluster_feature_id)+'_id'\n",
    "    train[cluster_feature] = kmeans.predict(train[cluster_cols])\n",
    "    test[cluster_feature] = kmeans.predict(test[cluster_cols])\n",
    "    return train, test, kmeans"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 54,
   "metadata": {},
   "outputs": [],
   "source": [
    "train, test, kmeans1 = create_k_clusters(train, test, cluster_feature_id = 1, cluster_cols = cluster1_cols, k=8)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 55,
   "metadata": {},
   "outputs": [],
   "source": [
    "train.rename(index=str, columns={'cluster1_id': 'cluster_loc'}, inplace=True)\n",
    "test.rename(index=str, columns={'cluster1_id': 'cluster_loc'}, inplace=True)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 56,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "train['cluster'] = kmeans1.labels_\n",
    "train.cluster = 'cluster_' + (train.cluster + 1).astype('str')\n",
    "for i in range(0,len(cluster1_cols)):\n",
    "    for j in range(0, len(cluster1_cols)):\n",
    "        sns.relplot(data=train, x=cluster1_cols[i], y=cluster1_cols[j], hue='cluster')"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 57,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "1    7177\n",
       "3    6042\n",
       "2    5823\n",
       "4    5315\n",
       "6    5234\n",
       "0    4825\n",
       "7    3497\n",
       "5    2980\n",
       "Name: cluster_loc, dtype: int64"
      ]
     },
     "execution_count": 57,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train.cluster_loc.value_counts()"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 58,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "1    3130\n",
       "3    2591\n",
       "2    2529\n",
       "6    2188\n",
       "4    2180\n",
       "0    2113\n",
       "7    1456\n",
       "5    1339\n",
       "Name: cluster_loc, dtype: int64"
      ]
     },
     "execution_count": 58,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "test.cluster_loc.value_counts()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Clustering 2: size fields and age"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 59,
   "metadata": {},
   "outputs": [],
   "source": [
    "cluster2_cols = ['lotsizesquarefeet', 'living_area_sqft', 'bedbath_index','age']"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 60,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "(     k           sse  change_in_sse\n",
       " 0    1  11396.252745            NaN\n",
       " 1    2   6527.111995   -4869.140750\n",
       " 2    3   5329.062460   -1198.049535\n",
       " 3    4   4062.655844   -1266.406617\n",
       " 4    5   3681.552782    -381.103062\n",
       " 5    6   3286.194071    -395.358711\n",
       " 6    7   2989.163329    -297.030742\n",
       " 7    8   2809.788669    -179.374660\n",
       " 8    9   2679.259244    -130.529425\n",
       " 9   10   2504.380908    -174.878337\n",
       " 10  11   2357.591416    -146.789492\n",
       " 11  12   2262.398101     -95.193315,\n",
       " Text(0.5, 1.0, 'The Elbow Method to find the optimal k'))"
      ]
     },
     "execution_count": 60,
     "metadata": {},
     "output_type": "execute_result"
    },
    {
     "data": {
      "image/png": "iVBORw0KGgoAAAANSUhEUgAAAZEAAAEWCAYAAACnlKo3AAAABHNCSVQICAgIfAhkiAAAAAlwSFlzAAALEgAACxIB0t1+/AAAADh0RVh0U29mdHdhcmUAbWF0cGxvdGxpYiB2ZXJzaW9uMy4xLjAsIGh0dHA6Ly9tYXRwbG90bGliLm9yZy+17YcXAAAgAElEQVR4nO3deZxU1Zn/8c9DI4KAItAYARFFXOKujYI7VLO4YoxxySIajZOMoyZmxiUzxsTsmsRlMjE/426MikvEGKMSaFRcaTRxQwVBFkVFZRE1IPD8/jinQtFUV3dXV9Xtqvq+X696Vd1zb9373Oruevqcc+855u6IiIjko1PSAYiISPlSEhERkbwpiYiISN6UREREJG9KIiIikjclERERyZuSSIUxsx+Y2R9KcJzBZuZm1jkuTzOzM4p93FIo5LmY2U1m9uNC7CvLvs3MbjSzpWb2rJkdbGavtWN/bmY7FGv7UjGz75nZdUXa95tmVt/MuqL9rDsyJZEyY2YrMx7rzOzTjOWvFPhYN5nZ6ibH/Echj5GvjCT2XJPyvjHmN1u5n5Ik3WaOfaqZTW/HLg4CRgMD3X0/d3/c3XcqUHgb6Kj/JJjZYWa2KLPM3X/q7h0u1kqlJFJm3L1H+gEsAI7OKLutCIe8LPOY7r5nEY7RHt3NbLeM5S8D85IKpsS2Bd5094+TDkSql5JIZepiZreY2Udm9rKZ1aVXmFl/M7vHzJaY2TwzO6eAxx0Sm1WWm9kkM+udcdxjYizL4n+1u8Ty08zszxnbzTGziRnLC81srxzHvBWYkLF8CnBL5gbNnbOZjQO+B5yYpZa1rZk9ET/DR8ysb0vnEtftbWbPxffdCXTNFnR8z++AEfHYy2L5FvFnt8TM5pvZ/5jZRn+nZnY6cF3G+3/Y9L/y2PTyn2b2QvyZ3GlmXTPW/5eZLTazt83s6819wGb2E+Bg4DfxWL/JWF1vZrNjk9r/mZllvO/rZjYrrnvYzLbNcYxcn+mbZnaRmb0S93WjmXU1s+7AX4H+GTXl/pm1y4wa62nxd2mpmX3TzIbFz2VZ5vmY2RAzm2pmH5jZ+2Z2m5n1ai7uHOfT08wazOzqzM+kIrm7HmX6AN4E6puU/QD4J3AEUAP8DHg6rusEzAS+D3QBtgfmAmOb2f9NwI+bWTcYcKBzXJ4GvAXsBnQH7gH+ENftCHxMaHrZBDgfmJMRw7IY29bAfOCt+L7tgaVApxzHHwwsjOe6C/AaUE/4D73Fc46f1x+a7Hsa8EaMu1tc/nkrzqVLjP87cd3xwGc5PsNTgelNym4BJgE947m9DpzemvcDhwGLmvx+PAv0B3oDs4BvxnXjgHczfl5/jJ/nDs0caxpwRpMyBx4AegGDgCXAuLju2Pi57AJ0Bv4HeLKZfTf7mWacx0vANvE8nkh/pk3PuenPNOP35HeEhD6G8PdxH9APGAC8Bxwat98hxrEpUAs8BlyZ62+u6d8L0Cd+7ll/7pX2UE2kMk139wfdfS3hP/V0E9QwoNbdL3X31e4+F/g9cFKOff1n/G8t/bg5x7a3uvtLHppXLgZOMLMa4ETgL+4+2d0/A35J+HI+IMbwEbAXcCjwMPCWme0clx9393U5jrmI9YljAk1qIXmeM8CN7v66u38KTIzxketcgOGEL8Er3f0zd78bmNHCcf4l47O6yN0/cvc3gV8BX2vtPrK42t3fdvcPgT9nnMcJ8RzTP68f5Ln/n7v7MndfADRk7P/fgJ+5+yx3XwP8FNirmdpIrs807TfuvjCex0+Ak9sY54/c/Z/u/gghYd3u7u+5+1vA48DeAO4+J8axyt2XAL8m/B62Vn/gUeAud/+fNsZYljonHYAUxTsZrz8Bulq4impbQtV/Wcb6GsIfUXN+2YY/hoUZr+cTvlD7Ev6w5qdXuPs6M1tI+C8Qwh/dYYT/Ah8l1EwOBUbE5ZbcQviv/ADgEGBoxrp8zhk2/gx7xNe5zmUtoRaVOarpfFqvL+trM5nvH5B981Zpeh794+v+hBpa5nEKsf/057QtcJWZ/SpjvRHOpemxWvr9gI1/t/rTNu9mvP40y3IPADPrB1xNaL7rSajJLm3DcY4EVhJqPlVBNZHqshCY5+69Mh493f2IAu1/m4zXgwhNOe8DbxO+VIBwaWrc9q1YlE4iB8fXjxKSyKG0LoncQ/jjnevuTb+gWjrntg5jnetcFgMDmrSBD8qxr6bHfp/wmWX+tz6I9Z9TIS1m459XLm39nBYC/9bkc+/m7k9m2bal3w+yxPp2nnG15Gdxn3u4++bAVwnJr7V+DzwEPBj7bCqekkh1eRZYYWYXmFk3M6sxs93MbFiB9v9VM/u8mW0GXArcHZvUJgJHmlnKzDYBvgusAtJfKI8CI4Fu7r6IUEsYR2hbfr6lg8bmmFFAtss6Wzrnd4HB2Tqvm5HrXJ4C1gDnmFlnMzsO2C/Hvt4FBppZl3ge6c/qJ7FjdlvgPKAYlyBPBE7N+Hld0sL27xL6k1rrd8BFZrYr/OuCgS/liCXX7wfAWWY20MLFGt8D7syIq4+ZbdGG2HLpSahJLDOzAcB/5bGP/yA0sT5gZt0KFFeHpSRSReKX1NGEdut5hP98rwNy/QGebxveJ/J+jm1vJXQuvkPoxDwnHvc1wn90/xuPeTTh0uTVcf3rhD/cx+PyCkLn9xMx5tacW6O7v5HHOd8Vnz+wJvecNHOcZs8lns9xhKa1pYS2/ntz7G4q8DLwTsbnejahzX4uMJ3Q4X1DS3G1lbv/FbgyxjAnPudyFXB8vLrp6lbs/0/AL4A7zGwFoWP88Ga2zfn7Ef0ReITwucwldGDj7q8CtwNzY59dW5u5mvohsA+wHPgLuX9+WcXmzDMJtbFJmVfEVSLbsPlWRKRjsXDj6Bnu/rekY5GNqSYiIiJ5UxIREZG8qTlLRETyppqIiIjkrepuNuzbt68PHjw46TBERMrGzJkz33f32mzrqi6JDB48mMbGxqTDEBEpG2bW7IgGas4SEZG8KYmIiEjelERERCRvSiIiIpI3JREREcmbkkgLLrsMGho2LGtoCOUiItVOSaQFw4bBCSesTyQNDWF5WKEGTxcRKWNVd59IW40cCX/4Axx9NBx7LDz8MEycGMpFRKqdaiKtMHo0uMNtt8G3vqUEIiKSpiTSCo8+CmvXQo8ecM01G/eRiIhUKyWRFqT7QP7jP2DlSrj88g37SEREqpmSSAtmzAh9IGedFZZXrgzLM2YkG5eISEdQdfOJ1NXVeb4DMG6/PeyxB9x3X4GDEhHpwMxsprvXZVunmkgbpFIwbRqsWZN0JCIiHYOSSBvU18Py5fDcc0lHIiLSMSiJtMGoUeF5ypRk4xAR6SiURNqgtjb0iSiJiIgESiJtlErB9Onw6adJRyIikjwlkTaqr4dVq+DJJ5OOREQkeUoibXTIIdC5s5q0RERASaTNevSA/fdXEhERASWRvKRS0NgIy5YlHYmISLKURPKQSsG6deHGQxGRaqYkkofhw2GzzdSkJSKiJJKHLl1CB7uSiIhUOyWRPKVSMGsWvP120pGIiCRHSSRPqVR4Vm1ERKqZkkie9twT+vRREhGR6qYkkqdOncKAjFOmhPnXRUSqkZJIO6RSsGgRzJ6ddCQiIslQEmkH9YuISLVTEmmHIUNg0CD429+SjkREJBlKIu1gFkb1bWiAtWuTjkZEpPSURNoplYKlS+Hvf086EhGR0lMSaSdNmSsi1axoScTMbjCz98zspYyy3mY22cxmx+ctY7mZ2dVmNsfMXjCzfTLeMyFuP9vMJmSU72tmL8b3XG1mVqxzyeVzn4Ndd1W/iIhUp2LWRG4CxjUpuxCY4u5DgSlxGeBwYGh8nAlcAyHpAJcA+wP7AZekE0/c5syM9zU9Vsmkp8xdtSqpCEREklG0JOLujwEfNikeD9wcX98MHJtRfosHTwO9zGxrYCww2d0/dPelwGRgXFy3ubs/5e4O3JKxr5Krrw9zrj/1VFIRiIgko9R9Ilu5+2KA+Nwvlg8AFmZstyiW5SpflKU8KzM708wazaxxyZIl7T6Jpg49FGpq1C8iItWno3SsZ+vP8DzKs3L3a929zt3ramtr8wyxeZtvDsOGKYmISPUpdRJ5NzZFEZ/fi+WLgG0ythsIvN1C+cAs5YlJpeDZZ2HFiiSjEBEprVInkfuB9BVWE4BJGeWnxKu0hgPLY3PXw8AYM9sydqiPAR6O6z4ys+HxqqxTMvaViPr6cMPho48mGYWISGkV8xLf24GngJ3MbJGZnQ78HBhtZrOB0XEZ4EFgLjAH+D3w7wDu/iHwI2BGfFwaywC+BVwX3/MG8NdinUtrjBgB3bqpSUtEqot5lY1jXldX542NjUXZ95gxsHgxvPhiUXYvIpIIM5vp7nXZ1nWUjvWKkErBSy/BO+8kHYmISGkoiRRQemj4qVOTjUNEpFSURApo771hyy3VLyIi1UNJpIBqamDkSE2ZKyLVQ0mkwFIpmD8f5s5NOhIRkeJTEimwdL+IRvUVkWqgJFJgO+4IAwaoX0REqoOSSIGlp8ydOhXWrUs6GhGR4lISKYJUCj74AF54IelIRESKS0mkCNL9ImrSEpFKpyRSBP37w847q3NdRCqfkkiR1NfDY4/B6tVJRyIiUjxKIkWSSsEnn8AzzyQdiYhI8SiJFMlhh0GnTuoXEZHKpiRSJL16wb77ql9ERCqbkkgRpVKhOWvlyqQjEREpDiWRIqqvhzVrQge7iEglUhIpogMOgE03Vb+IiFQuJZEi6tYNDjxQSUREKpeSSJGlUvCPf8B77yUdiYhI4SmJFFl9fXhuaEg2DhGRYlASKbJ994UttlCTlohUJiWRIqupCTceKomISCVSEimBVCpMlztvXtKRiIgUlpJICWhoeBGpVEoiJbDLLrD11koiIlJ5lERKwCzURqZOBfekoxERKRwlkRJJpcK9Ii+9lHQkIiKFoyRSIul+EY3qKyKVREmkRLbZBoYOVb+IiFQWJZESqq+HRx+Fzz5LOhIRkcJQEimhVCrMLTJjRtKRiIgUhpJICY0cGa7UUpOWiFQKJZES6t0b9t5bnesiUjmUREqsvh6eego+/jjpSERE2i+RJGJm3zGzl83sJTO73cy6mtl2ZvaMmc02szvNrEvcdtO4PCeuH5yxn4ti+WtmNjaJc2mrVCp0rE+fnnQkIiLtV/IkYmYDgHOAOnffDagBTgJ+AVzh7kOBpcDp8S2nA0vdfQfgirgdZvb5+L5dgXHAb82sppTnko+DDoIuXdQvIiKVIanmrM5ANzPrDGwGLAZGAXfH9TcDx8bX4+MycX3KzCyW3+Huq9x9HjAH2K9E8edts81gxAj1i4hIZSh5EnH3t4BfAgsIyWM5MBNY5u5r4maLgAHx9QBgYXzvmrh9n8zyLO/ZgJmdaWaNZta4ZMmSwp5QHlIp+Pvf4YMPko5ERKR9kmjO2pJQi9gO6A90Bw7Psml6qEJrZl1z5RsXul/r7nXuXldbW9v2oAusvj4MxKgpc0Wk3CXRnFUPzHP3Je7+GXAvcADQKzZvAQwE3o6vFwHbAMT1WwAfZpZneU+HNmwY9OypfhERKX9JJJEFwHAz2yz2baSAV4AG4Pi4zQRgUnx9f1wmrp/q7h7LT4pXb20HDAWeLdE5tEvnznDooUoiIlL+kugTeYbQQf4c8GKM4VrgAuA8M5tD6PO4Pr7leqBPLD8PuDDu52VgIiEBPQSc5e5rS3gq7ZJKwezZsGBB0pGIiOTPvMpmSaqrq/PGxsakw+DFF2GPPeCGG+C005KORkSkeWY2093rsq3THesJ2W036NdPTVoiUt6URBKSnjJ3yhRNmSsi5UtJJEGpFLzzDrzyStKRiIjkR0kkQekpc9WkJSLlSkkkQYMHw5AhSiIiUr6URBKWSsG0abBmTYubioh0OEoiCUulYMUKmDkz6UhERNpOSSRhI0eGZ43qKyLlSEkkYbW1sOee6hcRkfKkJNIB1NfDk0/Cp58mHYmISNsoiXQAqRSsWgVPPJF0JCIibaMk0gEcfHAY2VdNWiJSbnImETPbPMe6QYUPpzr16AHDh6tzXUTKT0s1kWnpF2bW9P/k+woeTRWrrw+X+S5dmnQkIiKt11ISyZyCtneOddJOqVQYiHHatKQjERFpvZaSiDfzOtuytMN++0H37uoXEZHy0rmF9f3M7DxCrSP9mrhcW9TIqkyXLnDIIeoXEZHy0lJN5PdAT6BHxuv08nXFDa36pFLw2mvw1ltJRyIi0jo5ayLu/sNSBSKhcx1Ck9YppyQbi4hIa7R0ie83zGxofG1mdoOZLTezF8xs79KEWD123x369lW/iIiUj5aas84F3oyvTwb2BLYHzgOuLl5Y1alTJxg1SlPmikj5aCmJrHH3z+Lro4Bb3P0Dd/8b0L24oVWnVCr0ibz2WtKRiIi0rKUkss7MtjazrkAKyLx2qFvxwqpemjJXRMpJS0nk+0AjoUnrfnd/GcDMDgXmFje06nPZZTB/fpg2N51EGhpCuYhIR9TSfSLvAiOAj9x9qZmdAnwxlp9Z7OCqzbBhcMIJ4bmhIdwzcvLJMHFi0pGJiGTXUk3k/wErYwI5BPg5cAshiVxV7OCqzciRIWFMnw7LlsGxx4bl9OyHIiIdTUtJpMbdP4yvTwSudfd73P1iYIfihladRo6Es88Orz/+GB57TFdqiUjH1WISMbN0k1cKmJqxrqWmMMlDQwNcey3893/DppvCD34A550H69YlHZmIyMZaSgS3A4+a2fvAp8DjAGa2A7C8yLFVnYaG0CeSbsIaORKOPhquvDI0b/3+92HyKhGRjiJnTcTdfwJ8F7gJOMj9Xw0rnYCzixta9ZkxY8M+kFQKHnggDIdy001w4olhGl0RkY7CvMoa3Ovq6ryxsTHpMNrsqqvg29+G0aPhT38Kw8aLiJSCmc1097ps6zTHepk491y48cZw/8iYMaF5S0QkaUoiZeTUU+Guu0Kz12GHwbvvJh2RiFQ7JZEyc9xxoZ9k9mw4+GBYsCDpiESkmiWSRMysl5ndbWavmtksMxthZr3NbLKZzY7PW8ZtzcyuNrM5cQj6fTL2MyFuP9vMJiRxLkkYMwYmT4b33oODDtJgjSKSnKRqIlcBD7n7zoTh5WcBFwJT3H0oMCUuAxwODI2PM4FrAMysN3AJsD+wH3BJOvFUgwMOgGnTwtVaBx8Mzz+fdEQiUo1KnkTMbHPgEOB6AHdf7e7LgPHAzXGzm4Fj4+vxhCHo3d2fBnqZ2dbAWGCyu3/o7kuBycC4Ep5K4vbaCx5/HLp2DZcFP/FE0hGJSLVJoiayPbAEuNHMnjez68ysO7CVuy8GiM/94vYDgIUZ718Uy5or34iZnWlmjWbWuGTJksKeTcJ23DGMtbXVVuHy34ceSjoiEakmSSSRzsA+wDXuvjfwMeubrrKxLGWeo3zjQvdr3b3O3etqa2vbGm+HN2hQqJHstBMcc0y4gktEpBSSSCKLgEXu/kxcvpuQVN6NzVTE5/cytt8m4/0DgbdzlFelfv3CsCn77QcnnQQ33JB0RCJSDUqeRNz9HWChme0Ui1LAK8D9QPoKqwnApPj6fuCUeJXWcGB5bO56GBhjZlvGDvUxsaxq9eoFDz8cmrVOPx2uuCLpiESk0iU1nN/ZwG1m1oUwQ+JphIQ20cxOBxYAX4rbPggcAcwBPonb4u4fmtmPgBlxu0szhq2vWt27w/33w1e+Ekb/XbYsjARs2Rr/RETaSWNnVai1a+HMM0Oz1tlnh5GAO+nWUhHJQ66xszSweIWqqYHrroMttgjNWsuXw/XXayh5ESksfaVUMDP41a9gyy3h+9+HFSvgjjvCZFciIoWgBo4KZwYXXwxXXw333QdHHQUrVyYdlYhUCiWRKnH22XDzzTB1arh6a+nSpCMSkUqgJFJFTjkF7r4bnnsuDCX/zjtJRyQi5U5JpMp84Qvwl7/AnDlh4Mb585OOSETKmZJIFaqvh7/9DRYtgro6ePXV9esaGuCyy5KLTUTKi5JIlRoxAv73f+GDD2D//UMTV0MDnHACDBuWdHQiUi50iW8VO+OMcLnvqaeG+Um6dYN77w3DyouItIZqIlXua18LV26tWgWffBISiYhIaymJVLmGBrjtNjj3XFizBkaNgiefTDoqESkXSiJVLN0HMnFiGFvr9tth9WpIpTRLooi0jpJIFZsxIySQdB/ICSeERNKjB4wdGya6EhHJRaP4ykYWLw7NWgsXhntKDj006YhEJEm5RvFVTUQ2svXWoalr0CA44giYNi3piESko1ISkaw+97mQSAYPDolk6tSkIxKRjkhJRJq11VYhkQwZAkceGe5yFxHJpCQiOfXrF2ohQ4fC0UfDI48kHZGIdCRKItKi2tqQSHbaCY45Bh5+OOmIRKSjUBKRVunbF6ZMgV12gfHj4a9/TToiEekIlESk1fr0CYlk113h2GPD5b8iUt2URKRNevcOHey77x7mJvnzn5OOSESSpCQibbblliGR7LUXfPGLMGlS0hGJSFKURCQvvXrB5Mmwzz5w/PHwpz8lHZGIJEFJRPK2xRbhSq26ujDu1j33JB2RiJSakoi0SzqR7LcfnHgi3HVX0hGJSCkpiUi7bb45PPQQDB8OJ58Md96ZdEQiUipKIlIQPXuGe0cOOAC+/OUwpLyIVD4lESmYnj3hwQfh4IPhq18NMyaKSGVTEpGC6tFj/Rwkp5wCt96adEQiUkxKIlJw3bvDAw/AYYfBhAlw881JRyQixaIkIkWx2WbhbvZUCk47DW68MemIRKQYlESkaDbbDO6/H0aPhtNPh+uvTzoiESk0JREpqm7dwrAoY8fCGWfAd7+74fqGBrjssmRiE5H2SyyJmFmNmT1vZg/E5e3M7Bkzm21md5pZl1i+aVyeE9cPztjHRbH8NTMbm8yZSEu6dg3Douy/P/z61/Cd74TyhoZwp/uwYcnGJyL5S7Imci4wK2P5F8AV7j4UWAqcHstPB5a6+w7AFXE7zOzzwEnArsA44LdmVlOi2KWNunaFRx8NieTKK2GPPcJw8jfeCCNHJh2diOQrkSRiZgOBI4Hr4rIBo4C74yY3A8fG1+PjMnF9Km4/HrjD3Ve5+zxgDrBfac5A8rHppiGR7LsvvPgirFgBxx0HY8bA1VfD3LlJRygibZVUTeRK4HxgXVzuAyxz9zVxeREwIL4eACwEiOuXx+3/VZ7lPRswszPNrNHMGpcsWVLI85A2evJJmD8fvve9MO7WF74ACxfCuefCkCFhwqsLLoDHH4c1a1ren4gkq+RJxMyOAt5z95mZxVk29RbW5XrPhoXu17p7nbvX1dbWtileKZx0H8jEifCTn4R+kqlT4be/hdmz4YorYOutQ7/JIYfAVluFO9/vuAOWLUs6ehHJJomayIHAMWb2JnAHoRnrSqCXmXWO2wwE3o6vFwHbAMT1WwAfZpZneY90QDNmhASS7gMZOTIsz5gBO+wA3/52mOzq/fdD+VFHhRGCTz45zPE+ciT86lfw+uvJnoeIrGfuWf95L83BzQ4D/tPdjzKzu4B73P0OM/sd8IK7/9bMzgJ2d/dvmtlJwHHufoKZ7Qr8kdAP0h+YAgx197W5jllXV+eNjY1FPS8pnLVr4Zlnwh3wDzwQ+lIAhg4NSeaoo8JYXZtskmycIpXMzGa6e122dR3pPpELgPPMbA6hzyN9a9r1QJ9Yfh5wIYC7vwxMBF4BHgLOaimBSPmpqQkjA//0p/DCCzBvHvzmN6H/5P/+L9wR37dvmMvk1ltDLQbCvScNDRvuS/ekiBReojWRJKgmUjlWrgzNX+layrvvQqdOMGIE7LJLmGnx7rth1KgN+2N0SbFI2+SqiSiJSEVYtw5mzlyfUJ57LpR36hQuKX799TDr4ujRycYpUo6URDIoiVSHt94KQ9L/8pfhyi8IlxQfcQSMHw+HHx5mZBSRlpVLn4hIwQwYEDrfly6FCy8MCWPECJg8GU46KfSjjB0L11wTEo6I5EdJRCpSZh/Iz34G990HjY1h2t7HHw83N86dC//+7zBwYBi/68c/Dld/VVnlXKRdlESkIjV3T8pzz8FBB8Hll4d+kpdfDld+1dTAxReHMb2GDIHzzgtDtOiueZHc1CciEi1eHCbSmjQpXPW1ejX06QNHHhn6UcaODbM2ilQbdaxnUBKR1vjoo3C3/KRJoYN+6dIwEnF9fUgoRx8dhmURqQZKIhmURKStPvsMpk8PCWXSJHjzTTCD4cNDQhk/PszgOGzYhvegNDSEZrXzz08sdJGCUBLJoCQi7eEe7pxPJ5T0/SjbbBPulv/FL+Css0J/im5ulEqhS3xFCsQM9twTvv/9cHPjggVhGJaddoJVq+Ccc0K/ybhxYZj7TTaBf/4z6ahFikc1EZECWbYMvv71MMR9nz7wwQehvEsXqKsLV4UdeGAYC6xv32RjFWkL1URESuD558M9KBdfHGos994b7k8555zQDHbFFaH/pLY2jO31jW/ATTfBnDm6N0XKV+eWNxGRljQd4HHkyPXLl18etvn003DD4/Tp8MQTYXDI664L6/r1W19TOegg2HtvDW8v5UFJRKQAck24lS7r1i3MfXLwwWF53TqYNSsklHRiuffe9dvuv39IKgceGIZs6dVr/fEuu0xXg0nHoD4RkQ5k8eINk8rzz4eJucxgt91CLeWgg8LyOeesT1wa6l6KSZf4ZlASkXKyciU8++z6pPLUU+FGSAid8x99FDrqGxtDs9nJJ2t0Yik8JZEMSiJSztauDYNEppPKgw/CihUbblNbG+asz/bo3TuZuKW85Uoi6hMRKSM1NbDXXuGx665hjK8LLoBrrw0jE3frFq72mjMHpk0LUwZn6tWr+QTTr19oJmtK/S+Si5KISBlq2gcyduz65cwv9k8/DfPSpxPLnDnwxhuhiWzixNC5n9ajx4ZJZciQ8Dx48IbHyjy2iJqzRMpQIWoHq1fD/PkbJpj0Y968MGZY2iabhIQzZEi4S//LXw4d/P37r3/07p29JiPlT30iGZRERFq2Zg0sXLhhYnnggTAHS9eu2Ydy2XTTDZNK5mPAgPWve/bMfWw1n3U86hMRkTbp3Bm22y48Ro8OX+K33BLuxr/mmvkus0oAAAe9SURBVDC0y447wttvb/h4663w/I9/hE7/jz/eeN89euROMgMGqPmsnCiJiEhOue7Gb+melI8+yp5k0o+nngrPq1Zt/N5UKlxptmxZGC7m1VdDE9uQIbDttiHRSfLUnCUiORW7eck9TPrVNMncd1+4/yV9P0xmoqmpCYlkyJDsD81AWVjqE8mgJCLS8aVrP9/6Vmg+u+OOMNz+G29kfyxduuH7t9pq/dVlTRNM374bXgCgPpiWqU9ERMpGS81nhx668XuWLs2eXKZODX05mXr23DCprFkT5n655hr40pfCSMzqg2k91UREpEMpdM3gn/8MlyxnSzLz5oVLnTN16gQ77wy77x5mrBw0KDynXzetyVQDNWdlUBIRkbS1a0M/zBtvwK9/HS5j3mOPkCgWLAiXOTft9O/adX1SyUwymcmmucuYy7XpTM1ZIiJZ1NSEL/833oCnn15/CfOVV4YvendYsiQkk4UL1yeW9POUKeEigMw7/yEML5OtFtOlCxx/PNx+O4wZUxmXL6smIiJVrWkfTFuH1f/sszCEfzqxZEs26amSM3XvHpradt01XADQp0/uR+/eIem1RaFqPqqJiIg0ozUTiuWyySahljFoUPPbfPLJ+gSzcGGYFvmxx8IVZ1tsEe6B+eCD8FizJvs+zEINp6Vkk/nYfffi37ipmoiISAk1vXw5M4G5h3ti0gmlucf772+4vHJl88fbZJPQ9zNgQBiQM5+Jy1QTERHpAFq6fNksTCq2+eZhyJnWWrUKPvyw+aQzeXIYiubiiws/86WSiIhIibS36aw5m24KW28dHk01NITms/RFA+nkVSidCrer1jGzbcyswcxmmdnLZnZuLO9tZpPNbHZ83jKWm5ldbWZzzOwFM9snY18T4vazzWxCqc9FRKQtzj9/4y/wkSOLd3lvZs3n0kvD8wknhPJCKXkSAdYA33X3XYDhwFlm9nngQmCKuw8FpsRlgMOBofFxJnANhKQDXALsD+wHXJJOPCIikrvmUyglb85y98XA4vj6IzObBQwAxgOHxc1uBqYBF8TyWzxcAfC0mfUys63jtpPd/UMAM5sMjANuL9nJiIh0YNlqOGXfnJXJzAYDewPPAFvFBJNONP3iZgOAhRlvWxTLmisXEZESSSyJmFkP4B7g2+6+ItemWco8R3m2Y51pZo1m1rhkyZK2BysiIlklkkTMbBNCArnN3e+Nxe/GZiri83uxfBGwTcbbBwJv5yjfiLtf6+517l5XW1tbuBMREalySVydZcD1wCx3/3XGqvuB9BVWE4BJGeWnxKu0hgPLY3PXw8AYM9sydqiPiWUiIlIiSdwnciDwNeBFM/t7LPse8HNgopmdDiwAvhTXPQgcAcwBPgFOA3D3D83sR0D6OoNL053sIiJSGlU37ImZLQHmJx1HK/QF3k86iCKq5PPTuZWvSj6/9pzbtu6etS+g6pJIuTCzxubGqqkElXx+OrfyVcnnV6xzS/QSXxERKW9KIiIikjclkY7r2qQDKLJKPj+dW/mq5PMryrmpT0RERPKmmoiIiORNSURERPKmJNLBNDffSiUxsxoze97MHkg6lkKLo0zfbWavxp/hiKRjKhQz+078nXzJzG43s65Jx9QeZnaDmb1nZi9llGWd16jcNHNul8ffyxfM7E9m1qsQx1IS6Xiam2+lkpwLzEo6iCK5CnjI3XcG9qRCztPMBgDnAHXuvhtQA5yUbFTtdhNh+ohMzc1rVG5uYuNzmwzs5u57AK8DFxXiQEoiHYy7L3b35+LrjwhfQhUzxL2ZDQSOBK5LOpZCM7PNgUMIY8Ph7qvdfVmyURVUZ6CbmXUGNqOZAU/Lhbs/BjQdKmk8YT4j4vOxJQ2qQLKdm7s/4u5r4uLThEFr201JpANrMt9KpbgSOB9Yl3QgRbA9sAS4MTbXXWdm3ZMOqhDc/S3gl4Rx7RYTBkJ9JNmoiqK5eY0qzdeBvxZiR0oiHVQb5lspG2Z2FPCeu89MOpYi6QzsA1zj7nsDH1O+zSEbiH0D44HtgP5AdzP7arJRST7M7L8Jzea3FWJ/SiIdUDPzrVSCA4FjzOxN4A5glJn9IdmQCmoRsMjd0zXHuwlJpRLUA/PcfYm7fwbcCxyQcEzF0Ny8RhXBzCYARwFf8QLdJKgk0sHkmG+l7Ln7Re4+0N0HEzplp7p7xfw36+7vAAvNbKdYlAJeSTCkQloADDezzeLvaIoKuWigiebmNSp7ZjYOuAA4xt0/KdR+lUQ6nvR8K6PM7O/xcUTSQUmrnQ3cZmYvAHsBP004noKItau7geeAFwnfHWU9RIiZ3Q48BexkZoviXEY/B0ab2WxgdFwuO82c22+AnsDk+L3yu4IcS8OeiIhIvlQTERGRvCmJiIhI3pREREQkb0oiIiKSNyURERHJm5KISMLMbHDmaKsi5URJRERE8qYkItKBmNn2cfDGYUnHItIaSiIiHUQcLuUe4DR3n5F0PCKt0TnpAEQEgFrCOE1fdPeXkw5GpLVUExHpGJYDCwljp4mUDdVERDqG1YRZ9B42s5Xu/sekAxJpDSURkQ7C3T+OE3dNNrOP3b1ihiGXyqVRfEVEJG/qExERkbwpiYiISN6UREREJG9KIiIikjclERERyZuSiIiI5E1JRERE8vb/AbM3Fq8NNi3HAAAAAElFTkSuQmCC\n",
      "text/plain": [
       "<Figure size 432x288 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "select_k(cluster_df = train[cluster2_cols], ks = range(1,13))"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Compare 5 vs. 7 clusters"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 61,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 1008x432 with 2 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "compare_clusters(cluster_df=train[cluster2_cols],\n",
    "                x_column='lotsizesquarefeet', y_column='living_area_sqft', z_column='bedbath_index',\n",
    "                k1=5, k2=7)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 62,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 1008x432 with 2 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "compare_clusters(cluster_df=train[cluster2_cols],\n",
    "                x_column='lotsizesquarefeet', y_column='living_area_sqft', z_column='age',\n",
    "                k1=5, k2=7)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 63,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 1008x432 with 2 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "compare_clusters(cluster_df=train[cluster2_cols],\n",
    "                x_column='lotsizesquarefeet', y_column='bedbath_index', z_column='age',\n",
    "                k1=5, k2=7)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 64,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 1008x432 with 2 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "compare_clusters(cluster_df=train[cluster2_cols],\n",
    "                x_column='living_area_sqft', y_column='bedbath_index', z_column='age',\n",
    "                k1=5, k2=7)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "I'm going to go with 7 clusters."
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 65,
   "metadata": {},
   "outputs": [],
   "source": [
    "train, test, kmeans2 = create_k_clusters(train, test, cluster_feature_id = 2, cluster_cols = cluster2_cols, k=7)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 66,
   "metadata": {},
   "outputs": [],
   "source": [
    "train.rename(index=str, columns={'cluster2_id': 'cluster_home'}, inplace=True)\n",
    "test.rename(index=str, columns={'cluster2_id': 'cluster_home'}, inplace=True)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 67,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "iVBORw0KGgoAAAANSUhEUgAAAa0AAAFgCAYAAAAIICZdAAAABHNCSVQICAgIfAhkiAAAAAlwSFlzAAALEgAACxIB0t1+/AAAADh0RVh0U29mdHdhcmUAbWF0cGxvdGxpYiB2ZXJzaW9uMy4xLjAsIGh0dHA6Ly9tYXRwbG90bGliLm9yZy+17YcXAAAgAElEQVR4nO3deXxddbX//9fKOWmaOW3TgU60hTKUIi1EBlHgAmJBBAdUEBBHrgJXrwo/EbiAqFdx+DkiUkRAFJFJqagMVxkUGVqggJSpFNqG0iZtk7YZm2F9/9g7JcNpck6ak3128n4+HnnknM8eztpNm9XPZ3/2Z5m7IyIiEgd5UQcgIiKSLiUtERGJDSUtERGJDSUtERGJDSUtERGJjWTUAQzGokWL/J577ok6DBGRVCzqAEayWPa0Nm7cGHUIIiISgVgmLRERGZ2UtEREJDaUtEREJDaUtEREJDaUtEREJDaUtEREJDaUtEREJDaUtEREJDaUtEREJDaUtEREJDaUtEREJDaUtEREJDaymrTM7FdmVmNm/97JdjOzn5jZSjN71swOzGY8IiKpNLU2Uddcx6bmTWxq2sTWxvqoQ5KdyHZP6wZgUT/bjwfmhl9nA1dnOR4RkR42N2+mvq2eW1++lZ8+9VPqWutopY2mpsaoQ5MUspq03P1hYHM/u5wM/NoDjwEVZrZbNmMSEelS17iVTu/k0XWPUjKmhJP2PInzHzqfhvYGmmmJOjxJIep7WtOAtd3eV4dtfZjZ2Wa2zMyW1dbWDktwIjJybW3ZSitNPLH+CaaVTuMdU9/B1cuv5pJDL+HuVXeTZ1H/epRUov6ppKrw6al2dPfF7l7l7lUTJ07MclgiMpI1t7SytcV4Zu02KpPzeH1zLd987Jt87ZCvsXbbWqaVTCOZF8vC7iNe1D+VamBGt/fTgXURxSIio8TaLa2ccvWjbG1pB+DkhVM4bv8PsLllM4XJQqqmVFFaUBpxlJJK1D2tJcDHw1mEhwJb3P3NiGMSkRGqtbWVdVvr+NbdL+xIWAB3PV3DrOL51LfW8/bJB1OWLIswSulPVntaZvY74Cig0syqgcuAfAB3/wXwF+AEYCXQBHwym/GIyOjV2dlJCy2s3bqe6vrmPts3Nmynatb+FCYKGZM/JoIIJR1ZTVruftoA2x04N5sxiIi0tbWxqbWOf77xLyYVTub9C6fyg/te2bG9eEyCBdOmUpyAooLCCCOVgUR9T0tEJOs2tW7m9L9+jJqmGpJ5SX5yxK/40rF7cufT65haUcilJ+5LeUGSkrFjow5VBqCkJSIjWn1zMw9VP0RNUw0A7Z3tfOHhT3HZId/kZ/PnU1ZQxO7jyiOOUtIV9UQMEZGsWVffyG8eXcvGxq092ts721lW8xjTy8spLUhEFJ0MhpKWiIxIb27dyldue46fPfAqh089hrGJt4b+8iyPM/Y9k7F5BYwvGh9hlJIpDQ+KyIizobGGzs4iHn11EwBX3b+Ba469mTtW3UR7Zysfn/dJxo2tpFCTLmJHPS0RGVHWN67nSw/+N+BMLisA4P4Vm/jsda8zpu5DfOXAi9mvch8mF6uHFUdKWiIyomzbvo3nNj5HbctrfPeU+RQkg19z9c1t7Du1nETK1eMkLjQ8KCIj0pn3ns4dJ97NA+cfwYZtzUwqLSSZ6GBCiZZnijP1tEQk9ppbW6iu28LGhgamFUxj3vh5AHzo7hN5z12Hsrn9GcYVJplcquWZ4k49LRGJtQ1bm7jjqbX8+dkaZk0o5IJFe3Pju2/kjtfu4OW6lzlxzonMKJlJUUFB1KHKEFDSEpHY2tLcxI3/eo2fP/g6AM+v28oTr9ez5LzDOH3f06MNTrJCw4MiEltbW9q586n1Pdpqt7VSu601oogk25S0RCS28gwmlfUd9isdmx9BNDIclLREJFbWN9RQva2a5TXLmVRcyP+cuA9jEm/9KvvAgVNQzhq5dE9LRGKjrnkLnXSQZ3lMLprC+Q+fz2WHfosHzj+CZ6o3M3NCCRNKkuxWpmntI5WSlojEwvqGGv5vzX38bPnPaGpr4uiZR3PxoRfz1X98ia8ffgUn7D8j6hBlGChpiUgsbGvbwpVLr9zx/m9r/sbccXO5+NBL0CIXo4fuaYlILDxds7xP2xNvPkF+Xj4FeXoGa7RQT0tEYmH/yvl92hZMWkDJmFLKx+oe1mihnpaI5KTaxlpW1q/kR0/+iN+98DvGjx3P1w6+iDF5YwA4eMrBfGyfjylhjTLqaYlITqpuqOYT936CTu8E4Lcv/pbrjruOo2YcSad3krAkk4snRxylDDclLRHJOTUNNVz9zNU7EhbA6q2rWVm/ksOnHR5hZBI1JS0RyRkt29vZ1NRCItlJu7f32d7W2RZBVJJLdE9LRHLC9u3b2dzcTKc7hYlyPj3/0z22Ty6azL7j940oOskV6mmJSOQamptZU9/K//xxBa9vbOSYfSv58nvmcfMJN3Pry7cyuWgyp+x1iu5hiZKWiERv2/ZOTlv8BFuag+G/W5etA4yL3rs3lxx8Ccm8JIlEItogJSdoeFBEIrepoXVHwupy/4oaGlra2di4XQlLdlDSEpHIlReNwXotxTS7spi8PJhWoeew5C1KWiISufyE88Vj5uxIXGWFSa54/zwmFRdGG5jkHN3TEpHITSkr5dSDp/PBA2dQ37SdiaUFFI8xkkn9ipKe9DdCRHLClLAG1szxEQciOU3DgyIiEhtKWiIiEhtKWiIiEhtKWiIiEhtKWiIiEhtKWiIiEhtKWiIiEhtKWiIiEht6uFhEhsz6hg00tDdQ01TD7LLZFOUVUl5UHnVYMoIoaYnIkFjfsIHFz17Dba/cBkBhspDr33O9kpYMKQ0PisiQaOlo3pGwAJrbm7ly6ZW82fBmhFHJSKOkJSJDor61vk/buoZ1dHhHBNHISKWkJSJDYkrxFMoLeg4FHj/7eEryyyKKSEYiJS0RGRJleWXcsOgGDp96OLuX7c5n9/8sZ847k4qxSloydMzdo44hY1VVVb5s2bKowxCRFNY3bKDd26gYU0FJQUnU4UTBBt5FBivrPS0zW2RmL5nZSjO7MMX2mWb2gJk9bWbPmtkJ2Y5JRLJnSslkppdOH60JS7Isq0nLzBLAVcDxwDzgNDOb12u3S4Bb3X0hcCrw82zGJCIi8ZXtntbBwEp3X+Xu24FbgJN77eNA16B3ObAuyzGJiEhMZTtpTQPWdntfHbZ1dzlwhplVA38B/ivViczsbDNbZmbLamtrsxGriIjkuGwnrVQ3JHvP/DgNuMHdpwMnADeZWZ+43H2xu1e5e9XEiROzEKqIiOS6bCetamBGt/fT6Tv892ngVgB3fxQYC1RmOS4REYmhbCetpcBcM5ttZmMIJlos6bXPGuAYADPblyBpafxPRET6yOqCue7ebmbnAfcCCeBX7v68mV0BLHP3JcBXgGvN7EsEQ4ef8Dg+PCYywqzfspVOz2NMAipLNX1dcoMeLhaRHtrb21m1qZEL73ieF97cyjvnjufrJ+3H1IriqEOLCz1cnEUqTSIiPdQ0tHDmdUvZsLUVgPtX1NLa9m9+8OF5TCwrjTg6Ge209qCI9NC0vWNHwuryj5UbaXP9upDo6W+hiPRQOCZJQbLnr4Y5lcXgnRFFJPIWJS0RYUNdA29sbmTd5gbKCxJ88wP7kp8Ibs2UjU3y3VPmM7VCQ4MSPd3TEhnl1tU18l+3PMuTq+sYXzyG77x/HkfvOZEHLziSbS1tlBXmUzE2EXWYIoB6WiKj2sYtjXzrzy/y5Oo6ADY3bufcW56htROmVRSzz5QKppYXU1QwNuJIRQJKWiKjWGt7J0+ECatLW4ezvr45oohE+qekJTKKFSTzWDijvEdbIs+YXF4YUUQi/VPSEhnFKsuLufTEeew3NagOVFqQ5IenzGdMIn6LDsjooIkYIqPc9PHFXHfmQto6IJkwivKN8pKiqMMSSUlJS0SYMk5rC0o8aHhQRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ0lLRERiQ6u8i8TMtq11NNDE0jceY3LxFPYYtyeVpZOjDktkWChpicTMutb1nH7vmbR2tAKwoPIAfviu71NZNiXiyESyT8ODIjFSv6WGHy//yY6EBbB84zOsa1wXYVQiw0dJSyRG2r2d+u1b+rRvaamPIBqR4aekJRIj40onc/qeH+3RVl5Qzt6V8yKKSGR46Z6WSIwkEgkO2+0wfnj49/j9qjuYMnYS//m2sylLlkUdmsiwUNISiZnxZZM4tmwRB01cSH6igJKSiqhDEhk2SloiMTWuXNPcZfTRPS0RkVHCzC43s/MHcVyFmZ2TjZgypaQlIiIDqQAySloWGPIco6QlIjJCmdnHzexZM3vGzG7qte1BM6sKX1ea2evh6/3M7AkzWx4eOxf4DrBH2Pa9cL8LzGxpuM/Xw7ZZZvaCmf0ceAqYMdTXpHtaIiIjkJntB1wMHO7uG81sPPCFNA79HPBjd/+tmY0BEsCFwHx3XxCe+zhgLnAwYMASMzsCWAPsDXzS3bMynKikJSIyMh0N3O7uGwHcfbOZpXPco8DFZjYduNPdX0lx3HHh19Ph+xKCJLYGWO3ujw1B/ClpeFBEZGQywPvZ3s5bOWBsV6O73wycBDQD95rZ0Ts597fdfUH4tae7Xxdua9z10HdOSUtEZGT6G/ARM5sAEA4Pdvc6cFD4+pSuRjObA6xy958AS4C3AduA0m7H3gt8ysxKwmOmmdmkbFxEbxoeFIlIR0cH9c1tlBTkU5CfiDocGWHc/Xkz+xbwkJl1EAzlvd5tl+8Dt5rZmcDfu7V/FDjDzNqA9cAV4dDiI2b2b+Cv7n6Bme0LPBoOHTYAZwAd2b4uc++v95ibqqqqfNmyZVGHITJoDc3b2Nq+DXOYWDSJTY3tTC4fO/CBEgdp3TiSwUl7eNDMjk3RdtbQhiMy8tU01nD9Czdwxl/P4NwHzuOJDY+Tn7eNN+ubow5NJOdlck/rUjO72syKzWyymf0JeF+2AhMZidra2rh/9f0sfm4xtc21vFL/Cuf87VwavYWO9s6owxPJeZkkrSOBV4HlwD+Bm939lP4PEZHuNjdv5L7V9/Vo6/AOlq5fyuTyMRFFJRIfmSStccAhBImrFdjd0pz0LyKBwmQRs8pn9WmfUzGbtrb24Q9IJGYySVqPEcwaWQS8HZgKPDLQQWa2yMxeMrOVZnbhTvb5iJmtMLPnzezmDGISiZWyonL+823/ybSSaTvaFs1axG5Fu1FUVBhhZCLxkPbsQTOb6e5rerUd4e4P93NMAngZeDdQDSwFTnP3Fd32mQvcChzt7nVmNsnda/qLRbMHJe7WN6ynvrWewmQhhYkCJpVMiTokGToagcqiTJ7TWmtmZwBz3P0KM5sJtAxwzMHASndfBWBmtwAnAyu67fNZ4Cp3rwMYKGGJjARTSqYwRYlKJGOZJK2fA50E61ldQfCE9B0EQ4U7Mw1Y2+19NcF9se72AjCzRwgWZrzc3e/pfSIzOxs4G2DmzJkZhC0ikvtmXfjnjwH/C8wkWMPvote/894hvV1iZpcDDe7+/QyPqwA+5u4/H4IYioDbgD0IHkb+k7unvHWUSib3tA5x93MJe1dhz2ig6U6pusm9xyOTBAstHgWcBvwy/APqeZD7YnevcveqiRMnZhC2iEhuCxPWtcDuBL83dweuDdtzwVDX0/q+u+8DLAQON7Pj0z1vJkmrLbxH5WFAEwl6Xv2ppmc9lenAuhT73OXube7+GvASQRITiZ1tW+po37iK1keupvXF+2jbuiHqkCQe/hco6tVWFLYPWi7W03L3Jnd/IHy9PdxverrXlMnw4E+APwCTwvWsTgEuGeCYpcBcM5sNvAGcCvT+n8MfCXpYN5hZJcFw4aoM4hLJGWM3rSD5m/eR7AyWYOuY+Q5aP3QDBeWTI45MctzO7nkM+l5IHOpphaNq7wN+nO51pZ20wgt4EjgmDPL97v7CAMe0m9l5BCsCJ4BfhYs4XgEsc/cl4bbjzGwFwfjmBe6+Kd24RHJFU90Giv5+KXS+tWZoYs2/6GysASUt6d8agiHBVO2DldP1tMwsCfwO+EnXZL10DJi0ei1nXxN+yI5t7r65v+Pd/S/AX3q1XdrttQNfDr9EYsvohO19Swl5m9YUlAFdRHBPq/sQYVPYPliDrqdlZo8D7yWop/UZ+o5+ddXTuqZHo9ks0q+ntRh4xd1/lOb+QHr3tJ4EloXfawmeu3olfP1kJh8mMpLll1Sy/e2f79lYPh2r6DOsL9JDOEvws8BqgkSzGvjsLs4ezNl6Wmb2TaAc+O9MLgjS6Gm5++zwQ34BLAl7ToSzPfqs/C4yWiXz82ne6wS2F09kzPIbaRu3J3mHnUN++W5RhyYxECaoIZvinqv1tMJhx4uBF4GnwuN/5u6/TOe6MlkR40l3P6hX2zJ3r0rrBENIK2JIrmvaVk8iWUBBoZZmGoW0IkYWZTJ7cKOZXQL8hqD7egagCRMiKRSV9nnUUESGQCZJ6zTgMoJp7wAPh20io0rN1mZa2jspG5ukoqgg6nBEclY4oaP3P5Iz3f25wZ4zkynvm4EvDvaDREaCNZsb+e49L/Hi+m0ctddEPnvEHCaXjR34QJFRyN17L9u3y9JOWma2F3A+MKv7ce5+9FAHJZKL1tU3c+Z1T7B6UxMAK2saqGvazlcX7c2kMt27EhkOmQwP3gb8AvglacwQERlpmts6diSsLnc/+yZfOW7viCISGX0ySVrt7n511iIRyXEFyTzyDDq7TbidXDaWdGfgisiuy2TB3D+Z2TlmtpuZje/6ylpkIjkmPwGfO3KPHe+TecY3Tt6PSSUDFTsQkaGSyXNar6VodnefM7QhDUzPaclweLO+mVdrG9jcuJ2qWeMpTUJDu9O4vYPXNzaxz5RSCpIwsaz34twyyg3uOa3Ly/vU0+LyLSOunlav8y4hKCw8P91jMpk9OHtQUYnE0Jtbmvncb57kmeotAJQUJLnr3MPZY1IJAHtOKu3vcJHMBAmr+9qDuwPXcnk5Q524BqmrnlbaScuCpS7M3VOWsDKzDxKspJGRAYcHzezorg9I9ZXpB4rEwSsbGnYkLICG1nZ+9H8vs3mbFr+VrBg19bTC/UoIFkn/ZqbXlE5P60iCdanel2KbA3dm+qEiua52W0uftk2N29neoUkXkhWjrZ7WN4AfEKxkn5F0Fsy9LPz+yf72M7Oz3P3GTAMQyUWHzJlAYX6C5ra3nu44/dDdmVKh+1eSFaOmnpaZLQD2dPcvhaVMMpLJ7MGBaLUMGTHKk8Zd5x7Oe/abwiGzx/PT0xZSNVPrCUrWXETfXkdk9bSAk4BmgnpaqRaQ6KqntSD82tPdrwu3DVRP6zDgoHA48p/AXmb24EAX02Uok5ZWNpYRo7S0kL2mlPKtk/flRx85gPcdMJXJ5Vr1QrIkmGzRp57WLk7CyMl6Wu5+tbtPdfdZwDuBl939qHQvKpOHiweMZQjPJZITKjWdXYZLkKBGfD2tXZX2c1oDnsjsaXdfOCQnG4Ce0xKRHKZRpywayuHBR4bwXCIiIn1kssp7AfAh+q7yfkX4/byhDk5EROIr0npawF3AFuBJoHWwHygiIqNDpPW0gOnuvmioAxAREUlXJve0/mVm+2ctEhERkQEM2NMys+cIprMngU+a2SqC4UEjWOX9bdkNUUREJJDO8OCJWY9CRESyLldKk4QrYOxGsOoGwHHuXpPOsemsPbg6/JCb3P3MXh98E3BmygNFRCRt+9+4f596Ws+d9VwulCWBLJQmAU5394wfuM3kntZ+vQJK8NYSICIiMkhhwrqWYNFcC79fG7YPWq6WJtkV6dTT+pqZbQPeZmZbw69tQA3BNHgREdk1Q15Pq1tpkqPd/QDSX9S8qzTJAqAKqCYoTfJquDjuBb1KkywgWAD3iPD4vYFfu/vCrpG6nbg+TIL/Y2kuPw9pJC13/7a7lwLfc/ey8KvU3Se4+9fS/SAREdmpIa+nRYrSJGke9yhwkZl9Fdjd3VNVPu1emuQpYB+CJAYDlCYJne7u+wPvCr/Svs2U9nNa7v41MxsXBtZ9GfuH0z2HiIiklI16WoMuTRKuZPFegtIknwFWpTj3t939mh6NQX2sgUqT4O5vhN+3mdnNBD22Xw90HGRwTysM/GGCJem/Hn6/PN3jRURkp7JRTysnS5OYWdLMKsPX+QQz1P+d7kVlMhHji8DbCbp+/wEsBGozOF5ERFIIZwn2qae1K7MH3f15oKs0yTPA/99rl+8DnzezfwGV3do/CvzbzJYTDPv92t03AY+Y2b/N7Hvufh9BGZVHw2d5b6dnUutPAUEP7llgOfAGwSSUtKRdmsTMlrr728MLOcTdW81seXizblipNImI5DCVJsmiTNYerA4fMPsjcL+Z1QHrshOWiIhIX5lMxPhA+PJyM3sAKAfuyUpUIiISe1GXJsHMDgTeSTDm+oi7bx/sB4uIyMiWjdIkmcwevBS4EZhAcNPuejO7ZKgDEhER2ZlMelqnAQvdvQXAzL5D8FDZN7MRmIiISG+ZTHl/nW4PoBGMU746pNGIiIj0I516Wj8luIfVCjxvZveH798N/DO74YmIiLwlneHBrgeingT+0K39wSGPRkREsiYX6mmZWSnwj25N04HfuPt/p3N8OvW0bhxkbCIikqYX9tm3Tz2tfV98YcTV03L3bQQrw3ft9yRwZ7rnTac0yXNhvZSUX+l+kIiIpBYmrD71tML2Qcv1elrhuSfRs+fVr3SGB08Mv58bfu+68NPpu8CjiIhkrr96WoPqbXWrp3W4u28MF8z9QhqHdtXT+q2ZjQESBPW05nct29ernpYBS8J6WmsI6ml90t3PSeOzTgN+7+muJ0h6w4OrwyAPd/fDu2260MweAa5I98NERCSlYamnlWatxUeBi81sOnCnu7+S4rju9bQASgiS2BrSq6fV5VQyqKUFmU15Lzazd3a9MbN3AMUDHWRmi8zsJTNbaWYX9rPfKWbmXd1VEZFRZGd1syKppwWcBDQTrMZ+9E7O/e2wkvECd9/T3a8Ltw1YTwvAzA4Aku7+ZDr7d8kkaX0auMrMXjez1whuyH1qgKASwFXA8cA84DQzm5div1KCbuvjGcQjIjJSjJp6Wt2cBvwuw2PST1ru/qS7H0BwAV3Z9akBDjsYWOnuq8J1Cm8BTk6x3zeA7wIt6cYjIjJShLME+9TT2pXZgzlcT6vLRxhE0sqkntZkgpuCU939+LDHdFi3LmGqY04BFrn7Z8L3ZxLU4jqv2z4LgUvc/UNm9iBwvrv3KZZlZmcDZwPMnDnzoNWrV6d7jSIiw0n1tLIok+HBGwi6hFPD9y8DAz0MluqHtyNLmlke8EPgKwN9uLsvdvcqd6+aOHFiWgFLPLTX1dOxbVvUYYhIDGSyYG6lu99qZl8DcPd2M+sY4Jhqes7Tn07PwpGlwHzgwXB2yhSCqZMnpeptycjStnET21e9xuYbbyBRUUHl2WeTmDCeRElJ1KGJyBCIup5WY3hDz8NgDgW2DHDMUmCumc0G3iCY3rjjYTl330K3sdT+hgdl5Nn+6qusOeusHe+33XMPc+6+W0lLZISItJ4W8GWCmSRzwuezfg38V38HuHs7cB7BsOILwK3u/ryZXWFmJw0yZhkB2jZtZvP11/do62xspPFf6T7eISKjUSY9rRUEC+Y2EUx//CPBfa1+uftfgL/0art0J/selUE8EmOWTJCXokeVV5bpBCQRGU0y6Wn9mmD64/8CPyV4+vmmfo8Q2YlkeTmV55yDFRbuaBszezaFB7wtwqhEJNdl0tPaO3xOq8sD4dx/kUHJmzieOX/+Mw0PPUxy3DgKD1xI/iTNDBWRncskaT1tZod2rSllZocAj2QnLBkN8kvLobSc8ad9NOpQREaFXKinFZ7vHmA3ghz0D+Bcdx9oNjqQXuXi5whmDOYDHzezNeH73Qnuc4mIyC666nN/71NP69xfHD3i6mmFPuLuW8N9bgc+TLBi0oDSuad1IvA+YBEwGzgSOCp8/d50PkRERHYuTFh96mmF7YOWq/W03H1r+DIJjKH/hX17SLs0iYiIZM2oq6dlZveGx/+VoLeVlkxmD4qISHYMSz2tNI97FLjIzL4K7O7uzSn26V5P6ymCmeVzw21p1dNy9/cQ3NcqCGNNi5KWiEj0Rl09rfCzWggWrUhV/SMlJS0RkeiNmnpaZlZiZruFr5PACcCL6V6UkpaISMTCWYJ96mntyuzBHK6nVUxwD+xZ4BmgBvhFuteVdj2tXFJVVeXLlmlNXRHJSaqnlUXqaYmISGxksiKGiIhI2qKupyUiIpK2qOtpiYiIREpJS0REYkNJS0REYkNJS0REYkNJS0RklDCzy83s/EEcV2Fm/S6Am+H5xpjZYjN72cxeNLMPpXusZg+KiOSAH3z0xD71tL7y+7tHaj2ti4Ead9/LzPKA3ktM7ZR6WiIiEQsTVp96WmH7oOVqPS3gU8C3Ady9s2sl+nQoaYmIRK+/elqD0q2e1tHufgDwxTQP7aqntQCoAqoJ6mm9Gq7ofkGveloLgIPCeloQ1NP6tbsvTFWP0cwqwpffMLOnzOw2M5uc7nUpaYmIRG801dNKAtOBR9z9wPDzvp9mbEpaIiI5YDTV09pEUHblD+H724ADBzhmByUtEZHojZp6Wh6UFvkTcFTYdAywIt2LUtISEYlYOEuwTz2tXZk9mMP1tAC+Clwe1tQ6E/hKugeqnpaIyNBSPa0sUk9LRERiQw8Xi4hIVqieloiIxIbqaYmIyKimpCUiIrGhpDUKtTU30dbYEHUYIiIZ0z2tUaStsZlEaw2JR36CtWyi4+Bz6Sibw5hxE6IOTUQkLeppjSKJtjryFr+LvCd/iT3/BxLXH0ui/uWowxKRYZJD9bS+ZWZrzSzjIR/1tEaRzlcfJq9lS4+2xKM/pG3CvuSXVezkKBEZDtUX/qNPPa3p33nXSK2n9SfgZ8ArmQaintZoUlDSp6lzTBmep78GIlEKE1afelph+6Dlaj0td3/M3d8czDXpt9UokjejCuWZZesAAA+SSURBVMbPeashORaO+P8YU1IWXVAiAqOontau0vDgKJJXPoXOs/5K56p/QNMm8vY9gbbkuD6Pq4vIsBuWelrBiN2AHgUuNrPpwJ3u/kqK47rX0wIoIUhiaxi4ntYuUdIaZfLKp5C38MM73ithieSENQRDgqnaB2vQ9bTC5ZfeS1BP6zPAqhTn/ra7X9Oj0WwWA9fT2iUaHhQRid6oqae1q5S0REQiFs4S7FNPa1dmD+ZyPS0z+66ZVQNFZlZtZpenfazqaYmIDCnV08oi9bRERCQ2NBFjhNje2EJibD6JRCLqUEREgJjW0zKzRcCPgQTwS3f/Tq/tXwY+QzCTpRb4VDbm9o9UzVuaWP1cLa+v2Mr0uSXMWTiZoorej3uIiAy/bNTTymrSMrMEcBXwboIH1Jaa2RJ3X9Ftt6eBKndvMrPPA98luBEoA2jZ0shjd73Gin/VAPDqU7WsfWkrR526B4UVfVe/EBGJu2zf0zoYWOnuq9x9O3ALcHL3Hdz9AXfvmur5GDA9yzGNGO0d8OJjtT3aVi3fRHuH7gOLyMiU7aQ1DVjb7X112LYznwb+mtWIRpi8RM8EZXlGeg+9i4jET7aTVqpfnynn2JvZGQTrXH1vJ9vPNrNlZrastrY21S6jTn6+ceC7p/Zo2/+IySQT8XuMQUQkHdmeiFFNz1V+pwPreu9kZscSLOx4pLu3pjqRuy8GFkPwnNbQhxo/BaVFzH/XbszYdzxrX9jM1LkVjNutiLHlup8lIiNTtpPWUmCumc0G3gBOBXostW9mC4FrgEXuXpPleEacwnGlFI4rZcrcyoF3FhGJuawOD7p7O3AewTpVLwC3uvvzZnaFmZ0U7vY9ghWCbwtrtSzJZkwiIhJfWsZJRGRoaSpUFmkZJxERiQ0lrVzV0QadndDRAY2aLSkiAlp7MCe1b9xAR109dbfeTnLCOMrf/37yx7RBfn7UoYmIREpJKwe1rXuT1089PehpAXU3/55Zt91CflkhFFZEHJ2ISHQ0PJhj2jfVsvHqxTsSFkB7TQ3NTz8FyeIIIxMRiZ6SVkyY1mYSEVHSyjXJCROp/PzZkPfWjyY5aRJjFxyoe1oiMurpnlYOSk7djTlL/kD9bbeTmDCe8pNOJn/ylKjDEhGJnB4ujlhnZyedHZ0k8/X/B5ERQmP5WaTflBFpb2nBm6HhsTfxpjaKD5tKZ3GCwvLCqEMTEclZSloR8Rao/enTdDa1A9C0bAOVnz8AlLRERHZKEzEi0vxK/Y6EBYBDw0PVtG5NWZlFRERQ0oqMJVIMe+eZRsNFRPqhpBWRsXMqSJSNeashYZT+xwwKSguiC0pEJMfpnlZE8isKqDxnAU3P1dLZ2E7xQZPoHKv/Q4iI9EdJaxh0dHTQ0dzKmJKiHu35FQWUv2t6RFGJiMSPklaWNdU18dJjb7JhbRN77D+OaXuPo2i81hAUERkMJa0satq0jXuvf5l1K7cA8OpTtRx47DQOPG46BWVKXCIimdJNlCxq67AdCavLsw+/SVtbRAGJiMScklYW5aVYmT2RnwcxXDpLRCQXKGllUcI6mHtQZY+2Q46fQb5mCYqIDIruaWVRUWUZh39oD/Y+eBIbXtvK7vtXUlqepKDXLEIREUmPklaWFY8vpnh8MbsfoNIiIiK7SuNUIiISG0paIiISG0paIiISG0paIiISG0paIiISG0paIiISG0paGWrZ2kjLtqaowxARGZX0nFaamuq2sW3zdp687w0SCag6YXeKyxKMLSuJOjQRkVFDSStNTVvbuf37z0C4bOCqZzbxscveztiyaOMSERlNNDyYhrbW7Tz70LodCQugs8N55fF10QUlIjIKKWmlIZHIo7A40ad9bEl+BNGIiIxeSlppyEsmmX/UDMYWv5WkSsePZfaCyRFGJSIy+uieVpoKS5KceslBvPHSRhKJPKbsOZ7icVqtXURkOClppSlZUECyAPY6dGbUoYiIjFoaHhQRkdhQ0hIRkdhQ0hIRkdhQ0hIRkdhQ0hIRkdhQ0hIRkdgYtVPeG+saaG+DvDwjkeikaFxp1CGJiMgARmXSaqpv4q+LX2TDa1sB2OeQSg57/xyKxmnFdhGRXDbqhgfbtrdRW93Iltq3amK9+PhG6jeoRpaISK7LetIys0Vm9pKZrTSzC1NsLzCz34fbHzezWdmKpaGuhXUvb6G+poUPnl/FUafvvWNbzeqt2fpYEREZIlkdHjSzBHAV8G6gGlhqZkvcfUW33T4N1Ln7nmZ2KnAl8NGhjqWhroX7r1/BupfrAcjLW8n7vriAuW+fxCtLa5gxr3KoP1JERIZYtntaBwMr3X2Vu28HbgFO7rXPycCN4evbgWPMzIY6kOZtbTsSFkBnp/P4Xa+y/1HTOfqMPSgs6Vt6REREcku2k9Y0YG2399VhW8p93L0d2AJM6H0iMzvbzJaZ2bLa2tqMA2lr7ejTtr25g+LyAvY4aLJmD4qIxEC2k1aqHpMPYh/cfbG7V7l71cSJEzMOpKxyLMUVBT3a5h85lcLSJGMKx2Z8PhERGX7ZnvJeDczo9n460LtGfdc+1WaWBMqBzUMdSMm4sXzwggN5+r41bK1tZp/DdmPqnhXkF6j6sIhIXGQ7aS0F5prZbOAN4FTgY732WQKcBTwKnAL83d379LSGQtmEQg49eRYd252iCvWuRETiJqtJy93bzew84F4gAfzK3Z83syuAZe6+BLgOuMnMVhL0sE7NZkwFRQWggsMiIrFkWerUZFVVVZUvW7Ys6jBERFIZ8tnP8pZRtyKGiIjEl5KWiIjEhpKWiIjEhpKWiIjEhpKWiIjEhpKWiIjEhpKWiIjEhpKWiIjEhpKWiIjEhpKWiIjEhpKWiIjERizXHjSzWmD1LpyiEtg4ROHkCl1T7htp1wO6plQ2uvuioQpGeopl0tpVZrbM3auijmMo6Zpy30i7HtA1yfDT8KCIiMSGkpaIiMTGaE1ai6MOIAt0TblvpF0P6JpkmI3Ke1oiIhJPo7WnJSIiMaSkJSIisTGik5aZLTKzl8xspZldmGJ7gZn9Ptz+uJnNGv4oM5PGNX3ZzFaY2bNm9jcz2z2KONM10PV02+8UM3Mzy/mpyOlck5l9JPw5PW9mNw93jJlK4+/dTDN7wMyeDv/unRBFnOkys1+ZWY2Z/Xsn283MfhJe77NmduBwxyg74e4j8gtIAK8Cc4AxwDPAvF77nAP8Inx9KvD7qOMegmv6D6AofP35XL6mdK4n3K8UeBh4DKiKOu4h+BnNBZ4GxoXvJ0Ud9xBc02Lg8+HrecDrUcc9wDUdARwI/Hsn208A/goYcCjweNQx6yv4Gsk9rYOBle6+yt23A7cAJ/fa52TgxvD17cAxZmbDGGOmBrwmd3/A3ZvCt48B04c5xkyk8zMC+AbwXaBlOIMbpHSu6bPAVe5eB+DuNcMcY6bSuSYHysLX5cC6YYwvY+7+MLC5n11OBn7tgceACjPbbXiik/6M5KQ1DVjb7X112JZyH3dvB7YAE4YlusFJ55q6+zTB/xZz1YDXY2YLgRnufvdwBrYL0vkZ7QXsZWaPmNljZpbrS/6kc02XA2eYWTXwF+C/hie0rMn035oMk2TUAWRRqh5T7/n96eyTS9KO18zOAKqAI7Ma0a7p93rMLA/4IfCJ4QpoCKTzM0oSDBEeRdAT/oeZzXf3+izHNljpXNNpwA3u/gMzOwy4KbymzuyHlxVx+90waozknlY1MKPb++n0HbLYsY+ZJQmGNfobMohaOteEmR0LXAyc5O6twxTbYAx0PaXAfOBBM3ud4N7CkhyfjJHu37u73L3N3V8DXiJIYrkqnWv6NHArgLs/CowlWHg2rtL6tybDbyQnraXAXDObbWZjCCZaLOm1zxLgrPD1KcDf3T2X/zc14DWFw2nXECSsXL9X0u/1uPsWd69091nuPovgHt1J7r4smnDTks7fuz8STJjBzCoJhgtXDWuUmUnnmtYAxwCY2b4ESat2WKMcWkuAj4ezCA8Ftrj7m1EHJSN4eNDd283sPOBegtlPv3L3583sCmCZuy8BriMYxlhJ0MM6NbqIB5bmNX0PKAFuC+eUrHH3kyILuh9pXk+spHlN9wLHmdkKoAO4wN03RRd1/9K8pq8A15rZlwiG0T6Ry/8BNLPfEQzPVob34S4D8gHc/RcE9+VOAFYCTcAno4lUetMyTiIiEhsjeXhQRERGGCUtERGJDSUtERGJDSUtERGJDSUtERGJDSUtERGJDSUtGXZmNmtnJSEyOdbMPmFmP8vw+IsGG4eZXRGuNpLJ570ePkAsIkNASUtGm4sG3iU1d7/U3f9vKIMRkcwoaUlUkmZ2Y1hg73YzKzKzg8zsITN70szu7SoFEbY/Y2aPAuf2Os8MM7snLFB4WVejmf0xPM/zZnZ22PYdoNDMlpvZb8NdE2Z2bbjffWZWuLOAzewGMzslfP26mX3dzJ4ys+fMbJ+wfUJ4nqfN7Bq6LbxqZmeY2RPh519jZgkz293MXjGzSjPLM7N/mNlxQ/DnKzIiKWlJVPYGFrv724CtBMnop8Ap7n4Q8CvgW+G+1wNfcPfDUpznYOB0YAHw4W6L6X4qPE8V8AUzm+DuFwLN7r7A3U8P95tLUNtqP6Ae+FAG17DR3Q8ErgbOD9suA/7p7gsJ1q+bCTvW4/socLi7LyBYvul0d18NXAn8gmAppBXufl8GMYiMKiN27UHJeWvd/ZHw9W8Ihu3mA/eHayYmgDfNrByocPeHwn1vAo7vdp77u9btM7M7gXcCywgS1QfCfWYQJKdU6/u95u7Lw9dPArMyuIY7ux33wfD1EV2v3f3PZlYXth8DHAQsDa+vEKgJ9/ulmX0Y+BxB8hWRnVDSkqj0XvRyG/B8796UmVWk2Le/87iZHQUcCxzm7k1m9iDBquOpdC/d0kGQTNLVdWwHPf8tpYrXgBvd/Wt9NpgV8VaF6RKCPwsRSUHDgxKVmWGxQAgKCD4GTOxqM7N8M9svLIy4xczeGe57eq/zvNvMxof3ot4PPEJQF60uTFj7ENTh6tJmZvnZuijg4a4Yzex4YFzY/jfgFDObFG4bb2a7h9uuBH4LXApcm8XYRGJPSUui8gJwlpk9C4wnvJ8FXGlmzwDLgXeE+34SuCqciNHc6zz/JBgyXA7cEdbauodgosezwDcIEmKXxcCz3SZiDLWvA0eY2VPAcQR1pnD3FcAlwH1hXPcDu5nZkcDbgSvd/bfAdjNTGQyRnVBpEhERiQ31tEREJDY0EUOkFzO7Cji8V/OP3f36KOIRkbdoeFBERGJDw4MiIhIbSloiIhIbSloiIhIbSloiIhIb/w+z8IarnWRsMQAAAABJRU5ErkJggg==\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    },
    {
     "data": {
      "image/png": "...\n",
      "text/plain": [
       "<Figure size 441.5x360 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "train['cluster'] = kmeans2.labels_\n",
    "train.cluster = 'cluster_' + (train.cluster + 1).astype('str')\n",
    "\n",
    "for i in range(0,len(cluster2_cols)):\n",
    "    for j in range(0, len(cluster2_cols)):\n",
    "        sns.relplot(data=train, x=cluster2_cols[i], y=cluster2_cols[j], hue='cluster')"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### Feature Selection"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### Which variables and clusters give information about logerror?\n",
    "\n",
    "First, I need to confirm that 'logerror' is normally distributed, to determine if I can run t-tests to test the differences in means across different clusters. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 68,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "image/png": "iVBORw0KGgoAAAANSUhEUgAAAX0AAAD4CAYAAAAAczaOAAAABHNCSVQICAgIfAhkiAAAAAlwSFlzAAALEgAACxIB0t1+/AAAADh0RVh0U29mdHdhcmUAbWF0cGxvdGxpYiB2ZXJzaW9uMy4xLjAsIGh0dHA6Ly9tYXRwbG90bGliLm9yZy+17YcXAAAR/UlEQVR4nO3db6xc9Z3f8fdnDUlWTVpMuUmp7dRo692GbLtOdAtIPGgaEjAkWrPSRoKqiZWm8lYFKZGybU32AbtJkajaDVXULJVT3DhttBRtssICb1kvm9UqD/hzyRqCcSi3hIYbu3C3JiRRVCrotw/m52Vi5t479/p6xu7v/ZJG95zv+Z2Z7xlZnzn+zZmZVBWSpD78zLQbkCRNjqEvSR0x9CWpI4a+JHXE0Jekjpw37QaWc9FFF9XWrVun3YYknVMee+yxP6+qmVHbzurQ37p1K3Nzc9NuQ5LOKUn+x1LbnN6RpI4Y+pLUEUNfkjpi6EtSRwx9SeqIoS9JHTH0Jakjhr4kdcTQl6SOGPqS1BFDX5I6YuhLUkcMfUnqiKEvSR0x9CWpI4a+JHXE0Jekjhj6ktQRQ1+SOmLoS1JHDH1J6oihL0kdWTH0k7wlySNJHk9yJMlvtfqXk3w3yeF2297qSfKFJPNJnkjy3qH72pXkmXbbdeYOS5I0ynljjHkFeH9V/TjJ+cA3k/xB2/bPqur3Thl/LbCt3S4H7gQuT3IhcCswCxTwWJIDVfXSehyIJGllK57p18CP2+r57VbL7LIT+Erb7yHggiQXA9cAh6rqRAv6Q8CO02tfkrQaY83pJ9mQ5DDwIoPgfrhtuq1N4dyR5M2ttgl4fmj3hVZbqn7qY+1OMpdkbnFxcZWHI0lazlihX1WvVdV2YDNwWZJfBG4B/hbwd4ELgX/RhmfUXSxTP/Wx9lbVbFXNzszMjNOeJGlMq7p6p6p+APwJsKOqjrcpnFeA/whc1oYtAFuGdtsMHFumLkmakHGu3plJckFb/lngA8B32jw9SQJcDzzZdjkAfKxdxXMF8HJVHQceAK5OsjHJRuDqVpMkTcg4V+9cDOxPsoHBi8Q9VXVfkj9OMsNg2uYw8E/a+IPAdcA88BPg4wBVdSLJ54BH27jPVtWJ9TsUSdJKUrXchTjTNTs7W3Nzc9NuQ5LOKUkeq6rZUdv8RK4kdcTQl07D1j33T7sFaVUMfUnqiKEvSR0x9CWpI4a+JHXE0Jekjhj6ktQRQ1+SOmLoS1JHDH1J6oihL0kdMfQlqSOGviR1xNCXpI4Y+pLUEUNfkjpi6EtSR8b5YfS3JHkkyeNJjiT5rVa/JMnDSZ5J8l+SvKnV39zW59v2rUP3dUurP53kmjN1UJKk0cY5038FeH9V/RKwHdiR5ArgXwF3VNU24CXgE238J4CXqupvAne0cSS5FLgBeDewA/id9mPrkqQJWTH0a+DHbfX8divg/cDvtfp+4Pq2vLOt07ZflSStfndVvVJV3wXmgcvW5SgkSWMZa04/yYYkh4EXgUPAfwd+UFWvtiELwKa2vAl4HqBtfxn4q8P1EfsMP9buJHNJ5hYXF1d/RJKkJY0V+lX1WlVtBzYzODt/16hh7W+W2LZU/dTH2ltVs1U1OzMzM057kqQxrerqnar6AfAnwBXABUnOa5s2A8fa8gKwBaBt/yvAieH6iH0kSRMwztU7M0kuaMs/C3wAOAp8A/jVNmwXcG9bPtDWadv/uKqq1W9oV/dcAmwDHlmvA5Ekrey8lYdwMbC/XWnzM8A9VXVfkqeAu5P8S+DPgLva+LuA/5RknsEZ/g0AVXUkyT3AU8CrwE1V9dr6Ho4kaTkrhn5VPQG8Z0T9WUZcfVNV/xv4yBL3dRtw2+rblCStBz+RK0kdMfQlqSOGviR1xNCXpI4Y+pLUEUNfkjpi6EtSRwx9SeqIoS9JHTH0Jakjhr4kdcTQl6SOGPqS1BFDX5I6YuhLUkcMfUnqiKEvSR0x9CWpI+P8MPqWJN9IcjTJkSSfbPXfTPL9JIfb7bqhfW5JMp/k6STXDNV3tNp8kj1n5pAkSUsZ54fRXwU+XVXfSvI24LEkh9q2O6rq3wwPTnIpgx9Dfzfw14E/SvLzbfMXgQ8CC8CjSQ5U1VPrcSCSpJWN88Pox4HjbflHSY4Cm5bZZSdwd1W9Anw3yTyv/4D6fPtBdZLc3cYa+pI0Iaua00+yFXgP8HAr3ZzkiST7kmxstU3A80O7LbTaUvVTH2N3krkkc4uLi6tpT5K0grFDP8lbga8Bn6qqHwJ3Aj8HbGfwP4HfPjl0xO61TP2nC1V7q2q2qmZnZmbGbU+SNIZx5vRJcj6DwP9qVX0doKpeGNr+JeC+troAbBnafTNwrC0vVZckTcA4V+8EuAs4WlWfH6pfPDTsV4An2/IB4IYkb05yCbANeAR4FNiW5JIkb2LwZu+B9TkMSdI4xjnTvxL4KPDtJIdb7TPAjUm2M5iieQ74NYCqOpLkHgZv0L4K3FRVrwEkuRl4ANgA7KuqI+t4LJKkFYxz9c43GT0ff3CZfW4DbhtRP7jcfpKkM8tP5EpSRwx9SeqIoS9JHTH0Jakjhr4kdcTQl6SOGPqS1BFDX5I6YuhLUkcMfUnqiKEvSR0x9CWpI4a+JHXE0JfWaOue+6fdgrRqhr4kdcTQl6SOGPrSaXKaR+cSQ1+SOjLOD6NvSfKNJEeTHEnyyVa/MMmhJM+0vxtbPUm+kGQ+yRNJ3jt0X7va+GeS7DpzhyVJGmWcM/1XgU9X1buAK4CbklwK7AEerKptwINtHeBaYFu77QbuhMGLBHArcDlwGXDryRcKSdJkrBj6VXW8qr7Vln8EHAU2ATuB/W3YfuD6trwT+EoNPARckORi4BrgUFWdqKqXgEPAjnU9GknSslY1p59kK/Ae4GHgHVV1HAYvDMDb27BNwPNDuy202lJ1SdKEjB36Sd4KfA34VFX9cLmhI2q1TP3Ux9mdZC7J3OLi4rjtSZLGMFboJzmfQeB/taq+3sovtGkb2t8XW30B2DK0+2bg2DL1n1JVe6tqtqpmZ2ZmVnMskqQVjHP1ToC7gKNV9fmhTQeAk1fg7ALuHap/rF3FcwXwcpv+eQC4OsnG9gbu1a0mSZqQ88YYcyXwUeDbSQ632meA24F7knwC+B7wkbbtIHAdMA/8BPg4QFWdSPI54NE27rNVdWJdjkKSNJYVQ7+qvsno+XiAq0aML+CmJe5rH7BvNQ1KktaPn8iVpI4Y+pLUEUNfkjpi6EtSRwx9SeqIoS9JHTH0Jakjhr4kdcTQl6SOGPqS1BFDX5I6YuhLUkcMfUnqiKEvSR0x9CWpI4a+JHXE0Jekjhj6ktQRQ1+SOrJi6CfZl+TFJE8O1X4zyfeTHG6364a23ZJkPsnTSa4Zqu9otfkke9b/UCRJKxnnTP/LwI4R9Tuqanu7HQRIcilwA/Duts/vJNmQZAPwReBa4FLgxjZWkjRB5600oKr+NMnWMe9vJ3B3Vb0CfDfJPHBZ2zZfVc8CJLm7jX1q1R1LktbsdOb0b07yRJv+2dhqm4Dnh8YstNpS9TdIsjvJXJK5xcXF02hPknSqtYb+ncDPAduB48Bvt3pGjK1l6m8sVu2tqtmqmp2ZmVlje5KkUVac3hmlql44uZzkS8B9bXUB2DI0dDNwrC0vVZckTciazvSTXDy0+ivAySt7DgA3JHlzkkuAbcAjwKPAtiSXJHkTgzd7D6y9bUnSWqx4pp/kd4H3ARclWQBuBd6XZDuDKZrngF8DqKojSe5h8Abtq8BNVfVau5+bgQeADcC+qjqy7kcjSVrWOFfv3DiifNcy428DbhtRPwgcXFV3kqR15SdyJakjhr4kdcTQl6SOGPqS1BFDX5I6YuhLUkcMfUnqiKEvSR0x9CWpI4a+JHXE0Jekjhj6ktQRQ1+SOmLoS1JHDH1J6oihL0kdMfQlqSOGviR1ZMXQT7IvyYtJnhyqXZjkUJJn2t+NrZ4kX0gyn+SJJO8d2mdXG/9Mkl1n5nCk6di65/5ptyCNZZwz/S8DO06p7QEerKptwINtHeBaYFu77QbuhMGLBIMfVL8cuAy49eQLhSRpclYM/ar6U+DEKeWdwP62vB+4fqj+lRp4CLggycXANcChqjpRVS8Bh3jjC4kk6Qxb65z+O6rqOED7+/ZW3wQ8PzRuodWWqr9Bkt1J5pLMLS4urrE9SdIo6/1GbkbUapn6G4tVe6tqtqpmZ2Zm1rU5SerdWkP/hTZtQ/v7YqsvAFuGxm0Gji1TlyRN0FpD/wBw8gqcXcC9Q/WPtat4rgBebtM/DwBXJ9nY3sC9utUkSRN03koDkvwu8D7goiQLDK7CuR24J8kngO8BH2nDDwLXAfPAT4CPA1TViSSfAx5t4z5bVae+OSxJOsNWDP2qunGJTVeNGFvATUvczz5g36q6kyStKz+RK62BH8bSucrQl6SOGPqS1BFDX5I6YuhLUkcMfUnqiKEvSR0x9CWpI4a+JHXE0Jekjhj6ktQRQ1+SOmLoS1JHDH1J6oihL0kdMfQlqSOGviR1xNCXpI6cVugneS7Jt5McTjLXahcmOZTkmfZ3Y6snyReSzCd5Isl71+MAJEnjW48z/b9fVdurarat7wEerKptwINtHeBaYFu77QbuXIfHliStwpmY3tkJ7G/L+4Hrh+pfqYGHgAuSXHwGHl+StITTDf0C/jDJY0l2t9o7quo4QPv79lbfBDw/tO9Cq0mSJuS809z/yqo6luTtwKEk31lmbEbU6g2DBi8euwHe+c53nmZ7kqRhp3WmX1XH2t8Xgd8HLgNeODlt0/6+2IYvAFuGdt8MHBtxn3uraraqZmdmZk6nPUnSKdYc+kn+UpK3nVwGrgaeBA4Au9qwXcC9bfkA8LF2Fc8VwMsnp4EkSZNxOmf67wC+meRx4BHg/qr6r8DtwAeTPAN8sK0DHASeBeaBLwH/9DQeWzrrbN1z/7RbkFa05jn9qnoW+KUR9f8FXDWiXsBNa3086WxhuOtc5idyJakjhr4kdcTQl6SOGPqS1BFDX5I6YuhLq+CVOzrXGfqS1BFDX5I6YuhL68jpH53tDH1J6oihL0kdMfQlqSOGviR1xNCX1plv5upsZuhLYzLM9f8DQ18aw2oD3xcIna0MfUnqiKEvrWCtZ+1b99zvGb/OOoa+JHVk4qGfZEeSp5PMJ9kz6ceXVmM9ztQ949fZZM0/jL4WSTYAXwQ+CCwAjyY5UFVPTbIPaTlnKqC37rmf527/0Bm5b2lcEw194DJgvqqeBUhyN7ATMPQ1cdM4+17uMZ+7/UN/8cJwctyoZV84dDpSVZN7sORXgR1V9Y/b+keBy6vq5qExu4HdbfUXgKcn1uDKLgL+fNpNnCV8LgZ8Hl7nc/G6aT8Xf6OqZkZtmPSZfkbUfupVp6r2Ansn087qJJmrqtlp93E28LkY8Hl4nc/F687m52LSb+QuAFuG1jcDxybcgyR1a9Kh/yiwLcklSd4E3AAcmHAPktStiU7vVNWrSW4GHgA2APuq6sgkezhNZ+W005T4XAz4PLzO5+J1Z+1zMdE3ciVJ0+UnciWpI4a+JHXE0F+jJL+epJJcNO1epiHJv07ynSRPJPn9JBdMu6dJ8ytFBpJsSfKNJEeTHEnyyWn3NE1JNiT5syT3TbuXUQz9NUiyhcFXSXxv2r1M0SHgF6vq7wD/Dbhlyv1M1NBXilwLXArcmOTS6XY1Na8Cn66qdwFXADd1/FwAfBI4Ou0mlmLor80dwD/nlA+W9aSq/rCqXm2rDzH4zEVP/uIrRarq/wAnv1KkO1V1vKq+1ZZ/xCDwNk23q+lIshn4EPAfpt3LUgz9VUryy8D3q+rxafdyFvlHwB9Mu4kJ2wQ8P7S+QKdBNyzJVuA9wMPT7WRq/i2DE8L/O+1GljLpr2E4JyT5I+Cvjdj0G8BngKsn29F0LPc8VNW9bcxvMPjv/Vcn2dtZYMWvFOlNkrcCXwM+VVU/nHY/k5bkw8CLVfVYkvdNu5+lGPojVNUHRtWT/G3gEuDxJDCY0vhWksuq6n9OsMWJWOp5OCnJLuDDwFXV3wc+/EqRIUnOZxD4X62qr0+7nym5EvjlJNcBbwH+cpL/XFX/cMp9/RQ/nHUakjwHzFZVd98smGQH8Hng71XV4rT7mbQk5zF4A/sq4PsMvmLkH5xjnzBfFxmcAe0HTlTVp6bdz9mgnen/elV9eNq9nMo5fa3VvwPeBhxKcjjJv592Q5PU3sQ++ZUiR4F7egz85krgo8D727+Fw+1sV2chz/QlqSOe6UtSRwx9SeqIoS9JHTH0Jakjhr4kdcTQl6SOGPqS1JH/Bxzy+GgBqWLRAAAAAElFTkSuQmCC\n",
      "text/plain": [
       "<Figure size 432x288 with 1 Axes>"
      ]
     },
     "metadata": {
      "needs_background": "light"
     },
     "output_type": "display_data"
    }
   ],
   "source": [
    "plt.hist(train.logerror, bins=1000)\n",
    "plt.show()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Looks good!"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Test:** Home driven clusters\n",
    "\n",
    "First, let's look at the mean log error by cluster id. We will do this for both the train and test as more of a data quality check...to confirm that our cluster id's are showing similar results in both samples. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 71,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "4    7767\n",
       "2    6118\n",
       "6    6020\n",
       "0    5871\n",
       "3    5569\n",
       "1    5259\n",
       "5    4289\n",
       "Name: cluster_home, dtype: int64"
      ]
     },
     "execution_count": 71,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train.cluster_home.value_counts()"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 69,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "   cluster_home  logerror\n",
      "0             0  0.005005\n",
      "1             1  0.014288\n",
      "2             2  0.004163\n",
      "3             3  0.010781\n",
      "4             4  0.024821\n",
      "5             5  0.011449\n",
      "6             6  0.010718\n",
      "   cluster_home  logerror\n",
      "0             0  0.002514\n",
      "1             1  0.013325\n",
      "2             2  0.000336\n",
      "3             3  0.013832\n",
      "4             4  0.019181\n",
      "5             5  0.013464\n",
      "6             6  0.011169\n"
     ]
    }
   ],
   "source": [
    "print(pd.DataFrame(train.groupby(['cluster_home'])['logerror'].mean().reset_index()))\n",
    "print(pd.DataFrame(test.groupby(['cluster_home'])['logerror'].mean().reset_index()))"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Test the different in the mean logerror for each cluster vs all others. When the p-value is < .05 then we keep the cluster id, else we replace the cluster id with -1. "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 70,
   "metadata": {},
   "outputs": [],
   "source": [
    "import scipy as sp\n",
    "import numpy as np\n",
    "\n",
    "less_significant_clusters = []\n",
    "\n",
    "for i in range(0,max(train.cluster_home)+1):\n",
    "    stat, pval = sp.stats.ttest_ind(\n",
    "        train[train.cluster_home == i].logerror.dropna(),\n",
    "        train[train.cluster_home != i].logerror.dropna())\n",
    "    if pval > .05:\n",
    "        less_significant_clusters = less_significant_clusters + [i]\n",
    "\n",
    "        "
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 75,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "[1, 3, 5, 6]"
      ]
     },
     "execution_count": 75,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "less_significant_clusters"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 72,
   "metadata": {},
   "outputs": [],
   "source": [
    "train.cluster_home = train.cluster_home.replace(less_significant_clusters, -1)\n",
    "test.cluster_home = test.cluster_home.replace(less_significant_clusters, -1)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 73,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "-1    8953\n",
       " 4    3418\n",
       " 2    2578\n",
       " 0    2577\n",
       "Name: cluster_home, dtype: int64"
      ]
     },
     "execution_count": 73,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "test.cluster_home.value_counts()"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 74,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "-1    21137\n",
       " 4     7767\n",
       " 2     6118\n",
       " 0     5871\n",
       "Name: cluster_home, dtype: int64"
      ]
     },
     "execution_count": 74,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train.cluster_home.value_counts()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Test:** Location driven clusters"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 76,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>cluster_loc</th>\n",
       "      <th>logerror</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>0</th>\n",
       "      <td>0</td>\n",
       "      <td>0.015151</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1</th>\n",
       "      <td>1</td>\n",
       "      <td>0.011431</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>2</th>\n",
       "      <td>2</td>\n",
       "      <td>0.011161</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>3</th>\n",
       "      <td>3</td>\n",
       "      <td>0.017595</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>4</th>\n",
       "      <td>4</td>\n",
       "      <td>0.014994</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>5</th>\n",
       "      <td>5</td>\n",
       "      <td>0.010282</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>6</th>\n",
       "      <td>6</td>\n",
       "      <td>0.002305</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>7</th>\n",
       "      <td>7</td>\n",
       "      <td>0.013613</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "   cluster_loc  logerror\n",
       "0            0  0.015151\n",
       "1            1  0.011431\n",
       "2            2  0.011161\n",
       "3            3  0.017595\n",
       "4            4  0.014994\n",
       "5            5  0.010282\n",
       "6            6  0.002305\n",
       "7            7  0.013613"
      ]
     },
     "execution_count": 76,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "pd.DataFrame(train.groupby(['cluster_loc'])['logerror'].mean().reset_index())"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 77,
   "metadata": {},
   "outputs": [],
   "source": [
    "less_significant_clusters = []\n",
    "\n",
    "for i in range(0,max(train.cluster_loc)+1):\n",
    "    stat, pval = sp.stats.ttest_ind(\n",
    "        train[train.cluster_loc == i].logerror.dropna(),\n",
    "        train[train.cluster_loc != i].logerror.dropna())\n",
    "    if pval > .05:\n",
    "        less_significant_clusters = less_significant_clusters + [i]"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 78,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "[0, 1, 2, 4, 5, 7]"
      ]
     },
     "execution_count": 78,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "less_significant_clusters"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 79,
   "metadata": {},
   "outputs": [],
   "source": [
    "train.cluster_loc = train.cluster_loc.replace(less_significant_clusters, -1)\n",
    "test.cluster_loc = test.cluster_loc.replace(less_significant_clusters, -1)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Test:** is_taxdelinquent"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 80,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>is_taxdelinquent</th>\n",
       "      <th>logerror</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>0</th>\n",
       "      <td>0.0</td>\n",
       "      <td>0.011800</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1</th>\n",
       "      <td>1.0</td>\n",
       "      <td>0.027048</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "   is_taxdelinquent  logerror\n",
       "0               0.0  0.011800\n",
       "1               1.0  0.027048"
      ]
     },
     "execution_count": 80,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "pd.DataFrame(train.groupby(['is_taxdelinquent'])['logerror'].mean().reset_index())"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 81,
   "metadata": {},
   "outputs": [],
   "source": [
    "stats, pval = sp.stats.ttest_ind(\n",
    "    train[train.is_taxdelinquent == 0].logerror.dropna(),\n",
    "    train[train.is_taxdelinquent == 1].logerror.dropna())\n",
    "\n",
    "if pval > .05:\n",
    "    train.drop(columns=['is_taxdelinquent'], inplace=True)\n",
    "    test.drop(columns=['is_taxdelinquent'], inplace=True)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Data Validation**"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 82,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.0062069273100000336\n"
     ]
    },
    {
     "data": {
      "text/plain": [
       "True"
      ]
     },
     "execution_count": 82,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "print(pval)\n",
    "# if pval < 0.05 then the column should still exist: \n",
    "'is_taxdelinquent' in train.columns"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Results:** is_taxdelinquent was correctly left as feature. \n",
    "\n",
    "_________________________\n",
    "\n",
    "**Test:** has_pool"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 83,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>has_pool</th>\n",
       "      <th>logerror</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>0</th>\n",
       "      <td>0.0</td>\n",
       "      <td>0.013897</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1</th>\n",
       "      <td>1.0</td>\n",
       "      <td>0.005831</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "   has_pool  logerror\n",
       "0       0.0  0.013897\n",
       "1       1.0  0.005831"
      ]
     },
     "execution_count": 83,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "pd.DataFrame(train.groupby(['has_pool'])['logerror'].mean().reset_index())"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 84,
   "metadata": {},
   "outputs": [],
   "source": [
    "stats, pval = sp.stats.ttest_ind(\n",
    "    train[train.has_pool == 0].logerror.dropna(),\n",
    "    train[train.has_pool == 1].logerror.dropna())\n",
    "\n",
    "if pval > .05:\n",
    "    train.drop(columns=['has_pool'], inplace=True)\n",
    "    test.drop(columns=['has_pool'], inplace=True)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Data Validation**"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 85,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "5.1251707281765945e-05\n"
     ]
    },
    {
     "data": {
      "text/plain": [
       "True"
      ]
     },
     "execution_count": 85,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "print(pval)\n",
    "# verify column exists if pval < 0.05, and not if greater\n",
    "'has_pool' in train.columns"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Results:** has_pool was correctly left as feature\n",
    "\n",
    "____________________________ \n",
    "\n",
    "**Test:** has_fireplace"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 86,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>has_fireplace</th>\n",
       "      <th>logerror</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>0</th>\n",
       "      <td>0.0</td>\n",
       "      <td>0.011879</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1</th>\n",
       "      <td>1.0</td>\n",
       "      <td>0.013712</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "   has_fireplace  logerror\n",
       "0            0.0  0.011879\n",
       "1            1.0  0.013712"
      ]
     },
     "execution_count": 86,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "pd.DataFrame(train.groupby(['has_fireplace'])['logerror'].mean().reset_index())"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 87,
   "metadata": {},
   "outputs": [],
   "source": [
    "stats, pval = sp.stats.ttest_ind(\n",
    "    train[train.has_fireplace == 0].logerror.dropna(),\n",
    "    train[train.has_fireplace == 1].logerror.dropna())\n",
    "\n",
    "if pval > .05:\n",
    "    train.drop(columns=['has_fireplace'], inplace=True)\n",
    "    test.drop(columns=['has_fireplace'], inplace=True)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Data Validation**"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 88,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.43614713550643824\n"
     ]
    },
    {
     "data": {
      "text/plain": [
       "False"
      ]
     },
     "execution_count": 88,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "print(pval)\n",
    "# verify column exists if pval < 0.05, and not if greater\n",
    "'has_fireplace' in train.columns"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Results:** has_fireplace was correctly removed\n",
    "_______________________\n",
    "\n",
    "**Test:** has_garage"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 89,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>has_garage</th>\n",
       "      <th>logerror</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>0</th>\n",
       "      <td>0.0</td>\n",
       "      <td>0.010693</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1</th>\n",
       "      <td>1.0</td>\n",
       "      <td>0.014809</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "   has_garage  logerror\n",
       "0         0.0  0.010693\n",
       "1         1.0  0.014809"
      ]
     },
     "execution_count": 89,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "pd.DataFrame(train.groupby(['has_garage'])['logerror'].mean().reset_index())"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 90,
   "metadata": {},
   "outputs": [],
   "source": [
    "stats, pval = sp.stats.ttest_ind(\n",
    "    train[train.has_garage == 0].logerror.dropna(),\n",
    "    train[train.has_garage == 1].logerror.dropna())\n",
    "\n",
    "if pval > .05:\n",
    "    train.drop(columns=['has_garage'], inplace=True)\n",
    "    test.drop(columns=['has_garage'], inplace=True)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Data Validation**"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 91,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.01684256641583778\n"
     ]
    },
    {
     "data": {
      "text/plain": [
       "True"
      ]
     },
     "execution_count": 91,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "print(pval)\n",
    "\n",
    "# verify column exists if pval < 0.05, and not if greater\n",
    "'has_garage' in train.columns\n"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "**Results:** has_garage was correctly left as a feature\n",
    "\n",
    "_______________________\n",
    "\n",
    "**Clean up remaining features**"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 92,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>propertylandusetypeid</th>\n",
       "      <th>regionidcity</th>\n",
       "      <th>regionidcounty</th>\n",
       "      <th>regionidzip</th>\n",
       "      <th>logerror</th>\n",
       "      <th>has_pool</th>\n",
       "      <th>is_taxdelinquent</th>\n",
       "      <th>has_garage</th>\n",
       "      <th>lotsizesquarefeet</th>\n",
       "      <th>structure_dollar_per_sqft</th>\n",
       "      <th>land_dollar_per_sqft</th>\n",
       "      <th>living_area_sqft</th>\n",
       "      <th>tax_rate</th>\n",
       "      <th>bedbath_index</th>\n",
       "      <th>latitude</th>\n",
       "      <th>longitude</th>\n",
       "      <th>age</th>\n",
       "      <th>cluster_loc</th>\n",
       "      <th>cluster</th>\n",
       "      <th>cluster_home</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>60138</th>\n",
       "      <td>261.0</td>\n",
       "      <td>33840</td>\n",
       "      <td>1286</td>\n",
       "      <td>96985</td>\n",
       "      <td>-0.0661</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.088815</td>\n",
       "      <td>0.838465</td>\n",
       "      <td>0.877371</td>\n",
       "      <td>0.824825</td>\n",
       "      <td>0.927847</td>\n",
       "      <td>0.753253</td>\n",
       "      <td>0.101103</td>\n",
       "      <td>0.948192</td>\n",
       "      <td>0.107692</td>\n",
       "      <td>-1</td>\n",
       "      <td>cluster_2</td>\n",
       "      <td>-1</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>79163</th>\n",
       "      <td>261.0</td>\n",
       "      <td>24245</td>\n",
       "      <td>3101</td>\n",
       "      <td>96475</td>\n",
       "      <td>0.0237</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.813012</td>\n",
       "      <td>0.752754</td>\n",
       "      <td>0.203305</td>\n",
       "      <td>0.528028</td>\n",
       "      <td>0.421139</td>\n",
       "      <td>0.136136</td>\n",
       "      <td>0.509108</td>\n",
       "      <td>0.851923</td>\n",
       "      <td>0.269231</td>\n",
       "      <td>-1</td>\n",
       "      <td>cluster_4</td>\n",
       "      <td>-1</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>55204</th>\n",
       "      <td>261.0</td>\n",
       "      <td>12447</td>\n",
       "      <td>3101</td>\n",
       "      <td>96346</td>\n",
       "      <td>0.0516</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.936120</td>\n",
       "      <td>0.364495</td>\n",
       "      <td>0.342540</td>\n",
       "      <td>0.856767</td>\n",
       "      <td>0.493523</td>\n",
       "      <td>0.823824</td>\n",
       "      <td>0.629813</td>\n",
       "      <td>0.454068</td>\n",
       "      <td>0.276923</td>\n",
       "      <td>3</td>\n",
       "      <td>cluster_5</td>\n",
       "      <td>4</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>51963</th>\n",
       "      <td>261.0</td>\n",
       "      <td>12447</td>\n",
       "      <td>3101</td>\n",
       "      <td>96356</td>\n",
       "      <td>0.0040</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.969506</td>\n",
       "      <td>0.418255</td>\n",
       "      <td>0.148014</td>\n",
       "      <td>0.914064</td>\n",
       "      <td>0.335588</td>\n",
       "      <td>0.582583</td>\n",
       "      <td>0.635155</td>\n",
       "      <td>0.475485</td>\n",
       "      <td>0.300000</td>\n",
       "      <td>-1</td>\n",
       "      <td>cluster_5</td>\n",
       "      <td>4</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1005</th>\n",
       "      <td>261.0</td>\n",
       "      <td>54212</td>\n",
       "      <td>3101</td>\n",
       "      <td>96510</td>\n",
       "      <td>-0.1267</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.133282</td>\n",
       "      <td>0.190344</td>\n",
       "      <td>0.113547</td>\n",
       "      <td>0.372372</td>\n",
       "      <td>0.024193</td>\n",
       "      <td>0.381882</td>\n",
       "      <td>0.477577</td>\n",
       "      <td>0.721763</td>\n",
       "      <td>0.338462</td>\n",
       "      <td>-1</td>\n",
       "      <td>cluster_7</td>\n",
       "      <td>-1</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "       propertylandusetypeid regionidcity regionidcounty regionidzip  \\\n",
       "60138                  261.0        33840           1286       96985   \n",
       "79163                  261.0        24245           3101       96475   \n",
       "55204                  261.0        12447           3101       96346   \n",
       "51963                  261.0        12447           3101       96356   \n",
       "1005                   261.0        54212           3101       96510   \n",
       "\n",
       "       logerror  has_pool  is_taxdelinquent  has_garage  lotsizesquarefeet  \\\n",
       "60138   -0.0661       0.0               0.0         1.0           0.088815   \n",
       "79163    0.0237       1.0               0.0         0.0           0.813012   \n",
       "55204    0.0516       1.0               0.0         0.0           0.936120   \n",
       "51963    0.0040       1.0               0.0         0.0           0.969506   \n",
       "1005    -0.1267       0.0               0.0         0.0           0.133282   \n",
       "\n",
       "       structure_dollar_per_sqft  land_dollar_per_sqft  living_area_sqft  \\\n",
       "60138                   0.838465              0.877371          0.824825   \n",
       "79163                   0.752754              0.203305          0.528028   \n",
       "55204                   0.364495              0.342540          0.856767   \n",
       "51963                   0.418255              0.148014          0.914064   \n",
       "1005                    0.190344              0.113547          0.372372   \n",
       "\n",
       "       tax_rate  bedbath_index  latitude  longitude       age  cluster_loc  \\\n",
       "60138  0.927847       0.753253  0.101103   0.948192  0.107692           -1   \n",
       "79163  0.421139       0.136136  0.509108   0.851923  0.269231           -1   \n",
       "55204  0.493523       0.823824  0.629813   0.454068  0.276923            3   \n",
       "51963  0.335588       0.582583  0.635155   0.475485  0.300000           -1   \n",
       "1005   0.024193       0.381882  0.477577   0.721763  0.338462           -1   \n",
       "\n",
       "         cluster  cluster_home  \n",
       "60138  cluster_2            -1  \n",
       "79163  cluster_4            -1  \n",
       "55204  cluster_5             4  \n",
       "51963  cluster_5             4  \n",
       "1005   cluster_7            -1  "
      ]
     },
     "execution_count": 92,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train.head()"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 100,
   "metadata": {},
   "outputs": [],
   "source": [
    "cols_to_remove = ['tax_rate','regionidcity','regionidzip']\n",
    "non_cluster_features = ['lotsizesquarefeet', 'structure_dollar_per_sqft', 'land_dollar_per_sqft',\n",
    "                        'living_area_sqft', 'bedbath_index', 'latitude', 'longitude', 'age']\n",
    "train_no_clusters = train[non_cluster_features+['regionidcounty','logerror']]\n",
    "test_no_clusters = test[non_cluster_features+['regionidcounty','logerror']]"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 101,
   "metadata": {},
   "outputs": [],
   "source": [
    "cols_to_remove = cols_to_remove + non_cluster_features\n",
    "train_clusters = train.drop(columns=cols_to_remove +['cluster'])\n",
    "test_clusters = test.drop(columns=cols_to_remove)"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 102,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>lotsizesquarefeet</th>\n",
       "      <th>structure_dollar_per_sqft</th>\n",
       "      <th>land_dollar_per_sqft</th>\n",
       "      <th>living_area_sqft</th>\n",
       "      <th>bedbath_index</th>\n",
       "      <th>latitude</th>\n",
       "      <th>longitude</th>\n",
       "      <th>age</th>\n",
       "      <th>regionidcounty</th>\n",
       "      <th>logerror</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>60138</th>\n",
       "      <td>0.088815</td>\n",
       "      <td>0.838465</td>\n",
       "      <td>0.877371</td>\n",
       "      <td>0.824825</td>\n",
       "      <td>0.753253</td>\n",
       "      <td>0.101103</td>\n",
       "      <td>0.948192</td>\n",
       "      <td>0.107692</td>\n",
       "      <td>1286</td>\n",
       "      <td>-0.0661</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>79163</th>\n",
       "      <td>0.813012</td>\n",
       "      <td>0.752754</td>\n",
       "      <td>0.203305</td>\n",
       "      <td>0.528028</td>\n",
       "      <td>0.136136</td>\n",
       "      <td>0.509108</td>\n",
       "      <td>0.851923</td>\n",
       "      <td>0.269231</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0237</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>55204</th>\n",
       "      <td>0.936120</td>\n",
       "      <td>0.364495</td>\n",
       "      <td>0.342540</td>\n",
       "      <td>0.856767</td>\n",
       "      <td>0.823824</td>\n",
       "      <td>0.629813</td>\n",
       "      <td>0.454068</td>\n",
       "      <td>0.276923</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0516</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>51963</th>\n",
       "      <td>0.969506</td>\n",
       "      <td>0.418255</td>\n",
       "      <td>0.148014</td>\n",
       "      <td>0.914064</td>\n",
       "      <td>0.582583</td>\n",
       "      <td>0.635155</td>\n",
       "      <td>0.475485</td>\n",
       "      <td>0.300000</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0040</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1005</th>\n",
       "      <td>0.133282</td>\n",
       "      <td>0.190344</td>\n",
       "      <td>0.113547</td>\n",
       "      <td>0.372372</td>\n",
       "      <td>0.381882</td>\n",
       "      <td>0.477577</td>\n",
       "      <td>0.721763</td>\n",
       "      <td>0.338462</td>\n",
       "      <td>3101</td>\n",
       "      <td>-0.1267</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "       lotsizesquarefeet  structure_dollar_per_sqft  land_dollar_per_sqft  \\\n",
       "60138           0.088815                   0.838465              0.877371   \n",
       "79163           0.813012                   0.752754              0.203305   \n",
       "55204           0.936120                   0.364495              0.342540   \n",
       "51963           0.969506                   0.418255              0.148014   \n",
       "1005            0.133282                   0.190344              0.113547   \n",
       "\n",
       "       living_area_sqft  bedbath_index  latitude  longitude       age  \\\n",
       "60138          0.824825       0.753253  0.101103   0.948192  0.107692   \n",
       "79163          0.528028       0.136136  0.509108   0.851923  0.269231   \n",
       "55204          0.856767       0.823824  0.629813   0.454068  0.276923   \n",
       "51963          0.914064       0.582583  0.635155   0.475485  0.300000   \n",
       "1005           0.372372       0.381882  0.477577   0.721763  0.338462   \n",
       "\n",
       "      regionidcounty  logerror  \n",
       "60138           1286   -0.0661  \n",
       "79163           3101    0.0237  \n",
       "55204           3101    0.0516  \n",
       "51963           3101    0.0040  \n",
       "1005            3101   -0.1267  "
      ]
     },
     "execution_count": 102,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train_no_clusters.head()"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 103,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>propertylandusetypeid</th>\n",
       "      <th>regionidcounty</th>\n",
       "      <th>logerror</th>\n",
       "      <th>has_pool</th>\n",
       "      <th>is_taxdelinquent</th>\n",
       "      <th>has_garage</th>\n",
       "      <th>cluster_loc</th>\n",
       "      <th>cluster_home</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>60138</th>\n",
       "      <td>261.0</td>\n",
       "      <td>1286</td>\n",
       "      <td>-0.0661</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>-1</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>79163</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0237</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>-1</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>55204</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0516</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>3</td>\n",
       "      <td>4</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>51963</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0040</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>4</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1005</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>-0.1267</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>-1</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "       propertylandusetypeid regionidcounty  logerror  has_pool  \\\n",
       "60138                  261.0           1286   -0.0661       0.0   \n",
       "79163                  261.0           3101    0.0237       1.0   \n",
       "55204                  261.0           3101    0.0516       1.0   \n",
       "51963                  261.0           3101    0.0040       1.0   \n",
       "1005                   261.0           3101   -0.1267       0.0   \n",
       "\n",
       "       is_taxdelinquent  has_garage  cluster_loc  cluster_home  \n",
       "60138               0.0         1.0           -1            -1  \n",
       "79163               0.0         0.0           -1            -1  \n",
       "55204               0.0         0.0            3             4  \n",
       "51963               0.0         0.0           -1             4  \n",
       "1005                0.0         0.0           -1            -1  "
      ]
     },
     "execution_count": 103,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train_clusters.head()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### Encode\n",
    "\n",
    "Which columns are of numeric format but represent classes or categories?\n",
    "fips\n",
    "rawcensustractandblock\n",
    "regionidcity\n",
    "regionidcounty\n",
    "regionidzip\n"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 104,
   "metadata": {},
   "outputs": [],
   "source": [
    "def encode(train, test, col_name):\n",
    "  \n",
    "    encoded_values = sorted(list(train[col_name].unique()))\n",
    "    columns = [col_name + '_' + str(val) for val in encoded_values]\n",
    "\n",
    "    # Integer Encoding\n",
    "    int_encoder = LabelEncoder()\n",
    "    train.encoded = int_encoder.fit_transform(train[col_name])\n",
    "    test.encoded = int_encoder.transform(test[col_name])\n",
    "\n",
    "    # create 2D np arrays of the encoded variable (in train and test)\n",
    "    train_array = np.array(train.encoded).reshape(len(train.encoded),1)\n",
    "    test_array = np.array(test.encoded).reshape(len(test.encoded),1)\n",
    "    \n",
    "    # One Hot Encoding\n",
    "    ohe = OneHotEncoder(sparse=False, categories='auto')\n",
    "    train_ohe = ohe.fit_transform(train_array)\n",
    "    test_ohe = ohe.transform(test_array)\n",
    "\n",
    "    # Turn the array of new values into a data frame with columns names being the values\n",
    "    # and index matching that of train/test\n",
    "    # then merge the new dataframe with the existing train/test dataframe\n",
    "    train_encoded = pd.DataFrame(data=train_ohe,\n",
    "                            columns=columns, index=train.index)\n",
    "    train = train.join(train_encoded)\n",
    "\n",
    "    test_encoded = pd.DataFrame(data=test_ohe,\n",
    "                               columns=columns, index=test.index)\n",
    "    test = test.join(test_encoded)\n",
    "\n",
    "    return train, test, int_encoder, ohe\n",
    "\n",
    "def one_hot_encode(train, test, col_name):\n",
    "  \n",
    "    encoded_values = sorted(list(train[col_name].unique()))\n",
    "    columns = [col_name + '_' + str(val) for val in encoded_values]\n",
    "\n",
    "    # create 2D np arrays of the encoded variable (in train and test)\n",
    "    train_array = np.array(train[col_name]).reshape(len(train[col_name]),1)\n",
    "    test_array = np.array(test[col_name]).reshape(len(test[col_name]),1)\n",
    "    \n",
    "    # One Hot Encoding\n",
    "    ohe = OneHotEncoder(sparse=False, categories='auto')\n",
    "    train_ohe = ohe.fit_transform(train_array)\n",
    "    test_ohe = ohe.transform(test_array)\n",
    "\n",
    "    # Turn the array of new values into a data frame with columns names being the values\n",
    "    # and index matching that of train/test\n",
    "    # then merge the new dataframe with the existing train/test dataframe\n",
    "    train_encoded = pd.DataFrame(data=train_ohe,\n",
    "                            columns=columns, index=train.index)\n",
    "    train = train.join(train_encoded)\n",
    "\n",
    "    test_encoded = pd.DataFrame(data=test_ohe,\n",
    "                               columns=columns, index=test.index)\n",
    "    test = test.join(test_encoded)\n",
    "\n",
    "    return train, test, ohe"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 105,
   "metadata": {},
   "outputs": [],
   "source": [
    "train_clusters, test_clusters, ohe_loc = one_hot_encode(train_clusters, test_clusters, 'cluster_loc')\n",
    "train_clusters, test_clusters, ohe_home = one_hot_encode(train_clusters, test_clusters, 'cluster_home')"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 108,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>propertylandusetypeid</th>\n",
       "      <th>regionidcounty</th>\n",
       "      <th>logerror</th>\n",
       "      <th>has_pool</th>\n",
       "      <th>is_taxdelinquent</th>\n",
       "      <th>has_garage</th>\n",
       "      <th>cluster_loc</th>\n",
       "      <th>cluster_home</th>\n",
       "      <th>cluster_loc_-1</th>\n",
       "      <th>cluster_loc_3</th>\n",
       "      <th>cluster_loc_6</th>\n",
       "      <th>cluster_home_-1</th>\n",
       "      <th>cluster_home_0</th>\n",
       "      <th>cluster_home_2</th>\n",
       "      <th>cluster_home_4</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>60138</th>\n",
       "      <td>261.0</td>\n",
       "      <td>1286</td>\n",
       "      <td>-0.0661</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>-1</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>79163</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0237</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>-1</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>55204</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0516</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>3</td>\n",
       "      <td>4</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>51963</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>0.0040</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>4</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1005</th>\n",
       "      <td>261.0</td>\n",
       "      <td>3101</td>\n",
       "      <td>-0.1267</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>-1</td>\n",
       "      <td>-1</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "       propertylandusetypeid regionidcounty  logerror  has_pool  \\\n",
       "60138                  261.0           1286   -0.0661       0.0   \n",
       "79163                  261.0           3101    0.0237       1.0   \n",
       "55204                  261.0           3101    0.0516       1.0   \n",
       "51963                  261.0           3101    0.0040       1.0   \n",
       "1005                   261.0           3101   -0.1267       0.0   \n",
       "\n",
       "       is_taxdelinquent  has_garage  cluster_loc  cluster_home  \\\n",
       "60138               0.0         1.0           -1            -1   \n",
       "79163               0.0         0.0           -1            -1   \n",
       "55204               0.0         0.0            3             4   \n",
       "51963               0.0         0.0           -1             4   \n",
       "1005                0.0         0.0           -1            -1   \n",
       "\n",
       "       cluster_loc_-1  cluster_loc_3  cluster_loc_6  cluster_home_-1  \\\n",
       "60138             1.0            0.0            0.0              1.0   \n",
       "79163             1.0            0.0            0.0              1.0   \n",
       "55204             0.0            1.0            0.0              0.0   \n",
       "51963             1.0            0.0            0.0              0.0   \n",
       "1005              1.0            0.0            0.0              1.0   \n",
       "\n",
       "       cluster_home_0  cluster_home_2  cluster_home_4  \n",
       "60138             0.0             0.0             0.0  \n",
       "79163             0.0             0.0             0.0  \n",
       "55204             0.0             0.0             1.0  \n",
       "51963             0.0             0.0             1.0  \n",
       "1005              0.0             0.0             0.0  "
      ]
     },
     "execution_count": 108,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train_clusters.head()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Build 3 models, 1 for each county\n",
    "Try with clusters and then try with original features"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 106,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "3101    26231\n",
       "1286    11178\n",
       "2061     3484\n",
       "Name: regionidcounty, dtype: int64"
      ]
     },
     "execution_count": 106,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "train_clusters.regionidcounty.value_counts()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Separate the clusters dataframes by county"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 109,
   "metadata": {},
   "outputs": [],
   "source": [
    "train_3101_c = train_clusters[train_clusters.regionidcounty=='3101']\n",
    "test_3101_c = test_clusters[test_clusters.regionidcounty=='3101']\n",
    "\n",
    "train_1286_c = train_clusters[train_clusters.regionidcounty=='1286']\n",
    "test_1286_c = test_clusters[test_clusters.regionidcounty=='1286']\n",
    "\n",
    "train_2061_c = train_clusters[train_clusters.regionidcounty=='2061']\n",
    "test_2061_c = test_clusters[test_clusters.regionidcounty=='2061']"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Separate the non-clusters dataframes by county"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 110,
   "metadata": {},
   "outputs": [],
   "source": [
    "train_3101_nc = train_no_clusters[train_no_clusters.regionidcounty=='3101']\n",
    "test_3101_nc = test_no_clusters[test_no_clusters.regionidcounty=='3101']\n",
    "\n",
    "train_1286_nc = train_no_clusters[train_no_clusters.regionidcounty=='1286']\n",
    "test_1286_nc = test_no_clusters[test_no_clusters.regionidcounty=='1286']\n",
    "\n",
    "train_2061_nc = train_no_clusters[train_no_clusters.regionidcounty=='2061']\n",
    "test_2061_nc = test_no_clusters[test_no_clusters.regionidcounty=='2061']"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "Now that we have encoded and split by county, we can remove some other columns to have our final X with features.\n",
    "We only need a y_train and y_test for each county, not separated by the features, obviously. \n",
    "\n",
    "X dataframes for the cluster features:"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 111,
   "metadata": {},
   "outputs": [],
   "source": [
    "cols_to_drop = ['cluster_loc', 'cluster_home', 'cluster_loc_-1', 'cluster_home_-1', 'logerror', 'regionidcounty']\n",
    "\n",
    "X_train_3101_c = train_3101_c.drop(columns=cols_to_drop)\n",
    "X_test_3101_c = test_3101_c.drop(columns=cols_to_drop)\n",
    "\n",
    "X_train_1286_c = train_1286_c.drop(columns=cols_to_drop)\n",
    "X_test_1286_c = test_1286_c.drop(columns=cols_to_drop)\n",
    "\n",
    "X_train_2061_c = train_2061_c.drop(columns=cols_to_drop)\n",
    "X_test_2061_c = test_2061_c.drop(columns=cols_to_drop)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "X dataframes for the non-cluster features"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 112,
   "metadata": {},
   "outputs": [],
   "source": [
    "cols_to_drop = ['logerror', 'regionidcounty']\n",
    "\n",
    "X_train_3101_nc = train_3101_nc.drop(columns=cols_to_drop)\n",
    "X_test_3101_nc = test_3101_nc.drop(columns=cols_to_drop)\n",
    "\n",
    "X_train_1286_nc = train_1286_nc.drop(columns=cols_to_drop)\n",
    "X_test_1286_nc = test_1286_nc.drop(columns=cols_to_drop)\n",
    "\n",
    "X_train_2061_nc = train_2061_nc.drop(columns=cols_to_drop)\n",
    "X_test_2061_nc = test_2061_nc.drop(columns=cols_to_drop)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "y dataframes"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 113,
   "metadata": {},
   "outputs": [],
   "source": [
    "y_train_3101 = train_3101_c[['logerror']]\n",
    "y_test_3101 = test_3101_c[['logerror']]\n",
    "\n",
    "y_train_1286 = train_1286_c[['logerror']]\n",
    "y_test_1286 = test_1286_c[['logerror']]\n",
    "\n",
    "y_train_2061 = train_2061_c[['logerror']]\n",
    "y_test_2061 = test_2061_c[['logerror']]"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "## Model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 114,
   "metadata": {},
   "outputs": [],
   "source": [
    "from sklearn.svm import LinearSVR\n",
    "from sklearn.metrics import mean_squared_error\n",
    "from sklearn.linear_model import SGDRegressor, LassoCV\n",
    "from sklearn.tree import DecisionTreeRegressor"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### county: 3101\n",
    "\n",
    "#### Baseline"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 115,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.015616308566009774"
      ]
     },
     "execution_count": 115,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "se = y_train_3101.logerror * y_train_3101.logerror\n",
    "mse = se.mean()\n",
    "rmse = mse**1/2\n",
    "rmse"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### Clustering Features\n",
    "\n",
    "##### Linear Support Vector Regressor from sklearn.svm"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 116,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.015489162214499188\n"
     ]
    }
   ],
   "source": [
    "regr = LinearSVR(random_state=123, tol=1e-5, loss='squared_epsilon_insensitive', fit_intercept=False, dual=False)\n",
    "regr.fit(X_train_3101_c, y_train_3101)\n",
    "y_pred_3101 = regr.predict(X_train_3101_c)\n",
    "print(mean_squared_error(y_train_3101, y_pred_3101)**1/2)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Support Gradient Descent Regressor from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 117,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "3.717404672789985e+25"
      ]
     },
     "execution_count": 117,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "sgd = SGDRegressor(fit_intercept=False, max_iter=1000, random_state=123)\n",
    "sgd.fit(X_train_3101_c, y_train_3101)\n",
    "y_pred_3101 = sgd.predict(X_train_3101_c)\n",
    "mean_squared_error(y_train_3101, y_pred_3101)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Lasso with Cross Validation from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 118,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.01555953314441975"
      ]
     },
     "execution_count": 118,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "lasso = LassoCV(fit_intercept=False)\n",
    "lasso.fit(X_train_3101_c, y_train_3101)\n",
    "y_pred_3101 = lasso.predict(X_train_3101_c)\n",
    "mean_squared_error(y_train_3101, y_pred_3101)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Decision Tree Regressor from sklearn.tree"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 119,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.015461315422835164"
      ]
     },
     "execution_count": 119,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "dt = DecisionTreeRegressor(random_state=123)\n",
    "dt.fit(X_train_3101_c, y_train_3101)\n",
    "y_pred_3101 = dt.predict(X_train_3101_c)\n",
    "mean_squared_error(y_train_3101, y_pred_3101)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### non-clustering features\n",
    "\n",
    "##### Linear Support Vector Regressor from sklearn.svm"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 120,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.015504380239976105\n"
     ]
    }
   ],
   "source": [
    "regr = LinearSVR(random_state=123, tol=1e-5, loss='squared_epsilon_insensitive', fit_intercept=False, dual=False)\n",
    "regr.fit(X_train_3101_nc, y_train_3101)\n",
    "y_pred_3101 = regr.predict(X_train_3101_nc)\n",
    "print(mean_squared_error(y_train_3101, y_pred_3101)**1/2)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Support Gradient Descent Regressor from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 121,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.015505018714097377"
      ]
     },
     "execution_count": 121,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "sgd = SGDRegressor(fit_intercept=False, max_iter=1000, random_state=123)\n",
    "sgd.fit(X_train_3101_nc, y_train_3101)\n",
    "y_pred_3101 = sgd.predict(X_train_3101_nc)\n",
    "mean_squared_error(y_train_3101, y_pred_3101)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Lasso with Cross Validation from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 122,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.015504658509163846"
      ]
     },
     "execution_count": 122,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "lasso = LassoCV(fit_intercept=False)\n",
    "lasso.fit(X_train_3101_nc, y_train_3101)\n",
    "y_pred_3101 = lasso.predict(X_train_3101_nc)\n",
    "mean_squared_error(y_train_3101, y_pred_3101)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Decision Tree Regressor from sklearn.tree"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 125,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.013023397328485928"
      ]
     },
     "execution_count": 125,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "dt = DecisionTreeRegressor(max_depth = 10, random_state=123)\n",
    "dt.fit(X_train_3101_nc, y_train_3101)\n",
    "y_pred_3101 = dt.predict(X_train_3101_nc)\n",
    "mean_squared_error(y_train_3101, y_pred_3101)**1/2"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": []
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "WOW!!!"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 124,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/html": [
       "<div>\n",
       "<style scoped>\n",
       "    .dataframe tbody tr th:only-of-type {\n",
       "        vertical-align: middle;\n",
       "    }\n",
       "\n",
       "    .dataframe tbody tr th {\n",
       "        vertical-align: top;\n",
       "    }\n",
       "\n",
       "    .dataframe thead th {\n",
       "        text-align: right;\n",
       "    }\n",
       "</style>\n",
       "<table border=\"1\" class=\"dataframe\">\n",
       "  <thead>\n",
       "    <tr style=\"text-align: right;\">\n",
       "      <th></th>\n",
       "      <th>propertylandusetypeid</th>\n",
       "      <th>has_pool</th>\n",
       "      <th>is_taxdelinquent</th>\n",
       "      <th>has_garage</th>\n",
       "      <th>cluster_loc_3</th>\n",
       "      <th>cluster_loc_6</th>\n",
       "      <th>cluster_home_0</th>\n",
       "      <th>cluster_home_2</th>\n",
       "      <th>cluster_home_4</th>\n",
       "    </tr>\n",
       "  </thead>\n",
       "  <tbody>\n",
       "    <tr>\n",
       "      <th>79163</th>\n",
       "      <td>261.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>55204</th>\n",
       "      <td>261.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>51963</th>\n",
       "      <td>261.0</td>\n",
       "      <td>1.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>1.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>1005</th>\n",
       "      <td>261.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "    </tr>\n",
       "    <tr>\n",
       "      <th>24947</th>\n",
       "      <td>261.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "      <td>0.0</td>\n",
       "    </tr>\n",
       "  </tbody>\n",
       "</table>\n",
       "</div>"
      ],
      "text/plain": [
       "       propertylandusetypeid  has_pool  is_taxdelinquent  has_garage  \\\n",
       "79163                  261.0       1.0               0.0         0.0   \n",
       "55204                  261.0       1.0               0.0         0.0   \n",
       "51963                  261.0       1.0               0.0         0.0   \n",
       "1005                   261.0       0.0               0.0         0.0   \n",
       "24947                  261.0       0.0               0.0         0.0   \n",
       "\n",
       "       cluster_loc_3  cluster_loc_6  cluster_home_0  cluster_home_2  \\\n",
       "79163            0.0            0.0             0.0             0.0   \n",
       "55204            1.0            0.0             0.0             0.0   \n",
       "51963            0.0            0.0             0.0             0.0   \n",
       "1005             0.0            0.0             0.0             0.0   \n",
       "24947            0.0            0.0             0.0             0.0   \n",
       "\n",
       "       cluster_home_4  \n",
       "79163             0.0  \n",
       "55204             1.0  \n",
       "51963             1.0  \n",
       "1005              0.0  \n",
       "24947             0.0  "
      ]
     },
     "execution_count": 124,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "X_train_3101_c.head()"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "WOW!!!"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### county: 1286\n",
    "\n",
    "#### Baseline"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 126,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.009542069100017769"
      ]
     },
     "execution_count": 126,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "se = y_train_1286.logerror * y_train_1286.logerror\n",
    "mse = se.mean()\n",
    "rmse = mse**1/2\n",
    "rmse"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### Clustering Features\n",
    "\n",
    "##### Linear Support Vector Regressor from sklearn.svm"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 127,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.00940222305823838\n"
     ]
    }
   ],
   "source": [
    "regr = LinearSVR(random_state=123, tol=1e-5, loss='squared_epsilon_insensitive', fit_intercept=False, dual=False)\n",
    "regr.fit(X_train_1286_c, y_train_1286)\n",
    "y_pred_1286 = regr.predict(X_train_1286_c)\n",
    "print(mean_squared_error(y_train_1286, y_pred_1286)**1/2)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Support Gradient Descent Regressor from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 128,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "5.916918568168517e+25"
      ]
     },
     "execution_count": 128,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "sgd = SGDRegressor(fit_intercept=False, max_iter=1000, random_state=123)\n",
    "sgd.fit(X_train_1286_c, y_train_1286)\n",
    "y_pred_1286 = sgd.predict(X_train_1286_c)\n",
    "mean_squared_error(y_train_1286, y_pred_1286)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Lasso with Cross Validation from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 129,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.009443797727671469"
      ]
     },
     "execution_count": 129,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "lasso = LassoCV(fit_intercept=False)\n",
    "lasso.fit(X_train_1286_c, y_train_1286)\n",
    "y_pred_1286 = lasso.predict(X_train_1286_c)\n",
    "mean_squared_error(y_train_1286, y_pred_1286)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Decision Tree Regressor from sklearn.tree"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 130,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.00934710682384211"
      ]
     },
     "execution_count": 130,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "dt = DecisionTreeRegressor(random_state=123)\n",
    "dt.fit(X_train_1286_c, y_train_1286)\n",
    "y_pred_1286 = dt.predict(X_train_1286_c)\n",
    "mean_squared_error(y_train_1286, y_pred_1286)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### non-clustering features\n",
    "\n",
    "##### Linear Support Vector Regressor from sklearn.svm"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 131,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.009437521183568102\n"
     ]
    }
   ],
   "source": [
    "regr = LinearSVR(random_state=123, tol=1e-5, loss='squared_epsilon_insensitive', fit_intercept=False, dual=False)\n",
    "regr.fit(X_train_1286_nc, y_train_1286)\n",
    "y_pred_1286 = regr.predict(X_train_1286_nc)\n",
    "print(mean_squared_error(y_train_1286, y_pred_1286)**1/2)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Support Gradient Descent Regressor from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 132,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.009437521183568102"
      ]
     },
     "execution_count": 132,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "sgd = SGDRegressor(fit_intercept=False, max_iter=1000, random_state=123)\n",
    "sgd.fit(X_train_1286_nc, y_train_1286)\n",
    "y_pred_3101 = sgd.predict(X_train_1286_nc)\n",
    "mean_squared_error(y_train_1286, y_pred_1286)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Lasso with Cross Validation from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 133,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.009443116701874072"
      ]
     },
     "execution_count": 133,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "lasso = LassoCV(fit_intercept=False)\n",
    "lasso.fit(X_train_1286_nc, y_train_1286)\n",
    "y_pred_1286 = lasso.predict(X_train_1286_nc)\n",
    "mean_squared_error(y_train_1286, y_pred_1286)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Decision Tree Regressor from sklearn.tree"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 135,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.007329577412422474"
      ]
     },
     "execution_count": 135,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "dt = DecisionTreeRegressor(max_depth = 10, random_state=123)\n",
    "dt.fit(X_train_1286_nc, y_train_1286)\n",
    "y_pred_1286 = dt.predict(X_train_1286_nc)\n",
    "mean_squared_error(y_train_1286, y_pred_1286)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "WOW again!"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": []
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "### county: 2061\n",
    "\n",
    "#### Baseline"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 136,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.01494234337399539"
      ]
     },
     "execution_count": 136,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "se = y_train_2061.logerror * y_train_2061.logerror\n",
    "mse = se.mean()\n",
    "rmse = mse**1/2\n",
    "rmse"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### Clustering Features\n",
    "\n",
    "##### Linear Support Vector Regressor from sklearn.svm"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 137,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.014727491536770316\n"
     ]
    }
   ],
   "source": [
    "regr = LinearSVR(random_state=123, tol=1e-5, loss='squared_epsilon_insensitive', fit_intercept=False, dual=False)\n",
    "regr.fit(X_train_2061_c, y_train_2061)\n",
    "y_pred_2061 = regr.predict(X_train_2061_c)\n",
    "print(mean_squared_error(y_train_2061, y_pred_2061)**1/2)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Support Gradient Descent Regressor from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 138,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "1.0228063002211821e+24"
      ]
     },
     "execution_count": 138,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "sgd = SGDRegressor(fit_intercept=False, max_iter=1000, random_state=123)\n",
    "sgd.fit(X_train_2061_c, y_train_2061)\n",
    "y_pred_2061 = sgd.predict(X_train_2061_c)\n",
    "mean_squared_error(y_train_2061, y_pred_2061)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Lasso with Cross Validation from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 139,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.01479298787530697"
      ]
     },
     "execution_count": 139,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "lasso = LassoCV(fit_intercept=False)\n",
    "lasso.fit(X_train_2061_c, y_train_2061)\n",
    "y_pred_2061 = lasso.predict(X_train_2061_c)\n",
    "mean_squared_error(y_train_2061, y_pred_2061)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Decision Tree Regressor from sklearn.tree"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 140,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.014651281735142505"
      ]
     },
     "execution_count": 140,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "dt = DecisionTreeRegressor(random_state=123)\n",
    "dt.fit(X_train_2061_c, y_train_2061)\n",
    "y_pred_2061 = dt.predict(X_train_2061_c)\n",
    "mean_squared_error(y_train_2061, y_pred_2061)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "#### non-clustering features\n",
    "\n",
    "##### Linear Support Vector Regressor from sklearn.svm"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 141,
   "metadata": {},
   "outputs": [
    {
     "name": "stdout",
     "output_type": "stream",
     "text": [
      "0.01468169897402531\n"
     ]
    }
   ],
   "source": [
    "regr = LinearSVR(random_state=123, tol=1e-5, loss='squared_epsilon_insensitive', fit_intercept=False, dual=False)\n",
    "regr.fit(X_train_2061_nc, y_train_2061)\n",
    "y_pred_2061 = regr.predict(X_train_2061_nc)\n",
    "print(mean_squared_error(y_train_2061, y_pred_2061)**1/2)"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Support Gradient Descent Regressor from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 142,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.014699828590248962"
      ]
     },
     "execution_count": 142,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "sgd = SGDRegressor(fit_intercept=False, max_iter=1000, random_state=123)\n",
    "sgd.fit(X_train_2061_nc, y_train_2061)\n",
    "y_pred_2061 = sgd.predict(X_train_2061_nc)\n",
    "mean_squared_error(y_train_2061, y_pred_2061)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Lasso with Cross Validation from sklearn.linear_model"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 143,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.014703037273089121"
      ]
     },
     "execution_count": 143,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "lasso = LassoCV(fit_intercept=False)\n",
    "lasso.fit(X_train_2061_nc, y_train_2061)\n",
    "y_pred_2061 = lasso.predict(X_train_2061_nc)\n",
    "mean_squared_error(y_train_2061, y_pred_2061)**1/2"
   ]
  },
  {
   "cell_type": "markdown",
   "metadata": {},
   "source": [
    "##### Decision Tree Regressor from sklearn.tree"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": 145,
   "metadata": {},
   "outputs": [
    {
     "data": {
      "text/plain": [
       "0.007493248732462352"
      ]
     },
     "execution_count": 145,
     "metadata": {},
     "output_type": "execute_result"
    }
   ],
   "source": [
    "dt = DecisionTreeRegressor(max_depth = 10, random_state=123)\n",
    "dt.fit(X_train_2061_nc, y_train_2061)\n",
    "y_pred_2061 = dt.predict(X_train_2061_nc)\n",
    "mean_squared_error(y_train_2061, y_pred_2061)**1/2"
   ]
  },
  {
   "cell_type": "code",
   "execution_count": null,
   "metadata": {},
   "outputs": [],
   "source": []
  }
 ],
 "metadata": {
  "kernelspec": {
   "display_name": "Python 3",
   "language": "python",
   "name": "python3"
  },
  "language_info": {
   "codemirror_mode": {
    "name": "ipython",
    "version": 3
   },
   "file_extension": ".py",
   "mimetype": "text/x-python",
   "name": "python",
   "nbconvert_exporter": "python",
   "pygments_lexer": "ipython3",
   "version": "3.7.3"
  }
 },
 "nbformat": 4,
 "nbformat_minor": 2
}


NameError: name 'null' is not defined